<a href="https://colab.research.google.com/github/Ryong1998/house_price/blob/main/apartment_project.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# 프로젝트 주제

- 해당 프로젝트는 미래의 '서울 아파트 매매가격지수'를 예측하는 프로젝트 입니다

# 프로젝트 소개

- 다양한 지역의 다양한 부동산의 종류(아파트, 단독주택 등)들 중 '서울'의 '아파트'로 부동산 종류를 한정
- 최종적으로는 향후 1년간 서울 아파트 시장의 동향을 예측하고, 아파트를 구매하려는 소비자들에게 도움이 되는 지표를 제공하고자 함
- 부동산의 가치는 '1. 거주지로서의 특성'과 '2. 금융상품으로서의 특성' 두가지를 통해서 평가를 할 수 있다고 가정
- '1. 거주지로서의 특성'은 주변 편의시설, 교육시설, 아파트 평수, 주변 교통시설 등 더 편한 거주환경을 제공하는 요소들을 포함
- '2. 금융상품으로서의 특성'은 기준금리, 아파트 공급량, 아파트 미분양, 현재 매매가, 전세가율 등 금융관련 수치들로 표현이 되는 요소들을 포함
- '1. 거주지로서의 특성'에서 높은 가치를 의미하는 요소들은 시대가 변함에 따라서 바뀔 수가 있음(예를 들어 대가족에서 소가족 형태로 가족 구성원 구조가 바뀌면서 시대에 따라 사람들이 선호하는 아파트 평수가 바뀔 수도 있고, 인터넷 강의의 발달로 인해서 교육시설 인프라의 중요성이 향후 낮아질 수 있음)
- '1. 거주지로서의 특성'에서 높은 가치들은 과거 계속 변화했을 수 있지만 어떻게 변했는지 파악하기가 쉽지 않고, 미래에 어떻게 변할지 알 수 없기에 평가의 기준이 '변동적'이라는 특징이 있음
- 하지만 '2. 금융상품으로서의 특성'은 가격과 경제를 바탕으로 한 '수치'들을 표현 하기에 '1. 거주지로서의 특성'보다 일관성 있게 부동산의 가치를 평가할 수 있을거라는 가정
- '2. 금융상품으로서의 특성'에 해당하는 수치들은 그 자체로 변화하는 '1. 거주지로서의 특성'의 가치를 내포하고 있다고 가정
- 해당 프로젝트는 '2. 금융상품으로서의 특성'에 집중하여서 집값의 변화를 예측 할 예정
- 일별로 '1년뒤 서울 아파트 매매가격지수'를 예측하는 모델을 생성하여 진행
- 개별 아파트를 추천하지는 못하더라도, 서울 아파트 시장의 1년뒤 전망을 통해 현재 아파트를 살 타이밍인지 아닌지를 예측하는 프로젝트를 진행

In [2]:
# 구글 드라이브 마운트
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


# original_data 확보

- 'http://rtdown.molit.go.kr/' 사이트를 통해서 아파트매매가, 아파트 전/월세 가격 정보 파일로 얻음
- 'https://kr.investing.com/' 사이트를 통해서 한국국채금리, 미국국채금리, 코스피 정보를 얻음
- 'https://data.kbland.kr/publicdata/housing-supply' 사이트를 통해서 아파트 공급량 정보를 얻음
- 'https://data.kbland.kr/publicdata/unsold-apartments' 사이트를 통해서 미분양 아파트 정보를 얻음
- 'https://www.bok.or.kr/portal/singl/baseRate/list.do?dataSeCd=01&menuNo=200643' 사이트를 통해서 기준금리 정보를 얻음
- 'https://data.kbland.kr/kbstats/wmh?tIdx=HT01&tsIdx=weekAptSalePriceInx' 사이트를 통해서 주간 서울시 주택가격지수를 얻음



>> 공공데이터포털의 api를 이용해서 아파트매매가, 아파트 전/월세 가격 정보를 얻으려 했지만 일일 트래픽 제한으로 인해서 직접 'http://rtdown.molit.go.kr/' 사이트에 접속해서 파일들을 다운 받아 필요 데이터를 확보

# apartment_deal.csv 파일 생성

- 'http://rtdown.molit.go.kr/' 사이트를 통해서 아파트매매가 정보 파일들을 얻음
- '아파트 매매' 관련 정보들을 가지고 있는 데이터프레임을 생성하여 apartment_deal.csv 로 저장

## csv 파일들 불러오기 및 병합

- 아파트 매매 정보 원본본파일들은 연도별로 파일들이 나누어져 되어있고, 각 csv 파일 내의 모든 정보들이 필요하지는 않기에 전처리 과정 진행

In [ ]:
import pandas as pd
import os

# 연도별 아파트 매매 정보들이 들어있는 csv경로 설정
dir_path = "/content/drive/MyDrive/house_price/original_data/deal_price/Seoul"
file_list = os.listdir(dir_path)
file_list.sort()
df_list = list()
# 해당 폴더 안에 있는 csv 파일들을 읽어서 리스트 안에 데이터프레임들을 담음
for csv_file in file_list:
    df_list.append(pd.read_csv(dir_path+"/"+csv_file ,skiprows=15,  encoding='cp949'))

>> 코랩은 파일을 읽어올 때 업로드한 순서대로 파일을 불러오는 듯

In [ ]:
df_list[0].info() # 리스트 안에 잘 담겼는지 확인

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 120812 entries, 0 to 120811
Data columns (total 15 columns):
 #   Column    Non-Null Count   Dtype  
---  ------    --------------   -----  
 0   시군구       120812 non-null  object 
 1   번지        120812 non-null  object 
 2   본번        120812 non-null  int64  
 3   부번        120812 non-null  int64  
 4   단지명       120812 non-null  object 
 5   전용면적(㎡)   120812 non-null  float64
 6   계약년월      120812 non-null  int64  
 7   계약일       120812 non-null  int64  
 8   거래금액(만원)  120812 non-null  object 
 9   층         120812 non-null  int64  
 10  건축년도      120812 non-null  int64  
 11  도로명       120812 non-null  object 
 12  해제사유발생일   0 non-null       float64
 13  거래유형      120812 non-null  object 
 14  중개사소재지    120812 non-null  object 
dtypes: float64(2), int64(6), object(7)
memory usage: 13.8+ MB


In [ ]:
df_list[0].head() # 데이터 형태들을 확인

시군구     번지   본번  부번             단지명  전용면적(㎡)    계약년월  계약일  \
0  서울특별시 강남구 개포동  655-2  655   2  개포2차현대아파트(220)    77.75  200603   10   
1  서울특별시 강남구 개포동  655-2  655   2  개포2차현대아파트(220)    77.75  200603   29   
2  서울특별시 강남구 개포동  655-2  655   2  개포2차현대아파트(220)    77.75  200604   29   
3  서울특별시 강남구 개포동  655-2  655   2  개포2차현대아파트(220)    77.75  200606    1   
4  서울특별시 강남구 개포동  655-2  655   2  개포2차현대아파트(220)    77.75  200610   20   

  거래금액(만원)  층  건축년도      도로명  해제사유발생일 거래유형 중개사소재지  
0   59,500  7  1988  언주로 103      NaN    -      -  
1   60,000  6  1988  언주로 103      NaN    -      -  
2   67,000  9  1988  언주로 103      NaN    -      -  
3   60,000  4  1988  언주로 103      NaN    -      -  
4   72,250  5  1988  언주로 103      NaN    -      -

In [ ]:
# 모든 데이터프레임을 하나의 데이터프레임으로 통합
df_default = df_list[0]
for df_csv in df_list[1:]:
    df_default = pd.concat([df_default, df_csv], axis=0) # concat을 통해서 위-아래로 데이터 프레임들을 병합
df_default.reset_index(drop=True, inplace=True) # concat으로 합쳐질 때 인덱스 재설정
df_default.loc[1]

시군구          서울특별시 강남구 개포동
번지                   655-2
본번                   655.0
부번                     2.0
단지명         개포2차현대아파트(220)
전용면적(㎡)              77.75
계약년월                200603
계약일                     29
거래금액(만원)            60,000
층                        6
건축년도                1988.0
도로명                언주로 103
해제사유발생일                NaN
거래유형                     -
중개사소재지                   -
등기신청일자                 NaN
Name: 1, dtype: object

In [ ]:
df_default.head() # 병합한 테이블의 정보 파악

시군구     번지     본번   부번             단지명  전용면적(㎡)    계약년월  계약일  \
0  서울특별시 강남구 개포동  655-2  655.0  2.0  개포2차현대아파트(220)    77.75  200603   10   
1  서울특별시 강남구 개포동  655-2  655.0  2.0  개포2차현대아파트(220)    77.75  200603   29   
2  서울특별시 강남구 개포동  655-2  655.0  2.0  개포2차현대아파트(220)    77.75  200604   29   
3  서울특별시 강남구 개포동  655-2  655.0  2.0  개포2차현대아파트(220)    77.75  200606    1   
4  서울특별시 강남구 개포동  655-2  655.0  2.0  개포2차현대아파트(220)    77.75  200610   20   

  거래금액(만원)  층    건축년도      도로명  해제사유발생일 거래유형 중개사소재지 등기신청일자  
0   59,500  7  1988.0  언주로 103      NaN    -      -    NaN  
1   60,000  6  1988.0  언주로 103      NaN    -      -    NaN  
2   67,000  9  1988.0  언주로 103      NaN    -      -    NaN  
3   60,000  4  1988.0  언주로 103      NaN    -      -    NaN  
4   72,250  5  1988.0  언주로 103      NaN    -      -    NaN

In [ ]:
df_default.info() # 데이터프레임 합친 결과 확인

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1268633 entries, 0 to 1268632
Data columns (total 16 columns):
 #   Column    Non-Null Count    Dtype  
---  ------    --------------    -----  
 0   시군구       1268633 non-null  object 
 1   번지        1268408 non-null  object 
 2   본번        1268554 non-null  float64
 3   부번        1268554 non-null  float64
 4   단지명       1268633 non-null  object 
 5   전용면적(㎡)   1268633 non-null  float64
 6   계약년월      1268633 non-null  int64  
 7   계약일       1268633 non-null  int64  
 8   거래금액(만원)  1268633 non-null  object 
 9   층         1268633 non-null  int64  
 10  건축년도      1268631 non-null  float64
 11  도로명       1268633 non-null  object 
 12  해제사유발생일   6336 non-null     float64
 13  거래유형      1268633 non-null  object 
 14  중개사소재지    1268633 non-null  object 
 15  등기신청일자    31142 non-null    object 
dtypes: float64(5), int64(3), object(8)
memory usage: 154.9+ MB


## 필요한 컬럼만 선택

- df_default 데이터프레임에서 모든 컬럼들을 사용하지 않기에, 사용할 컬럼들만을 선택

In [ ]:
# 사용할 컬럼들만 거르고 컬럼명 영어로 치환 - 필요한 컬럼들만 선택
df_default = df_default[['시군구','본번','부번','도로명','단지명','계약년월','계약일','전용면적(㎡)','거래금액(만원)']]
df_default.columns = ['address','main_number','sub_number','road','name','year_month','day','area','deal_price']
df_default.head() # 잘 걸러졌는지 확인

address  main_number  sub_number     road            name  \
0  서울특별시 강남구 개포동        655.0         2.0  언주로 103  개포2차현대아파트(220)   
1  서울특별시 강남구 개포동        655.0         2.0  언주로 103  개포2차현대아파트(220)   
2  서울특별시 강남구 개포동        655.0         2.0  언주로 103  개포2차현대아파트(220)   
3  서울특별시 강남구 개포동        655.0         2.0  언주로 103  개포2차현대아파트(220)   
4  서울특별시 강남구 개포동        655.0         2.0  언주로 103  개포2차현대아파트(220)   

   year_month  day   area deal_price  floor  
0      200603   10  77.75     59,500      7  
1      200603   29  77.75     60,000      6  
2      200604   29  77.75     67,000      9  
3      200606    1  77.75     60,000      4  
4      200610   20  77.75     72,250      5

In [ ]:
# 타입 변경을 통해서 deal_price,year_month, day 타입 변경
df_default["deal_price"] = df_default["deal_price"].str.replace(",", "") # 'deal_price'에서 ','가 들어있는 부분 제거(추후 계산에 사용하기 위해서서)
df = df_default.astype({'year_month':'str','day':'str','deal_price':'int64'}).copy()
df.head() # 형태가 변경된거 확인

address  main_number  sub_number     road            name year_month  \
0  서울특별시 강남구 개포동        655.0         2.0  언주로 103  개포2차현대아파트(220)     200603   
1  서울특별시 강남구 개포동        655.0         2.0  언주로 103  개포2차현대아파트(220)     200603   
2  서울특별시 강남구 개포동        655.0         2.0  언주로 103  개포2차현대아파트(220)     200604   
3  서울특별시 강남구 개포동        655.0         2.0  언주로 103  개포2차현대아파트(220)     200606   
4  서울특별시 강남구 개포동        655.0         2.0  언주로 103  개포2차현대아파트(220)     200610   

  day   area  deal_price  floor  
0  10  77.75       59500      7  
1  29  77.75       60000      6  
2  29  77.75       67000      9  
3   1  77.75       60000      4  
4  20  77.75       72250      5

In [ ]:
df.info() # 타입변경 및 null 확인

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1268633 entries, 0 to 1268632
Data columns (total 10 columns):
 #   Column       Non-Null Count    Dtype  
---  ------       --------------    -----  
 0   address      1268633 non-null  object 
 1   main_number  1268554 non-null  float64
 2   sub_number   1268554 non-null  float64
 3   road         1268633 non-null  object 
 4   name         1268633 non-null  object 
 5   year_month   1268633 non-null  object 
 6   day          1268633 non-null  object 
 7   area         1268633 non-null  float64
 8   deal_price   1268633 non-null  int64  
 9   floor        1268633 non-null  int64  
dtypes: float64(3), int64(2), object(5)
memory usage: 96.8+ MB


In [ ]:
# 'main_number'혹은 'sub_number'이 null 인데 'road'도 null 인 값을 확인 -> 없음
# 즉, 'road가 주소에 관한한 정보가 더욱 많음'
df[((df['main_number'].isnull()) |(df['sub_number'].isnull())) &(df['road'].isnull()) ]

Empty DataFrame
Columns: [address, main_number, sub_number, road, name, year_month, day, area, deal_price, floor]
Index: []

> main_number와 sub_number에 null 값들이 있음을 확인 -> road 정보가 주소에 관한 정보로 적합하다는 판단

## year, month, day 컬럼추가

- 날짜 관련한 컬럼들을 추후 그룹화등을 할 때 사용하기에 'year_month' 컬럼과 'day' 컬럼을 가공하여서 다양한 날짜 관련 컬럼들을 생성

In [ ]:
# 추후 데이터들 그룹화에 사용하기 위해서 날짜관련 컬럼들들 분리 및 생성
df['year'] = df['year_month'].str[0:4] # '연','월' 합쳐져 있는 컬럼에서 연도만 추출
df['month'] = df['year_month'].str[4:] # '연','월' 합쳐져 있는 컬럼에서 월만 추출
df.loc[df["day"].str.len()==1,"day"]='0'+df.loc[df["day"].str.len()==1,"day"] # '일'이 있는 컬럼에서 해당 '일'이 1일, 2일 처럼 1자리 숫자인 경우 앞에 0을 추가
df['date'] = pd.to_datetime(df['year']+df['month']+df['day']) # 일자들을 합쳐서 date 컬럼 생성
df = df.astype({'year':'int64','month':'int64','day':'int64'}) # 원하는 타입으로 변경
df = df.drop(['year_month'], axis=1) # 사용 안하는 컬럼들 제거
df.head()

address  main_number  sub_number     road            name  day  \
0  서울특별시 강남구 개포동        655.0         2.0  언주로 103  개포2차현대아파트(220)   10   
1  서울특별시 강남구 개포동        655.0         2.0  언주로 103  개포2차현대아파트(220)   29   
2  서울특별시 강남구 개포동        655.0         2.0  언주로 103  개포2차현대아파트(220)   29   
3  서울특별시 강남구 개포동        655.0         2.0  언주로 103  개포2차현대아파트(220)    1   
4  서울특별시 강남구 개포동        655.0         2.0  언주로 103  개포2차현대아파트(220)   20   

    area  deal_price  floor  year  month       date  
0  77.75       59500      7  2006      3 2006-03-10  
1  77.75       60000      6  2006      3 2006-03-29  
2  77.75       67000      9  2006      4 2006-04-29  
3  77.75       60000      4  2006      6 2006-06-01  
4  77.75       72250      5  2006     10 2006-10-20

In [ ]:
df.info() # 타입들이 원하는데로 변경됨을 확인인

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1268633 entries, 0 to 1268632
Data columns (total 12 columns):
 #   Column       Non-Null Count    Dtype         
---  ------       --------------    -----         
 0   address      1268633 non-null  object        
 1   main_number  1268554 non-null  float64       
 2   sub_number   1268554 non-null  float64       
 3   road         1268633 non-null  object        
 4   name         1268633 non-null  object        
 5   day          1268633 non-null  int64         
 6   area         1268633 non-null  float64       
 7   deal_price   1268633 non-null  int64         
 8   floor        1268633 non-null  int64         
 9   year         1268633 non-null  int64         
 10  month        1268633 non-null  int64         
 11  date         1268633 non-null  datetime64[ns]
dtypes: datetime64[ns](1), float64(3), int64(5), object(3)
memory usage: 116.1+ MB


In [ ]:
# 주소 및 도로명들 분리
df["address_0"] = df["address"].str.split(' ',expand=True)[0] # '시' 만 추출
df["address_1"] = df["address"].str.split(' ',expand=True)[1] # '구' 만 추출
df["address_2"] = df["address"].str.split(' ',expand=True)[2] # '동' 만 추출
df["road_name"] = df["road"].str.split(' ',expand=True)[0] # '도로명' 만 추출
df["road_number"] = df["road"].str.split(' ',expand=True)[1] # '도로숫자' 만 추출
df= df[['year','month','day','address_0','address_1','address_2','road_name','road_number','area','deal_price','name','main_number','sub_number','date']] # 사용할 컬럼만 선택
df.head()

year  month  day address_0 address_1 address_2 road_name road_number  \
0  2006      3   10     서울특별시       강남구       개포동       언주로         103   
1  2006      3   29     서울특별시       강남구       개포동       언주로         103   
2  2006      4   29     서울특별시       강남구       개포동       언주로         103   
3  2006      6    1     서울특별시       강남구       개포동       언주로         103   
4  2006     10   20     서울특별시       강남구       개포동       언주로         103   

    area  deal_price            name  main_number  sub_number       date  
0  77.75       59500  개포2차현대아파트(220)        655.0         2.0 2006-03-10  
1  77.75       60000  개포2차현대아파트(220)        655.0         2.0 2006-03-29  
2  77.75       67000  개포2차현대아파트(220)        655.0         2.0 2006-04-29  
3  77.75       60000  개포2차현대아파트(220)        655.0         2.0 2006-06-01  
4  77.75       72250  개포2차현대아파트(220)        655.0         2.0 2006-10-20

## 결측치 처리1

In [ ]:
df.info() # road_number에 1개의의 null 값이 생김을 확인

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1268633 entries, 0 to 1268632
Data columns (total 14 columns):
 #   Column       Non-Null Count    Dtype         
---  ------       --------------    -----         
 0   year         1268633 non-null  int64         
 1   month        1268633 non-null  int64         
 2   day          1268633 non-null  int64         
 3   address_0    1268633 non-null  object        
 4   address_1    1268633 non-null  object        
 5   address_2    1268633 non-null  object        
 6   road_name    1268633 non-null  object        
 7   road_number  1268632 non-null  object        
 8   area         1268633 non-null  float64       
 9   deal_price   1268633 non-null  int64         
 10  name         1268633 non-null  object        
 11  main_number  1268554 non-null  float64       
 12  sub_number   1268554 non-null  float64       
 13  date         1268633 non-null  datetime64[ns]
dtypes: datetime64[ns](1), float64(3), int64(4), object(6)
memory usage

In [ ]:
df[df['road_number'].isnull()] # road_number에 null값이 들어 있는 row를 확인

year  month  day address_0 address_1 address_2 road_name road_number  \
1177515  2020     12   31     서울특별시        중구     만리동2가      만리재로        None   

            area  deal_price          name  main_number  sub_number       date  
1177515  39.9541      161000  서울역센트럴자이(임대)        176.0         1.0 2020-12-31

In [ ]:
# '서울역센트럴자이'를 확인 -> '' 값이 존재함을 확인..
df.loc[df['name'] == '서울역센트럴자이',:]

year  month  day address_0 address_1 address_2 road_name road_number  \
936223   2017      5    3     서울특별시        중구     만리동2가      만리재로         175   
936224   2017     12   20     서울특별시        중구     만리동2가      만리재로         175   
936225   2017     12   30     서울특별시        중구     만리동2가                         
1018067  2018      3   20     서울특별시        중구     만리동2가                         
1093938  2019      7   13     서울특별시        중구     만리동2가      만리재로         175   
1093939  2019      8   20     서울특별시        중구     만리동2가      만리재로         175   
1093940  2019      8   23     서울특별시        중구     만리동2가      만리재로         175   
1093941  2019      9    8     서울특별시        중구     만리동2가      만리재로         175   
1093942  2019      9   21     서울특별시        중구     만리동2가      만리재로         175   
1093943  2019     11   30     서울특별시        중구     만리동2가      만리재로         175   
1093944  2019     12   12     서울특별시        중구     만리동2가      만리재로         175   
1093945  2019     12   14     서울특별시        중구     만리동2가      만리재로         175   
1177510  2020      1    8     서울특별시        중구     만리동2가      만리재로         175   
1177511  2020      5   20     서울특별시        중구     만리동2가      만리재로         175   
1177512  2020      7   12     서울특별시        중구     만리동2가      만리재로         175   
1177513  2020      8   13     서울특별시        중구     만리동2가      만리재로         175   
1177514  2020     10   17     서울특별시        중구     만리동2가      만리재로         175   
1222610  2021     12   14     서울특별시        중구     만리동2가      만리재로         175   
1236741  2022      1   17     서울특별시        중구     만리동2가      만리재로         175   
1236742  2022      3    2     서울특별시        중구     만리동2가      만리재로         175   
1236743  2022      6    5     서울특별시        중구     만리동2가      만리재로         175   
1236744  2022     12   14     서울특별시        중구     만리동2가      만리재로         175   
1267368  2023      1   20     서울특별시        중구     만리동2가      만리재로         175   
1267369  2023      2   18     서울특별시        중구     만리동2가      만리재로         175   
1267370  2023      3    1     서울특별시        중구     만리동2가      만리재로         175   
1267371  2023      3    9     서울특별시        중구     만리동2가      만리재로         175   
1267372  2023      3   28     서울특별시        중구     만리동2가      만리재로         175   
1267373  2023      5   11     서울특별시        중구     만리동2가      만리재로         175   
1267374  2023      6   17     서울특별시        중구     만리동2가      만리재로         175   
1267375  2023      7    7     서울특별시        중구     만리동2가      만리재로         175   
1267376  2023      7   21     서울특별시        중구     만리동2가      만리재로         175   
1267377  2023      7   27     서울특별시        중구     만리동2가      만리재로         175   
1267378  2023      8   25     서울특별시        중구     만리동2가      만리재로         175   
1267379  2023      8   28     서울특별시        중구     만리동2가      만리재로         175   
1267380  2023      9    1     서울특별시        중구     만리동2가      만리재로         175   
1267381  2023      9    5     서울특별시        중구     만리동2가      만리재로         175   
1267382  2023      9   13     서울특별시        중구     만리동2가      만리재로         175   
1267383  2023      9   19     서울특별시        중구     만리동2가      만리재로         175   
1267384  2023      9   22     서울특별시        중구     만리동2가      만리재로         175   
1267385  2023      9   23     서울특별시        중구     만리동2가      만리재로         175   
1267386  2023     10    5     서울특별시        중구     만리동2가      만리재로         175   

            area  deal_price      name  main_number  sub_number       date  
936223   84.9720       79390  서울역센트럴자이        176.0         1.0 2017-05-03  
936224   59.9430       85000  서울역센트럴자이        176.0         1.0 2017-12-20  
936225   59.9400       85000  서울역센트럴자이        176.0         1.0 2017-12-30  
1018067  72.9900       85000  서울역센트럴자이        176.0         1.0 2018-03-20  
1093938  84.9720      134500  서울역센트럴자이        176.0         1.0 2019-07-13  
1093939  59.9400       95000  서울역센트럴자이        176.0         1.0 2019-08-20  
1093940  84.9720      139000  서울역센트럴자이        176.0         1.0 201

In [ ]:
# 값이 '' 로 되어 있는 row들을 확인인
df.loc[df['road_name'] == '',:]

year  month  day address_0 address_1 address_2 road_name road_number  \
1606     2006      2   23     서울특별시       강남구       논현동                         
1628     2006     10   19     서울특별시       강남구       논현동                         
2799     2006      1   24     서울특별시       강남구       대치동                         
2806     2006      2   14     서울특별시       강남구       대치동                         
2807     2006      2   14     서울특별시       강남구       대치동                         
...       ...    ...  ...       ...       ...       ...       ...         ...   
1255393  2023      9    9     서울특별시       서초구       반포동                         
1255394  2023      9   13     서울특별시       서초구       반포동                         
1255395  2023      9   24     서울특별시       서초구       반포동                         
1255396  2023      9   25     서울특별시       서초구       반포동                         
1255398  2023     10   17     서울특별시       서초구       반포동                         

           area  deal_price     name  main_number  sub_number       date  
1606     128.67       73500       경복        276.0         0.0 2006-02-23  
1628      95.48       71000       경복        276.0         0.0 2006-10-19  
2799      76.56       80000      청실1        633.0         0.0 2006-01-24  
2806     102.64      143500      청실1        633.0         0.0 2006-02-14  
2807     102.64      142000      청실1        633.0         0.0 2006-02-14  
...         ...         ...      ...          ...         ...        ...  
1255393   84.97      430000  래미안원베일리          1.0         1.0 2023-09-09  
1255394  101.97      470000  래미안원베일리          1.0         1.0 2023-09-13  
1255395   74.92      322000  래미안원베일리          1.0         1.0 2023-09-24  
1255396   84.93      394000  래미안원베일리          1.0         1.0 2023-09-25  
1255398   59.96      290000  래미안원베일리          1.0         1.0 2023-10-17  

[2047 rows x 14 columns]

> null 값이 없다고 ''값도 없는건 아니구나! -> 의미적으로는 결측치이지만 ''로 표시되어서 마치 값이 있는 것처럼 있을 수도 있음

In [ ]:
df.loc[df['name'] == '서울역센트럴자이(임대)','name']='서울역센트럴자이' # '서울역센트럴자이(임대)' 명칭을을 '서울역센트럴자이'로 수정
df.loc[df['name'] == '서울역센트럴자이','road_name']='만리재로' # 위에서 확인한 '서울역센트럴자이'의 값들로 'road_name' 수정
df.loc[df['name'] == '서울역센트럴자이','road_number']='175' # 위에서 확인한 '서울역센트럴자이'의 값들로 'road_number' 수정
df.info() # 우선 1차적으로 null 로 표시되는는 null 값들은 처리함을 확인

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1268633 entries, 0 to 1268632
Data columns (total 14 columns):
 #   Column       Non-Null Count    Dtype         
---  ------       --------------    -----         
 0   year         1268633 non-null  int64         
 1   month        1268633 non-null  int64         
 2   day          1268633 non-null  int64         
 3   address_0    1268633 non-null  object        
 4   address_1    1268633 non-null  object        
 5   address_2    1268633 non-null  object        
 6   road_name    1268633 non-null  object        
 7   road_number  1268633 non-null  object        
 8   area         1268633 non-null  float64       
 9   deal_price   1268633 non-null  int64         
 10  name         1268633 non-null  object        
 11  main_number  1268554 non-null  float64       
 12  sub_number   1268554 non-null  float64       
 13  date         1268633 non-null  datetime64[ns]
dtypes: datetime64[ns](1), float64(3), int64(4), object(6)
memory usage

## 결측치 처리2

- 앞에서 과정들을 통해서 ''들이 값들로 들어 있을 수도 있음을 깨닫고 '' 값들을 null로 간주하여서 결측치 처리 진행

In [ ]:
import numpy as np
df = df.replace('', np.nan) # ''값만 있는 값들을 null 값들로 수정
df.info() # 수정한 후 정보 확인

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1268633 entries, 0 to 1268632
Data columns (total 14 columns):
 #   Column       Non-Null Count    Dtype         
---  ------       --------------    -----         
 0   year         1268633 non-null  int64         
 1   month        1268633 non-null  int64         
 2   day          1268633 non-null  int64         
 3   address_0    1268633 non-null  object        
 4   address_1    1268633 non-null  object        
 5   address_2    1268633 non-null  object        
 6   road_name    1266588 non-null  object        
 7   road_number  1265322 non-null  object        
 8   area         1268633 non-null  float64       
 9   deal_price   1268633 non-null  int64         
 10  name         1268633 non-null  object        
 11  main_number  1268554 non-null  float64       
 12  sub_number   1268554 non-null  float64       
 13  date         1268633 non-null  datetime64[ns]
dtypes: datetime64[ns](1), float64(3), int64(4), object(6)
memory usage

In [ ]:
df.isnull().sum() # df의 'road_name'과 'road_number'의 null 값들이 증가함을 확인,

year              0
month             0
day               0
address_0         0
address_1         0
address_2         0
road_name      2045
road_number    3311
area              0
deal_price        0
name              0
main_number      79
sub_number       79
date              0
dtype: int64

> 처음에는 도로주소가 null값이 더 적은 줄 알았지만, 전처리 과정 중 지번주소가 null 값이 더 적은 것을 확인

In [ ]:
# 'main_number'나 'sub_number' 둘중 하나만 null 인 것을 확인 -> 없음
# 즉, 2개가 동시에 null 값을 가지고 있음
df[((df['main_number'].isnull()) &(df['sub_number'].notnull()))
  |((df['main_number'].notnull()) &(df['sub_number'].isnull()))]

Empty DataFrame
Columns: [year, month, day, address_0, address_1, address_2, road_name, road_number, area, deal_price, name, main_number, sub_number, date]
Index: []

In [ ]:
# 도로명정보에는 null이고 지번주소도 null인 데이터를 확인 -> 없다
# 즉, 도로명주소나 지번주소 둘 중 하나를 활용해서 주소에 대한 정보를 얻을 수 있다
df[((df['road_name'].isnull()) | (df['road_number'].isnull())) & (df['main_number'].isnull())]

Empty DataFrame
Columns: [year, month, day, address_0, address_1, address_2, road_name, road_number, area, deal_price, name, main_number, sub_number, date]
Index: []

In [ ]:
# 처리해야 할 null 값이 있는 데이터프레임을 조회
df.loc[df['main_number'].isnull(),['address_0','address_1','address_2','road_name','road_number','name','main_number','sub_number']]

address_0 address_1 address_2 road_name road_number           name  \
681633      서울특별시       서초구       신원동     헌릉로8길       10-12  힐스테이트 서초 젠트리스   
681634      서울특별시       서초구       신원동     헌릉로8길       10-12  힐스테이트 서초 젠트리스   
681635      서울특별시       서초구       신원동     헌릉로8길       10-12  힐스테이트 서초 젠트리스   
681636      서울특별시       서초구       신원동     헌릉로8길       10-12  힐스테이트 서초 젠트리스   
681637      서울특별시       서초구       신원동     헌릉로8길       10-12  힐스테이트 서초 젠트리스   
...           ...       ...       ...       ...         ...            ...   
1232881     서울특별시       서초구       신원동     헌릉로8길       10-12  힐스테이트 서초 젠트리스   
1256361     서울특별시       서초구       신원동     헌릉로8길       10-12  힐스테이트 서초 젠트리스   
1256362     서울특별시       서초구       신원동     헌릉로8길       10-12  힐스테이트 서초 젠트리스   
1256363     서울특별시       서초구       신원동     헌릉로8길       10-12  힐스테이트 서초 젠트리스   
1256364     서울특별시       서초구       신원동     헌릉로8길       10-12  힐스테이트 서초 젠트리스   

         main_number  sub_number  
681633           NaN         NaN  
681634           NaN         NaN  
681635           NaN         NaN  
681636           NaN         NaN  
681637           NaN         NaN  
...              ...         ...  
1232881          NaN         NaN  
1256361          NaN         NaN  
1256362          NaN         NaN  
1256363          NaN         NaN  
1256364          NaN         NaN  

[79 rows x 8 columns]

In [ ]:
df.loc[df['main_number'].isnull(),'name'].unique() # 처리해야 할 지번주소에 null 값이 있는 아파트명들 조회
                                                   # '힐스테이트 서초 젠트리스'만 수정하면 될듯

array(['힐스테이트 서초 젠트리스'], dtype=object)

In [ ]:
df.loc[df['name']=='힐스테이트 서초 젠트리스',:] # 기존 name 컬럼이 '힐스테이트 서초 젠트리스' 인 전체 값들이 지번주소가 null값으로 되어 있음

year  month  day address_0 address_1 address_2 road_name road_number  \
681633   2015      3    1     서울특별시       서초구       신원동     헌릉로8길       10-12   
681634   2015      4   17     서울특별시       서초구       신원동     헌릉로8길       10-12   
681635   2015      5    1     서울특별시       서초구       신원동     헌릉로8길       10-12   
681636   2015      6   16     서울특별시       서초구       신원동     헌릉로8길       10-12   
681637   2015      6   26     서울특별시       서초구       신원동     헌릉로8길       10-12   
...       ...    ...  ...       ...       ...       ...       ...         ...   
1232881  2022      9   28     서울특별시       서초구       신원동     헌릉로8길       10-12   
1256361  2023      4   20     서울특별시       서초구       신원동     헌릉로8길       10-12   
1256362  2023      9   11     서울특별시       서초구       신원동     헌릉로8길       10-12   
1256363  2023      9   16     서울특별시       서초구       신원동     헌릉로8길       10-12   
1256364  2023      9   21     서울특별시       서초구       신원동     헌릉로8길       10-12   

           area  deal_price           name  main_number  sub_number       date  
681633    84.95       73430  힐스테이트 서초 젠트리스          NaN         NaN 2015-03-01  
681634    84.99       79000  힐스테이트 서초 젠트리스          NaN         NaN 2015-04-17  
681635   101.90       95000  힐스테이트 서초 젠트리스          NaN         NaN 2015-05-01  
681636    84.95       87200  힐스테이트 서초 젠트리스          NaN         NaN 2015-06-16  
681637   101.90       94500  힐스테이트 서초 젠트리스          NaN         NaN 2015-06-26  
...         ...         ...            ...          ...         ...        ...  
1232881   84.95      173000  힐스테이트 서초 젠트리스          NaN         NaN 2022-09-28  
1256361   84.95      160000  힐스테이트 서초 젠트리스          NaN         NaN 2023-04-20  
1256362   84.99      163000  힐스테이트 서초 젠트리스          NaN         NaN 2023-09-11  
1256363  101.90      190000  힐스테이트 서초 젠트리스          NaN         NaN 2023-09-16  
1256364   84.95      161000  힐스테이트 서초 젠트리스          NaN         NaN 2023-09-21  

[79 rows x 14 columns]

In [ ]:
# 지번주소 null 값들을 네이버를 통해 검색하여서 정보를 얻고 수정
df.loc[df['name']=='힐스테이트 서초 젠트리스','main_number'] = 557
df.loc[df['name']=='힐스테이트 서초 젠트리스','sub_number'] = 0

In [ ]:
# 사용할 컬럼들 선택택과, 컬럼명들 수정
df_deal = df[['date','year','month','day','address_0','address_1','address_2','main_number','sub_number','name','area','deal_price']].copy()
df_deal.columns =['date','year','month','day','address_0','address_1','address_2','address_3','address_4','name','area','deal_price']
df_deal = df_deal[df_deal['year']>=2011] # 전세/월세데이터가 2011년 이후로 있어서 연도 선택
df_deal.head()

date  year  month  day address_0 address_1 address_2  address_3  \
355306 2011-07-09  2011      7    9     서울특별시       강남구       개포동      655.0   
355307 2011-07-28  2011      7   28     서울특별시       강남구       개포동      655.0   
355308 2011-01-19  2011      1   19     서울특별시       강남구       개포동      658.0   
355309 2011-09-02  2011      9    2     서울특별시       강남구       개포동      658.0   
355310 2011-12-17  2011     12   17     서울특별시       강남구       개포동      658.0   

        address_4            name   area  deal_price  
355306        2.0  개포2차현대아파트(220)  77.75       64000  
355307        2.0  개포2차현대아파트(220)  77.75       65500  
355308        1.0  개포6차우성아파트1동~8동  67.28       70500  
355309        1.0  개포6차우성아파트1동~8동  79.97       85000  
355310        1.0  개포6차우성아파트1동~8동  67.28       68000

In [ ]:
df_deal.info() # 데이터프레임 정보 확인

<class 'pandas.core.frame.DataFrame'>
Int64Index: 913327 entries, 355306 to 1268632
Data columns (total 12 columns):
 #   Column      Non-Null Count   Dtype         
---  ------      --------------   -----         
 0   date        913327 non-null  datetime64[ns]
 1   year        913327 non-null  int64         
 2   month       913327 non-null  int64         
 3   day         913327 non-null  int64         
 4   address_0   913327 non-null  object        
 5   address_1   913327 non-null  object        
 6   address_2   913327 non-null  object        
 7   address_3   913327 non-null  float64       
 8   address_4   913327 non-null  float64       
 9   name        913327 non-null  object        
 10  area        913327 non-null  float64       
 11  deal_price  913327 non-null  int64         
dtypes: datetime64[ns](1), float64(3), int64(4), object(4)
memory usage: 90.6+ MB


> 해당 데이터프레임은 거래일자의 정보를 나타내는 'date', 'month', 'day' 컬럼들, 주소의 정보를 나타내는 'address_0', 'address_1', 'address_2', 'address_4' 컬럼들, 아파트명을 나타내는 'name'컬럼, 아파트의 면적을 나타내는 'area' 컬럼, 매매가격을 나타내는 'deal_price' 컬럼으로 이루어져 있다

In [ ]:
df_deal.iloc[200] # 정보들 제대로 있는지 확인

date          2011-12-23 00:00:00
year                         2011
month                          12
day                            23
address_0                   서울특별시
address_1                     강남구
address_2                     개포동
address_3                   141.0
address_4                     0.0
name                      개포주공1단지
area                        56.57
deal_price                  95000
Name: 355506, dtype: object

In [ ]:
df_deal.to_csv('/content/drive/MyDrive/house_price/after_data/apartment_deal.csv',index=False) # 파일로 저장

# apartment_full_rent.csv, apartment_month_rent.csv 파일 생성

- 'http://rtdown.molit.go.kr/' 사이트를 통해서 아파트전세,월세 정보 파일로 얻음
- '아파트 전세' 관련 정보들을 가지고 있는 데이터프레임을 생성하여 apartment_full_rent.csv 로 저장
- '파이트 월세' 관련 정보들을 가지고 있는 데이터프레임을 생성하여 apartment_month_rent.csv 로 저장

## csv 파일들 불러오기 및 병합

- 아파트 전세정보 csv 파일들은 연도별로 파일들이 분류가 되어있고, 각 csv 파일 내의 모든 정보들이 전부 필요하지는 않기에 전처리 과정 진행

In [ ]:
import pandas as pd
import os


dir_path = "/content/drive/MyDrive/house_price/original_data/rent_price/Seoul"
file_list = os.listdir(dir_path)
file_list.sort()
df_list = list()

# 해당 폴더 안에 있는 csv 파일들을 읽어서 리스트 안에 데이터프레임들을 담음
for csv_file in file_list:
    df_list.append(pd.read_csv(dir_path+"/"+csv_file ,skiprows=15,  encoding='cp949', low_memory=False))


In [ ]:
df_list[-1].info() # 리스트 안에 잘 담겼는지 확인

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 224919 entries, 0 to 224918
Data columns (total 19 columns):
 #   Column         Non-Null Count   Dtype  
---  ------         --------------   -----  
 0   시군구            224919 non-null  object 
 1   번지             224861 non-null  object 
 2   본번             224892 non-null  float64
 3   부번             224892 non-null  float64
 4   단지명            224919 non-null  object 
 5   전월세구분          224919 non-null  object 
 6   전용면적(㎡)        224919 non-null  float64
 7   계약년월           224919 non-null  int64  
 8   계약일            224919 non-null  int64  
 9   보증금(만원)        224919 non-null  object 
 10  월세(만원)         224919 non-null  object 
 11  층              224919 non-null  int64  
 12  건축년도           224903 non-null  float64
 13  도로명            224919 non-null  object 
 14  계약기간           224919 non-null  object 
 15  계약구분           224919 non-null  object 
 16  갱신요구권 사용       224919 non-null  object 
 17  종전계약 보증금 (만원)  184614 non-nul

In [ ]:
# 모든 데이터프레임을을 통합
df_default = df_list[0]
for df_csv in df_list[1:]:
    df_default = pd.concat([df_default, df_csv], axis=0)
df_default.reset_index(drop=True, inplace=True) # concat으로 합쳐질 때 인덱스 재설정
df_default.info() # 데이터프레임 합친 결과 확인

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2310694 entries, 0 to 2310693
Data columns (total 19 columns):
 #   Column         Dtype  
---  ------         -----  
 0   시군구            object 
 1   번지             object 
 2   본번             float64
 3   부번             float64
 4   단지명            object 
 5   전월세구분          object 
 6   전용면적(㎡)        float64
 7   계약년월           int64  
 8   계약일            int64  
 9   보증금(만원)        object 
 10  월세(만원)         object 
 11  층              float64
 12  건축년도           float64
 13  도로명            object 
 14  계약기간           object 
 15  계약구분           object 
 16  갱신요구권 사용       object 
 17  종전계약 보증금 (만원)  object 
 18  종전계약 월세 (만원)   object 
dtypes: float64(5), int64(2), object(12)
memory usage: 335.0+ MB


In [ ]:
df_default.head() # 데이터 형태 확인

시군구     번지     본번   부번             단지명 전월세구분  전용면적(㎡)    계약년월  \
0  서울특별시 강남구 개포동  655-2  655.0  2.0  개포2차현대아파트(220)    전세    77.75  201101   
1  서울특별시 강남구 개포동  655-2  655.0  2.0  개포2차현대아파트(220)    전세    77.75  201101   
2  서울특별시 강남구 개포동  655-2  655.0  2.0  개포2차현대아파트(220)    전세    77.75  201102   
3  서울특별시 강남구 개포동  655-2  655.0  2.0  개포2차현대아파트(220)    전세    77.75  201102   
4  서울특별시 강남구 개포동  655-2  655.0  2.0  개포2차현대아파트(220)    전세    77.75  201102   

   계약일 보증금(만원) 월세(만원)    층    건축년도      도로명 계약기간 계약구분 갱신요구권 사용 종전계약 보증금 (만원)  \
0    5  35,000      0  7.0  1988.0  언주로 103    -    -        -           NaN   
1   18  20,000      0  8.0  1988.0  언주로 103    -    -        -           NaN   
2    1  24,000      0  5.0  1988.0  언주로 103    -    -        -           NaN   
3   11  31,000      0  9.0  1988.0  언주로 103    -    -        -           NaN   
4   24  30,500      0  9.0  1988.0  언주로 103    -    -        -           NaN   

  종전계약 월세 (만원)  
0          NaN  
1          NaN  
2          NaN  
3          NaN  
4          NaN

In [ ]:
df_default.isnull().sum() # 번지, 본번, 부번이 null 값들이 있음

시군구                    0
번지                  1644
본번                   261
부번                   261
단지명                    0
전월세구분                  0
전용면적(㎡)               36
계약년월                   0
계약일                    0
보증금(만원)                0
월세(만원)                 0
층                     36
건축년도                 265
도로명                    0
계약기간                   0
계약구분                   0
갱신요구권 사용               0
종전계약 보증금 (만원)    1834104
종전계약 월세 (만원)     1834104
dtype: int64

In [ ]:
df_default['전월세구분'].unique()

array(['전세', '월세'], dtype=object)

> 전월세구분이 '전세'와 '월세' 두 가지만 있음으로 조건문을 활용해서 나누기에 용이함

## 전세 데이터 프레임 생성

- apartment_deal 과 진행 과정이 거의 동일하기에 apartment_deal.csv 파일 생성의 진행과정을 참조해서 하나의 셀로 합쳐서 진행
- 주석 부분들은 중간과정 확인 부분

In [ ]:
# 전세 데이터 프레임 생성
df_full_rent = df_default.loc[df_default['전월세구분']=='전세',['시군구','본번','부번','도로명','계약년월','계약일','보증금(만원)','전용면적(㎡)','단지명']].copy()
df_full_rent.columns = ['address','main_number','sub_number','road','year_month','day','full_rent_price','area','name']


df_full_rent = df_full_rent.astype({'full_rent_price':'str','year_month':'str','day':'str','full_rent_price':'str'})
df_full_rent["full_rent_price"] = df_full_rent["full_rent_price"].str.replace(",", "")
df_full_rent.loc[df_full_rent["day"].str.len()==1,"day"]='0'+df_full_rent.loc[df_full_rent["day"].str.len()==1,"day"] # 일이 있는 컬럼에서 1자리 숫자인 경우 앞에 0을 추가성
df_full_rent['year'] = df_full_rent['year_month'].str[0:4] # 연,월 합쳐져 있는 컬럼에서 연도만 추출
df_full_rent['month'] = df_full_rent['year_month'].str[4:] # 연,월 합쳐져 있는 컬럼에서 월만 추출
df_full_rent['date'] = pd.to_datetime(df_full_rent['year']+df_full_rent['month']+df_full_rent['day']) # 일자들을 합쳐서 date 컬럼 생
df_full_rent = df_full_rent.astype({'year':'int64','month':'int64','day':'int64','full_rent_price':'int64'})
df_full_rent = df_full_rent.drop(['year_month'], axis=1) # 사용 안하는 컬럼들 제거

df_full_rent["address_0"] = df_full_rent["address"].str.split(' ',expand=True)[0] # '시' 만 추출해야 하나, 서울만 함으로 일단은 실행 X
df_full_rent["address_1"] = df_full_rent["address"].str.split(' ',expand=True)[1] # '구' 만 추출
df_full_rent["address_2"] = df_full_rent["address"].str.split(' ',expand=True)[2] # '동' 만 추출
df_full_rent["road_name"] = df_full_rent["road"].str.split(' ',expand=True)[0] # '도로명' 만 추출
df_full_rent["road_number"] = df_full_rent["road"].str.split(' ',expand=True)[1] # '도로숫자' 만 추출
df_full_rent= df_full_rent[['year','month','day','address_0','address_1','address_2','main_number','sub_number','road_name','road_number','area',"full_rent_price",'name','date']] # 사용할 컬럼만 선택


df_full_rent = df_full_rent.replace('', None) # ''값만 있는 값들을 null 값들로 수정

df_full_rent.loc[df_full_rent['name']=='힐스테이트 서초 젠트리스','main_number'] = 557
df_full_rent.loc[df_full_rent['name']=='힐스테이트 서초 젠트리스','sub_number'] = 0


df_full_rent = df_full_rent[['date','year','month','day','address_0','address_1','address_2','main_number','sub_number','name','area','full_rent_price']].copy()
df_full_rent.columns =['date','year','month','day','address_0','address_1','address_2','address_3','address_4','name','area','full_rent_price']

In [ ]:
df_full_rent.isnull().sum()

date                0
year                0
month               0
day                 0
address_0           0
address_1           0
address_2           0
address_3           0
address_4           0
name                0
area               25
full_rent_price     0
dtype: int64

### 'area' 컬럼 결측치 처리

- apartment_deal.csv 생성과 달리 area 컬럼에 결측치가 존재하기에 결측치 처리 부분 추가
- 결측치는 해당 주소의 전세 아파트의 거래 내역 중 가장 거래가 많았던 area 컬럼의 값 으로 대체하여 처리

In [ ]:
# area의 빈 칸들 해결
df_full_rent[df_full_rent['area'].isnull()].tail()

date  year  month  day address_0 address_1 address_2  address_3  \
357440 2013-11-16  2013     11   16     서울특별시       노원구       공릉동      683.0   
375219 2013-11-30  2013     11   30     서울특별시      동대문구       장안동      312.0   
389892 2013-01-17  2013      1   17     서울특별시      서대문구       창천동      501.0   
439901 2013-01-20  2013      1   20     서울특별시      영등포구    영등포동4가      103.0   
490009 2014-02-19  2014      2   19     서울특별시       강서구       화곡동       29.0   

        address_4          name  area  full_rent_price  
357440       14.0        한일휴니스빌   NaN             8000  
375219        8.0         태솔에버빌   NaN            12000  
389892       14.0         삼성아트빌   NaN             9000  
439901        0.0       영등포그랑그루   NaN             8000  
490009       47.0  드림하우스(29-47)   NaN             9500

In [ ]:
# area가 null값인 row들이 다른 주소정보관련 컬럼들을 리스트 화
add_1 = list(df_full_rent.loc[df_full_rent['area'].isnull(),'address_1'])
add_2 = list(df_full_rent.loc[df_full_rent['area'].isnull(),'address_2'])
add_3 = list(df_full_rent.loc[df_full_rent['area'].isnull(),'address_3'])
add_4 = list(df_full_rent.loc[df_full_rent['area'].isnull(),'address_4'])
area_list = list()

In [ ]:
# area_list 에 값 추가
for i in range(len(add_1)):
    # 해당 주소에서 거래된 매물들의 'area' 정보가 없을 경우, area null을 처리할 참조 자료가 없음으로 ''으로 처리리
    if (len(df_full_rent.loc[(df_full_rent['address_1'] ==add_1[i]) &
                     (df_full_rent['address_2'] ==add_2[i]) &
                     (df_full_rent['address_3'] ==add_3[i]) &
                     (df_full_rent['address_4'] ==add_4[i]),
                     'area'].value_counts())) == 0:

        area_list.append('')
    else:
        # 해당 주소에서 가장 많이 거래되었던 층수를 null 값에 채움움
        area_list.append(df_full_rent.loc[(df_full_rent['address_1'] ==add_1[i]) &
                     (df_full_rent['address_2'] ==add_2[i]) &
                     (df_full_rent['address_3'] ==add_3[i]) &
                     (df_full_rent['address_4'] ==add_4[i]),
                     'area'].value_counts().idxmax())
print(area_list) # area 이 null 값인 주소의 매물들의 가장 많이 거래된 층들을 출력력

[84.9, 33.33, 15.94, 15.94, 84.98, 142.034, 142.034, 142.034, 142.034, 17.07, 17.07, 17.07, 17.07, 17.07, 64.52, 23.47, 23.47, 13.2195, 13.2195, 13.2195, 13.2195, 49.88, 39.28, 12.1, '']


> 마지막에 ''인 값이 있는데 이건 해당 매물은 참조할 만할 거래내역이 없음을 의미

In [ ]:
# len을 통해서 리스트들이 다 만들어 졌는지 확인
print(len(add_1),len(add_2),len(add_3),len(add_4),len(area_list))

25 25 25 25 25


In [ ]:
# 맨 마지막 row가 '' 여서 해당 row의 area 값을 채우기 위해 참조할 값을 확인 -> 없음
# 해당은 area를 알수있는 방법이 없음 - 다른 참조할만할 area 값들이 없음 -> 추후 제거 필요
df_full_rent.loc[(df_full_rent['address_3']==29)&(df_full_rent['address_4']==47),:] # 테스트로 area이 null 값인 row를 대표로 확인인

date  year  month  day address_0 address_1 address_2  address_3  \
490009 2014-02-19  2014      2   19     서울특별시       강서구       화곡동       29.0   

        address_4          name  area  full_rent_price  
490009       47.0  드림하우스(29-47)   NaN             9500

In [ ]:
# area 가 null인 값들을 처리, 가장 많이 거래된 'area'의 정보로 결측치 처리리
for i in range(len(add_1)):
    df_full_rent.loc[(df_full_rent['address_1'] ==add_1[i]) &
                         (df_full_rent['address_2'] ==add_2[i]) &
                         (df_full_rent['address_3'] ==add_3[i]) &
                         (df_full_rent['address_4'] ==add_4[i]),
                         'area']=area_list[i]

In [ ]:
# null 대신 ''이 잘 들어있는지 확인
df_full_rent.loc[df_full_rent['area']=='',:]

date  year  month  day address_0 address_1 address_2  address_3  \
490009 2014-02-19  2014      2   19     서울특별시       강서구       화곡동       29.0   

        address_4          name area  full_rent_price  
490009       47.0  드림하우스(29-47)                  9500

In [ ]:
# area이 ''인 값 제거
df_full_rent=df_full_rent.drop(df_full_rent[df_full_rent['area']==''].index)

# 제거후 값 확인
df_full_rent.loc[df_full_rent['area']=='',:] # 제거가 된음 확인인

Empty DataFrame
Columns: [date, year, month, day, address_0, address_1, address_2, address_3, address_4, name, area, full_rent_price]
Index: []

In [ ]:
df_full_rent.info() # 값확인을 통해서 null값 처리가 되었는지 확인인

<class 'pandas.core.frame.DataFrame'>
Int64Index: 1580989 entries, 0 to 2310692
Data columns (total 12 columns):
 #   Column           Non-Null Count    Dtype         
---  ------           --------------    -----         
 0   date             1580989 non-null  datetime64[ns]
 1   year             1580989 non-null  int64         
 2   month            1580989 non-null  int64         
 3   day              1580989 non-null  int64         
 4   address_0        1580989 non-null  object        
 5   address_1        1580989 non-null  object        
 6   address_2        1580989 non-null  object        
 7   address_3        1580989 non-null  float64       
 8   address_4        1580989 non-null  float64       
 9   name             1580989 non-null  object        
 10  area             1580989 non-null  object        
 11  full_rent_price  1580989 non-null  int64         
dtypes: datetime64[ns](1), float64(2), int64(4), object(5)
memory usage: 156.8+ MB


> 해당 데이터프레임은 거래일자의 정보를 나타내는 'date', 'month', 'day' 컬럼들, 주소의 정보를 나타내는 'address_0', 'address_1', 'address_2', 'address_4' 컬럼들, 아파트명을 나타내는 'name'컬럼, 아파트의 면적을 나타내는 'area' 컬럼, 전세가격을 나타내는 'full_rent_price' 컬럼으로 이루어져 있다

In [ ]:
df_full_rent.to_csv('/content/drive/MyDrive/house_price/after_data/apartment_full_rent.csv', index=False) # 전세 csv 파일 생성성

## 월세 데이터 프레임 생성

- 전세 데이터프레임 생성 파트 참조

In [ ]:
# 월세 데이터 프레임 생성, 필요한 컬럼들만 필터링
df_month_rent = df_default.loc[df_default['전월세구분']=='월세',['시군구','본번','부번','도로명','계약년월','계약일','보증금(만원)','월세(만원)','전용면적(㎡)','단지명']].copy()
df_month_rent.columns = ['address','main_number','sub_number','road','year_month','day','rent_deposit','month_rent_price','area','name']
# df_month_rent.head()

df_month_rent.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 729704 entries, 25 to 2310693
Data columns (total 10 columns):
 #   Column            Non-Null Count   Dtype  
---  ------            --------------   -----  
 0   address           729704 non-null  object 
 1   main_number       729647 non-null  float64
 2   sub_number        729647 non-null  float64
 3   road              729704 non-null  object 
 4   year_month        729704 non-null  int64  
 5   day               729704 non-null  int64  
 6   rent_deposit      729704 non-null  object 
 7   month_rent_price  729704 non-null  object 
 8   area              729693 non-null  float64
 9   name              729704 non-null  object 
dtypes: float64(3), int64(2), object(5)
memory usage: 61.2+ MB


전세 파트와 다른 부분 확인! ↓

In [ ]:
df_month_rent["month_rent_price2"] = df_month_rent["month_rent_price"].str.replace(',','')
df_month_rent.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 729704 entries, 25 to 2310693
Data columns (total 11 columns):
 #   Column             Non-Null Count   Dtype  
---  ------             --------------   -----  
 0   address            729704 non-null  object 
 1   main_number        729647 non-null  float64
 2   sub_number         729647 non-null  float64
 3   road               729704 non-null  object 
 4   year_month         729704 non-null  int64  
 5   day                729704 non-null  int64  
 6   rent_deposit       729704 non-null  object 
 7   month_rent_price   729704 non-null  object 
 8   area               729693 non-null  float64
 9   name               729704 non-null  object 
 10  month_rent_price2  665236 non-null  object 
dtypes: float64(3), int64(2), object(6)
memory usage: 66.8+ MB


> "month_rent_price"를 replace를 적용해서 month_rent_price2 컬럼을 생성하는데 replace 함수가 제데로 처리가 안됨을 확인

>> df_month_rent["month_rent_price"].str.replace(',','')

>> 진행했을 때, 'month_rent_price2' 컬럼에서의 null 값이 매우 커짐 -> replace 매소드가 제대로 동작 안함을 확인

>> 왜 동작을 안할까? -> string 과 object 타입의 차이, object는 타입의 혼용?

In [ ]:
# 해당 파트를 통해서 우선 type 을 변경한 다음에 진행해야 함
df_month_rent = df_month_rent.astype({'month_rent_price':'str','rent_deposit':'str'})

- apartment_deal 과 진행 과정이 거의 동일하기에 한 셀로 합쳐서 진행
- 주석 부분들은 중간과정 확인 부분

In [ ]:
df_month_rent["rent_deposit"] = df_month_rent["rent_deposit"].str.replace(",", "")
df_month_rent["month_rent_price"] = df_month_rent["month_rent_price"].str.replace(',','')
df_month_rent = df_month_rent.astype({'year_month':'str','day':'str','rent_deposit':'int64','month_rent_price':'int64'})
df_month_rent['year'] = df_month_rent['year_month'].str[0:4] # 연,월 합쳐져 있는 컬럼에서 연도만 추출
df_month_rent['month'] = df_month_rent['year_month'].str[4:] # 연,월 합쳐져 있는 컬럼에서 월만 추출
df_month_rent.loc[df_month_rent["day"].str.len()==1,"day"]='0'+df_month_rent.loc[df_month_rent["day"].str.len()==1,"day"] # 일이 있는 컬럼에서 1자리 숫자인 경우 앞에 0을 추가성
df_month_rent['date'] = pd.to_datetime(df_month_rent['year']+df_month_rent['month']+df_month_rent['day']) # 일자들을 합쳐서 date 컬럼 생
df_month_rent = df_month_rent.astype({'year':'int64','month':'int64','day':'int64'})
df_month_rent = df_month_rent.drop(['year_month'], axis=1) # 사용 안하는 컬럼들 제거

df_month_rent["address_0"] = df_month_rent["address"].str.split(' ',expand=True)[0] # '시' 만 추출해야 하나, 서울만 함으로 일단은 실행 X
df_month_rent["address_1"] = df_month_rent["address"].str.split(' ',expand=True)[1] # '구' 만 추출
df_month_rent["address_2"] = df_month_rent["address"].str.split(' ',expand=True)[2] # '동' 만 추출
df_month_rent["road_name"] = df_month_rent["road"].str.split(' ',expand=True)[0] # '도로명' 만 추출
df_month_rent["road_number"] = df_month_rent["road"].str.split(' ',expand=True)[1] # '도로숫자' 만 추출
df_month_rent= df_month_rent[['year','month','day','address_0','address_1','address_2','main_number','sub_number','road_name','road_number','area',"rent_deposit","month_rent_price",'name','date']] # 사용할 컬럼만 선택


df_month_rent = df_month_rent.replace('', None) # ''값만 있는 값들을 null 값들로 수정

df_month_rent.loc[df_month_rent['name']=='힐스테이트 서초 젠트리스','main_number'] = 557
df_month_rent.loc[df_month_rent['name']=='힐스테이트 서초 젠트리스','sub_number'] = 0

df_month_rent = df_month_rent[['date','year','month','day','address_0','address_1','address_2','main_number','sub_number','name','area','rent_deposit','month_rent_price']]
df_month_rent.columns =['date','year','month','day','address_0','address_1','address_2','address_3','address_4','name','area','rent_deposit','month_rent_price']

In [ ]:
df_month_rent.isnull().sum()

date                 0
year                 0
month                0
day                  0
address_0            0
address_1            0
address_2            0
address_3            0
address_4            0
name                 0
area                11
rent_deposit         0
month_rent_price     0
dtype: int64

### 'area' 컬럼 결측치 처리

- 전세의 area 결측치 처리 부분 참조

In [ ]:
add_1 = list(df_month_rent.loc[df_month_rent['area'].isnull(),'address_1'])
add_2 = list(df_month_rent.loc[df_month_rent['area'].isnull(),'address_2'])
add_3 = list(df_month_rent.loc[df_month_rent['area'].isnull(),'address_3'])
add_4 = list(df_month_rent.loc[df_month_rent['area'].isnull(),'address_4'])
area_list = list()
# area_list 에 값 추가
for i in range(len(add_1)):
    # 해당 주소에서 거래된 매물들의 '층' 정보가 없을 경우, area null을 처리할 참조 자료가 없음으로 ''으로 처리리
    if (len(df_month_rent.loc[(df_month_rent['address_1'] ==add_1[i]) &
                     (df_month_rent['address_2'] ==add_2[i]) &
                     (df_month_rent['address_3'] ==add_3[i]) &
                     (df_month_rent['address_4'] ==add_4[i]),
                     'area'].value_counts())) == 0:

        area_list.append('')
    else:
        # 해당 주소에서 가장 많이 거래되었던 층수를 null 값에 채울거임
        area_list.append(df_month_rent.loc[(df_month_rent['address_1'] ==add_1[i]) &
                     (df_month_rent['address_2'] ==add_2[i]) &
                     (df_month_rent['address_3'] ==add_3[i]) &
                     (df_month_rent['address_4'] ==add_4[i]),
                     'area'].value_counts().idxmax())


for i in range(len(add_1)):
    df_month_rent.loc[(df_month_rent['address_1'] ==add_1[i]) &
                         (df_month_rent['address_2'] ==add_2[i]) &
                         (df_month_rent['address_3'] ==add_3[i]) &
                         (df_month_rent['address_4'] ==add_4[i]),
                         'area']=area_list[i]



In [ ]:
df_month_rent.isnull().sum()

date                0
year                0
month               0
day                 0
address_0           0
address_1           0
address_2           0
address_3           0
address_4           0
name                0
area                0
rent_deposit        0
month_rent_price    0
dtype: int64

In [ ]:
df_month_rent.head()

date  year  month  day address_0 address_1 address_2  address_3  \
25 2011-03-18  2011      3   18     서울특별시       강남구       개포동      658.0   
28 2011-04-09  2011      4    9     서울특별시       강남구       개포동      658.0   
38 2011-07-09  2011      7    9     서울특별시       강남구       개포동      658.0   
46 2011-09-19  2011      9   19     서울특별시       강남구       개포동      658.0   
47 2011-09-20  2011      9   20     서울특별시       강남구       개포동      658.0   

    address_4            name   area  rent_deposit  month_rent_price  
25        1.0  개포6차우성아파트1동~8동  79.97         19000                63  
28        1.0  개포6차우성아파트1동~8동  79.97         21000                35  
38        1.0  개포6차우성아파트1동~8동  79.97          3000               160  
46        1.0  개포6차우성아파트1동~8동  79.97          6000               140  
47        1.0  개포6차우성아파트1동~8동  79.97          5000               160

In [ ]:
df_month_rent.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 729704 entries, 25 to 2310693
Data columns (total 13 columns):
 #   Column            Non-Null Count   Dtype         
---  ------            --------------   -----         
 0   date              729704 non-null  datetime64[ns]
 1   year              729704 non-null  int64         
 2   month             729704 non-null  int64         
 3   day               729704 non-null  int64         
 4   address_0         729704 non-null  object        
 5   address_1         729704 non-null  object        
 6   address_2         729704 non-null  object        
 7   address_3         729704 non-null  float64       
 8   address_4         729704 non-null  float64       
 9   name              729704 non-null  object        
 10  area              729704 non-null  float64       
 11  rent_deposit      729704 non-null  int64         
 12  month_rent_price  729704 non-null  int64         
dtypes: datetime64[ns](1), float64(3), int64(5), object(4)
mem

> 해당 데이터프레임은 거래일자의 정보를 나타내는 'date', 'month', 'day' 컬럼들, 주소의 정보를 나타내는 'address_0', 'address_1', 'address_2', 'address_4' 컬럼들, 아파트명을 나타내는 'name'컬럼, 아파트의 면적을 나타내는 'area' 컬럼, 보증근 정보를 나타내는 'rent_deposit' 컬럼,월세가격을 나타내는 'month_rent_price' 컬럼으로 이루어져 있다

In [ ]:
df_month_rent.to_csv('/content/drive/MyDrive/house_price/after_data/apartment_month_rent.csv', index=False)

# 부동산 지수 데이터 수정

In [ ]:
import pandas as pd
df_seoul_index = pd.read_excel('/content/drive/MyDrive/house_price/original_data/주간 아파트 매매가격지수_20231027.xlsx')
df_seoul_index

지역명 2008-04-07 00:00:52 2008-04-14 00:00:52 2008-04-21 00:00:52  \
0       전국              58.013              58.089              58.198   
1       서울              59.733              59.882              60.042   
2   강북14개구              59.739               59.98               60.25   
3   강남11개구              59.899              59.966              60.029   
4      수도권              62.334              62.457              62.638   
5    6개광역시              51.272              51.335              51.404   
6    5개광역시              49.125               49.16              49.192   
7     기타지방              62.411              62.436              62.483   
8       부산              46.536              46.594               46.66   
9       대구              51.373              51.353              51.331   
10      인천              64.499              64.713              64.975   
11      광주              51.008              51.075              51.122   
12      대전              48.013              48.052              48.065   
13      울산              60.452              60.466              60.501   
14      세종                   -                   -                   -   
15      경기              64.072              64.152              64.331   
16      충북              59.666              59.684               59.69   
17      충남              65.601              65.577              65.589   
18      전북              63.885              63.979              64.113   
19      전남                69.2              69.251              69.312   
20      경북              69.386              69.398              69.425   
21      경남              62.734              62.758              62.807   
22      제주              48.928              48.932              48.962   
23      강원              61.519              61.508              61.534   

   2008-04-28 00:00:52 2008-05-05 00:00:52 2008-05-12 00:00:52  \
0               58.281              58.355              58.427   
1               60.163              60.278              60.387   
2               60.444              60.625              60.796   
3               60.086              60.143              60.197   
4               62.771              62.898              63.014   
5               51.467              51.519              51.562   
6               49.214              49.237              49.254   
7               62.537              62.557              62.603   
8               46.707              46.743              46.781   
9               51.313              51.294              51.273   
10              65.249              65.451              65.631   
11              51.159              51.216              51.265   
12               48.08              48.102              48.107   
13              60.516              60.533              60.519   
14                   -                   -                   -   
15              64.442               64.56              64.666   
16              59.699              59.716              59.731   
17              65.616              65.613              65.631   
18               64.28              64.384              64.581   
19              69.313              69.374              69.374   
20               69.46              69.353              69.345   
21              62.874               62.89              62.936   
22              48.962              48.982              49.037   
23              61.547              61.604              61.637   

   2008-05-19 00:00:52 2008-05-26 00:00:52 2008-06-02 00:00:52  ...  \
0               58.493              58.553              58.616  ...   
1               60.458              60.526              60.595  ...   
2               60.909              61.037              61.156  ...   
3               60.231              60.245              60.271  ...   
4               63.108              63.198              63.297  ...   
5               51.614              51.645              51.697  ...   
6       

In [ ]:
df_seoul_index = df_seoul_index.loc[1,:]
df_seoul_index = df_seoul_index.reset_index()
df_seoul_index

index       1
0                    지역명      서울
1    2008-04-07 00:00:52  59.733
2    2008-04-14 00:00:52  59.882
3    2008-04-21 00:00:52  60.042
4    2008-04-28 00:00:52  60.163
..                   ...     ...
779  2023-09-18 00:00:52  90.635
780  2023-09-25 00:00:52  90.681
781  2023-10-09 00:00:52  90.733
782  2023-10-16 00:00:52  90.787
783  2023-10-23 00:00:52   90.82

[784 rows x 2 columns]

In [ ]:
df_seoul_index = df_seoul_index.loc[1:,:]
df_seoul_index.columns =['date','seoul_index']
df_seoul_index = df_seoul_index.reset_index(drop=True)
print(df_seoul_index.info())
df_seoul_index

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 783 entries, 0 to 782
Data columns (total 2 columns):
 #   Column       Non-Null Count  Dtype 
---  ------       --------------  ----- 
 0   date         783 non-null    object
 1   seoul_index  783 non-null    object
dtypes: object(2)
memory usage: 12.4+ KB
None


date seoul_index
0    2008-04-07 00:00:52      59.733
1    2008-04-14 00:00:52      59.882
2    2008-04-21 00:00:52      60.042
3    2008-04-28 00:00:52      60.163
4    2008-05-05 00:00:52      60.278
..                   ...         ...
778  2023-09-18 00:00:52      90.635
779  2023-09-25 00:00:52      90.681
780  2023-10-09 00:00:52      90.733
781  2023-10-16 00:00:52      90.787
782  2023-10-23 00:00:52       90.82

[783 rows x 2 columns]

In [ ]:
df_seoul_index['date'] = df_seoul_index['date'].astype('str')
df_seoul_index['seoul_index'] = df_seoul_index['seoul_index'].astype('float')
print(df_seoul_index.info())

df_seoul_index

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 783 entries, 0 to 782
Data columns (total 2 columns):
 #   Column       Non-Null Count  Dtype  
---  ------       --------------  -----  
 0   date         783 non-null    object 
 1   seoul_index  783 non-null    float64
dtypes: float64(1), object(1)
memory usage: 12.4+ KB
None


date  seoul_index
0    2008-04-07 00:00:52       59.733
1    2008-04-14 00:00:52       59.882
2    2008-04-21 00:00:52       60.042
3    2008-04-28 00:00:52       60.163
4    2008-05-05 00:00:52       60.278
..                   ...          ...
778  2023-09-18 00:00:52       90.635
779  2023-09-25 00:00:52       90.681
780  2023-10-09 00:00:52       90.733
781  2023-10-16 00:00:52       90.787
782  2023-10-23 00:00:52       90.820

[783 rows x 2 columns]

In [ ]:
df_seoul_index['date'] = df_seoul_index['date'].str.split(' ').str[0]
print(df_seoul_index.info())

df_seoul_index

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 783 entries, 0 to 782
Data columns (total 2 columns):
 #   Column       Non-Null Count  Dtype  
---  ------       --------------  -----  
 0   date         783 non-null    object 
 1   seoul_index  783 non-null    float64
dtypes: float64(1), object(1)
memory usage: 12.4+ KB
None


date  seoul_index
0    2008-04-07       59.733
1    2008-04-14       59.882
2    2008-04-21       60.042
3    2008-04-28       60.163
4    2008-05-05       60.278
..          ...          ...
778  2023-09-18       90.635
779  2023-09-25       90.681
780  2023-10-09       90.733
781  2023-10-16       90.787
782  2023-10-23       90.820

[783 rows x 2 columns]

In [ ]:
import pandas as pd

# df_seoul_index에서 date 컬럼을 문자열로 변환 후, 앞 10자리를 추출하여 datetime으로 변환
df_seoul_index['date'] = pd.to_datetime(df_seoul_index['date'], format='%Y-%m-%d')

# 변환된 DataFrame 출력
print(df_seoul_index.info())

df_seoul_index

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 783 entries, 0 to 782
Data columns (total 2 columns):
 #   Column       Non-Null Count  Dtype         
---  ------       --------------  -----         
 0   date         783 non-null    datetime64[ns]
 1   seoul_index  783 non-null    float64       
dtypes: datetime64[ns](1), float64(1)
memory usage: 12.4 KB
None


date  seoul_index
0   2008-04-07       59.733
1   2008-04-14       59.882
2   2008-04-21       60.042
3   2008-04-28       60.163
4   2008-05-05       60.278
..         ...          ...
778 2023-09-18       90.635
779 2023-09-25       90.681
780 2023-10-09       90.733
781 2023-10-16       90.787
782 2023-10-23       90.820

[783 rows x 2 columns]

In [ ]:
df_seoul_index.to_pickle('/content/drive/MyDrive/house_price/after_data/df_seoul_index.pkl')

# economic_data.csv 파일생성

- economic_data(거시경제 정보관련) 파일 생성
- economic_data 에는 한국기준금리, 부동산지수, 기준금리, 코스피지수, 한국국채금리, 미국국채금리, 장단기금리차, 아파트 분양 공급량, 아파트 미분양수, 아파트 미분양률 의 정보를 포함함

## 기준금리 정보관련 데이터 프레임 생성

- 'https://www.bok.or.kr/portal/singl/baseRate/list.do?dataSeCd=01&menuNo=200643' 홈페이지에서 기준금리의 변경 일자들을 제공하기에 해당 사이트에서 정보를 추출

### 데이터프레임 확인

In [ ]:
import pandas as pd

df = pd.read_csv('/content/drive/MyDrive/house_price/original_data/korean_rp.csv',encoding='cp949')
print(df.info())
df.head()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 55 entries, 0 to 54
Data columns (total 3 columns):
 #   Column  Non-Null Count  Dtype  
---  ------  --------------  -----  
 0   년도      55 non-null     int64  
 1   월일      55 non-null     object 
 2   기준금리    55 non-null     float64
dtypes: float64(1), int64(1), object(1)
memory usage: 1.4+ KB
None


년도       월일  기준금리
0  2023  01월 13일  3.50
1  2022  11월 24일  3.25
2  2022  10월 12일  3.00
3  2022  08월 25일  2.50
4  2022  07월 13일  2.25

In [ ]:
df['month']=df['월일'].str[0:2] # 월의 정보만 추출
df['day'] = df['월일'].str[4:6] # 일의 정보만 추출
df.head()

년도       월일  기준금리 month day
0  2023  01월 13일  3.50    01  13
1  2022  11월 24일  3.25    11  24
2  2022  10월 12일  3.00    10  12
3  2022  08월 25일  2.50    08  25
4  2022  07월 13일  2.25    07  13

In [ ]:
df['rp_date'] = df['년도'].astype('str')+df['month']+df['day'] # 새로운 컬럼 생성
df.head()

년도       월일  기준금리 month day   rp_date
0  2023  01월 13일  3.50    01  13  20230113
1  2022  11월 24일  3.25    11  24  20221124
2  2022  10월 12일  3.00    10  12  20221012
3  2022  08월 25일  2.50    08  25  20220825
4  2022  07월 13일  2.25    07  13  20220713

In [ ]:
df = df.rename(columns={'기준금리':'korea_rp'})
df = df.drop(['년도','월일','month','day'], axis=1) # 안쓰는 컬럼 제거
df=df.sort_index(ascending=False) # 날짜가 역순으로 되어 있어서 정렬
df['rp_date'] = pd.to_datetime(df['rp_date'], format='%Y-%m-%d') # date 타입으로 변경
print(df.info())
df

<class 'pandas.core.frame.DataFrame'>
Int64Index: 55 entries, 54 to 0
Data columns (total 2 columns):
 #   Column    Non-Null Count  Dtype         
---  ------    --------------  -----         
 0   korea_rp  55 non-null     float64       
 1   rp_date   55 non-null     datetime64[ns]
dtypes: datetime64[ns](1), float64(1)
memory usage: 1.3 KB
None


korea_rp    rp_date
54      4.75 1999-05-06
53      5.00 2000-02-10
52      5.25 2000-10-05
51      5.00 2001-02-08
50      4.75 2001-07-05
49      4.50 2001-08-09
48      4.00 2001-09-19
47      4.25 2002-05-07
46      4.00 2003-05-13
45      3.75 2003-07-10
44      3.50 2004-08-12
43      3.25 2004-11-11
42      3.50 2005-10-11
41      3.75 2005-12-08
40      4.00 2006-02-09
39      4.25 2006-06-08
38      4.50 2006-08-10
37      4.75 2007-07-12
36      5.00 2007-08-09
35      5.25 2008-08-07
34      5.00 2008-10-09
33      4.25 2008-10-27
32      4.00 2008-11-07
31      3.00 2008-12-11
30      2.50 2009-01-09
29      2.00 2009-02-12
28      2.25 2010-07-09
27      2.50 2010-11-16
26      2.75 2011-01-13
25      3.00 2011-03-10
24      3.25 2011-06-10
23      3.00 2012-07-12
22      2.75 2012-10-11
21      2.50 2013-05-09
20      2.25 2014-08-14
19      2.00 2014-10-15
18      1.75 2015-03-12
17      1.50 2015-06-11
16      1.25 2016-06-09
15      1.50 2017-11-30
14      1.75 2018-11-30
13      1.50 2019-07-18
12      1.25 2019-10-16
11      0.75 2020-03-17
10      0.50 2020-05-28
9       0.75 2021-08-26
8       1.00 2021-11-25
7       1.25 2022-01-14
6       1.50 2022-04-14
5       1.75 2022-05-26
4       2.25 2022-07-13
3       2.50 2022-08-25
2       3.00 2022-10-12
1       3.25 2022-11-24
0       3.50 2023-01-13

### '기준금리 변경날짜'들 사이에 있는 날짜들의 기준금리 정보 생성

- 위에서의 데이터 프레임은 '기준금리 변경일자'와 '변경된 기준금리'의 정보를 나타내는데, '기준금리 변경일자'들 사이에 있는 모든 날짜들에 대응하는 '기준금리'에 대한 정보도 필요하기에 사이 날짜들에 대한 기준금리 정보들을 생성

In [ ]:
import datetime

# 크롤링한 날짜 기간에 있는 모든 날짜들을 계산
start = datetime.datetime.strptime("06-05-1999", "%d-%m-%Y") # 시작날짜 설정
end = datetime.datetime.strptime("31-10-2023", "%d-%m-%Y") # 끝날짜 설정정
date_generated = [start + datetime.timedelta(days=x) for x in range(0, (end-start).days)] # 시작날짜와 끝날짜 사이에 있는 날짜들 생성
date_list=list()
for date in date_generated:
    date_list.append(date.strftime("%Y-%m-%d")) # date_list 에서 생성한 날짜들의 형식을 맞춰서 대입

In [ ]:
# df_date는 조회할 모든 날짜들의 정보가 들어있는 series
df_date = pd.DataFrame({
    "date": date_list
}, columns=["date"])
df_date['date'] = pd.to_datetime(df_date['date'], format='%Y-%m-%d %H:%M:%S', errors='raise') # date 타입으로 변경

In [ ]:
df_date.head() # 데이터 프레임 형태 확인

date
0 1999-05-06
1 1999-05-07
2 1999-05-08
3 1999-05-09
4 1999-05-10

In [ ]:
# 두개의 데이터프레임 결합을 통해서 날짜별 기준금리 현황을 생성
df_rp=pd.merge(df_date, df, left_on='date', right_on='rp_date', how='left')

In [ ]:
# 사용할 컬럼만을 선택
df_rp = df_rp[['date','korea_rp']]
df_rp # 생성한 데이터 프레임 형태 확인

date  korea_rp
0    1999-05-06      4.75
1    1999-05-07       NaN
2    1999-05-08       NaN
3    1999-05-09       NaN
4    1999-05-10       NaN
...         ...       ...
8939 2023-10-26       NaN
8940 2023-10-27       NaN
8941 2023-10-28       NaN
8942 2023-10-29       NaN
8943 2023-10-30       NaN

[8944 rows x 2 columns]

In [ ]:
# 가장 최근에 변경된 기준금리가 이후 변경되기 전까지 유지가 되기에, null값들을 젤 위에 있는 값(변경된 가장 최근의 기준금리 값)들로 채움
# 일자별 기준금리의 정보들을 생성
df_rp=df_rp.ffill() # ffill() 매소드를 통해서 젤 위의 있는 값으로 null 값들을 채움
print(df_rp.info())
df_rp

<class 'pandas.core.frame.DataFrame'>
Int64Index: 8944 entries, 0 to 8943
Data columns (total 2 columns):
 #   Column    Non-Null Count  Dtype         
---  ------    --------------  -----         
 0   date      8944 non-null   datetime64[ns]
 1   korea_rp  8944 non-null   float64       
dtypes: datetime64[ns](1), float64(1)
memory usage: 209.6 KB
None


date  korea_rp
0    1999-05-06      4.75
1    1999-05-07      4.75
2    1999-05-08      4.75
3    1999-05-09      4.75
4    1999-05-10      4.75
...         ...       ...
8939 2023-10-26      3.50
8940 2023-10-27      3.50
8941 2023-10-28      3.50
8942 2023-10-29      3.50
8943 2023-10-30      3.50

[8944 rows x 2 columns]

In [ ]:
# 기준금리 현황 그래프 출력
# x축을 날짜, y축을 기준금리 값으로 한 그래프 출력력
import plotly.graph_objects as go

# Create traces
fig = go.Figure()
fig.add_trace(go.Scatter(x=df_rp['date'], y=df_rp['korea_rp'],
                    mode='lines',
                    name='korea_rp',yaxis='y1'))


fig.show(renderer="colab")

## 서울 아파트 지수 추가

In [ ]:
import pandas as pd
df_seoul_index =pd.read_pickle('/content/drive/MyDrive/house_price/after_data/df_seoul_index.pkl')
df_seoul_index.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 783 entries, 0 to 782
Data columns (total 2 columns):
 #   Column       Non-Null Count  Dtype         
---  ------       --------------  -----         
 0   date         783 non-null    datetime64[ns]
 1   seoul_index  783 non-null    float64       
dtypes: datetime64[ns](1), float64(1)
memory usage: 12.4 KB


In [ ]:
df_final = pd.merge(df_rp, df_seoul_index, on = 'date', how = 'left')
print(df_final.info())
df_final

<class 'pandas.core.frame.DataFrame'>
Int64Index: 8944 entries, 0 to 8943
Data columns (total 3 columns):
 #   Column       Non-Null Count  Dtype         
---  ------       --------------  -----         
 0   date         8944 non-null   datetime64[ns]
 1   korea_rp     8944 non-null   float64       
 2   seoul_index  783 non-null    float64       
dtypes: datetime64[ns](1), float64(2)
memory usage: 279.5 KB
None


date  korea_rp  seoul_index
0    1999-05-06      4.75          NaN
1    1999-05-07      4.75          NaN
2    1999-05-08      4.75          NaN
3    1999-05-09      4.75          NaN
4    1999-05-10      4.75          NaN
...         ...       ...          ...
8939 2023-10-26      3.50          NaN
8940 2023-10-27      3.50          NaN
8941 2023-10-28      3.50          NaN
8942 2023-10-29      3.50          NaN
8943 2023-10-30      3.50          NaN

[8944 rows x 3 columns]

In [ ]:
df_final.loc[df_final['seoul_index'].notnull(),:]

date  korea_rp  seoul_index
3259 2008-04-07       5.0       59.733
3266 2008-04-14       5.0       59.882
3273 2008-04-21       5.0       60.042
3280 2008-04-28       5.0       60.163
3287 2008-05-05       5.0       60.278
...         ...       ...          ...
8901 2023-09-18       3.5       90.635
8908 2023-09-25       3.5       90.681
8922 2023-10-09       3.5       90.733
8929 2023-10-16       3.5       90.787
8936 2023-10-23       3.5       90.820

[783 rows x 3 columns]

In [ ]:
df_final = df_final.loc[df_final['date']>='2008-04-07',:]
df_final.head(10)

date  korea_rp  seoul_index
3259 2008-04-07       5.0       59.733
3260 2008-04-08       5.0          NaN
3261 2008-04-09       5.0          NaN
3262 2008-04-10       5.0          NaN
3263 2008-04-11       5.0          NaN
3264 2008-04-12       5.0          NaN
3265 2008-04-13       5.0          NaN
3266 2008-04-14       5.0       59.882
3267 2008-04-15       5.0          NaN
3268 2008-04-16       5.0          NaN

In [ ]:
df_final['seoul_index'] = df_final['seoul_index'].interpolate(method='values')
df_final['seoul_index'] = round(df_final['seoul_index'],2)
print(df_final.info())
df_final.head(10)

<class 'pandas.core.frame.DataFrame'>
Int64Index: 5685 entries, 3259 to 8943
Data columns (total 3 columns):
 #   Column       Non-Null Count  Dtype         
---  ------       --------------  -----         
 0   date         5685 non-null   datetime64[ns]
 1   korea_rp     5685 non-null   float64       
 2   seoul_index  5685 non-null   float64       
dtypes: datetime64[ns](1), float64(2)
memory usage: 177.7 KB
None


<ipython-input-76-2fd3feec2980>:1: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

<ipython-input-76-2fd3feec2980>:2: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



date  korea_rp  seoul_index
3259 2008-04-07       5.0        59.73
3260 2008-04-08       5.0        59.75
3261 2008-04-09       5.0        59.78
3262 2008-04-10       5.0        59.80
3263 2008-04-11       5.0        59.82
3264 2008-04-12       5.0        59.84
3265 2008-04-13       5.0        59.86
3266 2008-04-14       5.0        59.88
3267 2008-04-15       5.0        59.90
3268 2008-04-16       5.0        59.93

## 데이터프레임 기간 수정

- 전세,월세에 대한 정보가 2011년 이후 부터 있기에 데이터 프레임을 2011년 ~ 으로 자름

In [ ]:
df_final = df_final[(df_final['date']>='2011-01-01') ] # 사용할 날자만 자름
print(df_final.info())
df_final

<class 'pandas.core.frame.DataFrame'>
Int64Index: 4686 entries, 4258 to 8943
Data columns (total 3 columns):
 #   Column       Non-Null Count  Dtype         
---  ------       --------------  -----         
 0   date         4686 non-null   datetime64[ns]
 1   korea_rp     4686 non-null   float64       
 2   seoul_index  4686 non-null   float64       
dtypes: datetime64[ns](1), float64(2)
memory usage: 146.4 KB
None


date  korea_rp  seoul_index
4258 2011-01-01       2.5        59.42
4259 2011-01-02       2.5        59.43
4260 2011-01-03       2.5        59.43
4261 2011-01-04       2.5        59.43
4262 2011-01-05       2.5        59.44
...         ...       ...          ...
8939 2023-10-26       3.5        90.82
8940 2023-10-27       3.5        90.82
8941 2023-10-28       3.5        90.82
8942 2023-10-29       3.5        90.82
8943 2023-10-30       3.5        90.82

[4686 rows x 3 columns]

### 기준금리(역) 과 부동산지수 비교

In [ ]:
# Create traces
fig = go.Figure()
fig.add_trace(go.Scatter(x=df_final['date'], y=df_final['korea_rp'],
                    mode='lines',
                    name='korea_rp',yaxis='y1'))
# x축으로 그래프를 뒤집음
fig.update_layout(
    yaxis = dict(autorange="reversed")
)


fig.add_trace(go.Scatter(x=df_final['date'], y=df_final['seoul_index'],
                    mode='lines',
                    name='seoul_index',
                    yaxis="y2"))
fig.update_layout(

   # create first Y-axis
   yaxis=dict(
      title="rp point",
      titlefont=dict(color="blue"),
      tickfont=dict(color="blue")
   ),

   # create second Y-axis
   yaxis2=dict(
      title="seoul_index",
      overlaying="y",
      side="right")
)

> 기준금리(역)과 부동산 지수는 연관성이 있는듯

## 코스피 지수 데이터 추가

In [ ]:
df_kospi = pd.read_csv("/content/drive/MyDrive/house_price/original_data/kospi.csv",  encoding='UTF8') # 코스피 지수 정보 불러오기
df_kospi.head()

날짜        종가        시가        고가        저가      거래량    변동 %
0  2023- 11- 10  2,409.66  2,406.40  2,413.62  2,393.64  312.47M  -0.72%
1  2023- 11- 09  2,427.08  2,425.93  2,437.90  2,413.04  395.03M   0.23%
2  2023- 11- 08  2,421.62  2,460.22  2,468.43  2,418.14  467.22M  -0.91%
3  2023- 11- 07  2,443.96  2,476.35  2,476.35  2,418.74  457.68M  -2.33%
4  2023- 11- 06  2,502.37  2,399.80  2,502.37  2,395.03  528.58M   5.66%

In [ ]:
df_kospi=df_kospi.sort_index(ascending=False) # 날짜가 역순으로 되어 있어서 정렬
df_kospi.reset_index(drop=True, inplace=True) # index 재설정
df_kospi.head()

날짜        종가        시가        고가        저가      거래량    변동 %
0  2007- 01- 02  1,435.26  1,438.89  1,439.71  1,430.06  147.74M   0.06%
1  2007- 01- 03  1,409.35  1,436.42  1,437.79  1,409.31  203.21M  -1.81%
2  2007- 01- 04  1,397.29  1,410.55  1,411.12  1,388.50  241.17M  -0.86%
3  2007- 01- 05  1,385.76  1,398.60  1,400.59  1,372.36  277.29M  -0.83%
4  2007- 01- 08  1,370.81  1,376.76  1,384.65  1,366.48  177.59M  -1.08%

In [ ]:
df_kospi.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 4168 entries, 0 to 4167
Data columns (total 7 columns):
 #   Column  Non-Null Count  Dtype 
---  ------  --------------  ----- 
 0   날짜      4168 non-null   object
 1   종가      4168 non-null   object
 2   시가      4168 non-null   object
 3   고가      4168 non-null   object
 4   저가      4168 non-null   object
 5   거래량     4168 non-null   object
 6   변동 %    4168 non-null   object
dtypes: object(7)
memory usage: 228.1+ KB


In [ ]:
# 필요한 컬럼만 선택 후, 컬럼명 수정, 타입변경경
df_kospi = df_kospi[['날짜','종가']]
df_kospi.columns = ['kospi_date','kospi_index']
df_kospi["kospi_date"] = pd.to_datetime(df_kospi["kospi_date"])
df_kospi.head()

kospi_date kospi_index
0 2007-01-02    1,435.26
1 2007-01-03    1,409.35
2 2007-01-04    1,397.29
3 2007-01-05    1,385.76
4 2007-01-08    1,370.81

In [ ]:
df_kospi.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 4168 entries, 0 to 4167
Data columns (total 2 columns):
 #   Column       Non-Null Count  Dtype         
---  ------       --------------  -----         
 0   kospi_date   4168 non-null   datetime64[ns]
 1   kospi_index  4168 non-null   object        
dtypes: datetime64[ns](1), object(1)
memory usage: 65.2+ KB


In [ ]:
# kospi_index 값을 이후 계산에 사용하기 위해서 숫자 형태로 수정
df_kospi["kospi_index"] = df_kospi["kospi_index"].str.replace(",", "") # 문자형으로 되어 있기에 , 을 제거
df_kospi = df_kospi.astype({'kospi_index': 'float64'})# 컬럼 타입 변경
df_kospi.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 4168 entries, 0 to 4167
Data columns (total 2 columns):
 #   Column       Non-Null Count  Dtype         
---  ------       --------------  -----         
 0   kospi_date   4168 non-null   datetime64[ns]
 1   kospi_index  4168 non-null   float64       
dtypes: datetime64[ns](1), float64(1)
memory usage: 65.2 KB


In [ ]:
df_kospi.head() # 데이터프레임 형태 확인

kospi_date  kospi_index
0 2007-01-02      1435.26
1 2007-01-03      1409.35
2 2007-01-04      1397.29
3 2007-01-05      1385.76
4 2007-01-08      1370.81

### 코스피 지수 데이터와 병합

In [ ]:
# 기준금리&부동산지수 데이터프레임과 코스피 지수 데이터프레임 병합합
df_final=pd.merge(df_final, df_kospi, left_on='date', right_on='kospi_date', how='left') # 두 데이터프레임을 결함
df_final.head()

date  korea_rp  seoul_index kospi_date  kospi_index
0 2011-01-01       2.5        59.42        NaT          NaN
1 2011-01-02       2.5        59.43        NaT          NaN
2 2011-01-03       2.5        59.43 2011-01-03      2070.08
3 2011-01-04       2.5        59.43 2011-01-04      2085.14
4 2011-01-05       2.5        59.44 2011-01-05      2082.55

In [ ]:
df_final.info() # 정보확인 -> 주말등 휴장일들의 존재로 kospi_date 컬럼과 kospi_index 컬럼에서 null 값들이 있음

<class 'pandas.core.frame.DataFrame'>
Int64Index: 4686 entries, 0 to 4685
Data columns (total 5 columns):
 #   Column       Non-Null Count  Dtype         
---  ------       --------------  -----         
 0   date         4686 non-null   datetime64[ns]
 1   korea_rp     4686 non-null   float64       
 2   seoul_index  4686 non-null   float64       
 3   kospi_date   3161 non-null   datetime64[ns]
 4   kospi_index  3161 non-null   float64       
dtypes: datetime64[ns](2), float64(3)
memory usage: 219.7 KB


In [ ]:
# 휴장일에는 이전의 지수값이 유지된다고 가정
# 해결방안으로 이전의 값으로 null 값을 채우기
df_final["kospi_index"]=df_final["kospi_index"].fillna(method='ffill')
df_final.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 4686 entries, 0 to 4685
Data columns (total 5 columns):
 #   Column       Non-Null Count  Dtype         
---  ------       --------------  -----         
 0   date         4686 non-null   datetime64[ns]
 1   korea_rp     4686 non-null   float64       
 2   seoul_index  4686 non-null   float64       
 3   kospi_date   3161 non-null   datetime64[ns]
 4   kospi_index  4684 non-null   float64       
dtypes: datetime64[ns](2), float64(3)
memory usage: 219.7 KB


In [ ]:
# 가장 위에 있는 null 값은 직접 찾아서(네이버 검색을 통해서서) 대입
df_final["kospi_index"] = df_final["kospi_index"].fillna(2051)
df_final.info() # 값들 대입이 되었는지 확인

<class 'pandas.core.frame.DataFrame'>
Int64Index: 4686 entries, 0 to 4685
Data columns (total 5 columns):
 #   Column       Non-Null Count  Dtype         
---  ------       --------------  -----         
 0   date         4686 non-null   datetime64[ns]
 1   korea_rp     4686 non-null   float64       
 2   seoul_index  4686 non-null   float64       
 3   kospi_date   3161 non-null   datetime64[ns]
 4   kospi_index  4686 non-null   float64       
dtypes: datetime64[ns](2), float64(3)
memory usage: 219.7 KB


In [ ]:
df_final.head() # 형태 확인

date  korea_rp  seoul_index kospi_date  kospi_index
0 2011-01-01       2.5        59.42        NaT      2051.00
1 2011-01-02       2.5        59.43        NaT      2051.00
2 2011-01-03       2.5        59.43 2011-01-03      2070.08
3 2011-01-04       2.5        59.43 2011-01-04      2085.14
4 2011-01-05       2.5        59.44 2011-01-05      2082.55

In [ ]:
# 사용할 컬럼만 설정
df_final = df_final[['date','korea_rp','seoul_index','kospi_index']]
df_final.head()

date  korea_rp  seoul_index  kospi_index
0 2011-01-01       2.5        59.42      2051.00
1 2011-01-02       2.5        59.43      2051.00
2 2011-01-03       2.5        59.43      2070.08
3 2011-01-04       2.5        59.43      2085.14
4 2011-01-05       2.5        59.44      2082.55

### 코스피지수의 필요성 그래프로 점검

In [ ]:
# Create traces
fig = go.Figure()
fig.add_trace(go.Scatter(x=df_final['date'], y=df_final['kospi_index'],
                    mode='lines',
                    name='kospi_index',yaxis='y1'))



fig.add_trace(go.Scatter(x=df_final['date'], y=df_final['seoul_index'],
                    mode='lines',
                    name='seoul_index',
                    yaxis="y2"))
fig.update_layout(

   # create first Y-axis
   yaxis=dict(
      title="kospi index",
      titlefont=dict(color="blue"),
      tickfont=dict(color="blue")
   ),

   # create second Y-axis
   yaxis2=dict(
      title="seoul index",
      overlaying="y",
      side="right")
)

> 코스피지수와 부동산 지수는 어느정도의 상관성은 있나? 그래프로 봐서는 잘 모르겠음

## 한국국채 금리 데이터 추가

- 코스피 데이터프레임 생성과정과 거의 비슷

In [ ]:
import os


dir_path = "/content/drive/MyDrive/house_price/original_data/korean_bond"
file_list = os.listdir(dir_path)
file_list.sort()
name_list = list()
df_list = list()

# 해당 폴더 안에 있는 csv 파일들을 읽어서 리스트 안에 데이터프레임들을 담음
for csv_file in file_list:
    df_list.append(pd.read_csv(dir_path+"/"+csv_file , encoding='UTF8'))
    name_list.append(csv_file.split('.')[0])
for i in range(len(df_list)):
    df_korea = df_list[i] # 파일이 잘 들어갔는지 확인
    df_korea=df_korea.sort_index(ascending=False) # 날짜가 역순으로 되어 있어서 정렬
    df_korea.reset_index(drop=True, inplace=True) # index 재설정
    df_korea = df_korea[['날짜','종가']]
    df_korea.columns = ['korea_date',name_list[i]]
    df_korea['korea_date'] = pd.to_datetime(df_korea['korea_date'])
    df_final=pd.merge(df_final, df_korea, left_on='date', right_on='korea_date', how='left')
    df_final[name_list[i]]=df_final[name_list[i]].fillna(method='ffill') # 중간 공휴일들을 처리
    df_final[name_list[i]]=df_final[name_list[i]].fillna(method='bfill') # 제일 위의 있는 값을 근처 값으로 처리
    df_final = df_final.drop(['korea_date'], axis=1)

In [ ]:
df_final.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 4686 entries, 0 to 4685
Data columns (total 11 columns):
 #   Column         Non-Null Count  Dtype         
---  ------         --------------  -----         
 0   date           4686 non-null   datetime64[ns]
 1   korea_rp       4686 non-null   float64       
 2   seoul_index    4686 non-null   float64       
 3   kospi_index    4686 non-null   float64       
 4   korea_10_year  4686 non-null   float64       
 5   korea_1_year   4686 non-null   float64       
 6   korea_20_year  4686 non-null   float64       
 7   korea_2_year   4686 non-null   float64       
 8   korea_3_year   4686 non-null   float64       
 9   korea_4_year   4686 non-null   float64       
 10  korea_5_year   4686 non-null   float64       
dtypes: datetime64[ns](1), float64(10)
memory usage: 439.3 KB


In [ ]:
# 컬럼 순서 변경
df_final = df_final[['date', 'seoul_index','kospi_index','korea_rp',
                    'korea_1_year','korea_2_year','korea_3_year','korea_4_year','korea_5_year',
                    'korea_10_year','korea_20_year']]
df_final

date  seoul_index  kospi_index  korea_rp  korea_1_year  \
0    2011-01-01        59.42      2051.00       2.5         2.810   
1    2011-01-02        59.43      2051.00       2.5         2.810   
2    2011-01-03        59.43      2070.08       2.5         2.810   
3    2011-01-04        59.43      2085.14       2.5         2.830   
4    2011-01-05        59.44      2082.55       2.5         2.800   
...         ...          ...          ...       ...           ...   
4681 2023-10-26        90.82      2299.08       3.5         3.833   
4682 2023-10-27        90.82      2302.81       3.5         3.813   
4683 2023-10-28        90.82      2302.81       3.5         3.813   
4684 2023-10-29        90.82      2302.81       3.5         3.813   
4685 2023-10-30        90.82      2310.55       3.5         3.815   

      korea_2_year  korea_3_year  korea_4_year  korea_5_year  korea_10_year  \
0            3.400         3.440         4.090         4.140          4.570   
1            3.400         3.440         4.090         4.140          4.570   
2            3.400         3.440         4.090         4.140          4.570   
3            3.370         3.495         4.160         4.200          4.580   
4            3.420         3.495         4.150         4.170          4.630   
...            ...           ...           ...           ...            ...   
4681         3.995         3.692         4.218         3.608          3.977   
4682         3.979         3.692         4.169         3.608          3.977   
4683         3.973         3.692         4.169         3.608          3.977   
4684         3.973         3.692         4.169         3.608          3.977   
4685         3.996         3.692         4.180         3.608          3.977   

      korea_20_year  
0             4.730  
1             4.730  
2             4.730  
3             4.740  
4             4.750  
...             ...  
4681          4.254  
4682          4.095  
4683          4.085  
4684          4.085  
4685          4.142  

[4686 rows x 11 columns]

In [ ]:
# 년,월,일일 컬럼 생성
df_final['year'] = df_final['date'].dt.year
df_final['month'] = df_final['date'].dt.month
df_final['day'] = df_final['date'].dt.day
df_final.head()

date  seoul_index  kospi_index  korea_rp  korea_1_year  korea_2_year  \
0 2011-01-01        59.42      2051.00       2.5          2.81          3.40   
1 2011-01-02        59.43      2051.00       2.5          2.81          3.40   
2 2011-01-03        59.43      2070.08       2.5          2.81          3.40   
3 2011-01-04        59.43      2085.14       2.5          2.83          3.37   
4 2011-01-05        59.44      2082.55       2.5          2.80          3.42   

   korea_3_year  korea_4_year  korea_5_year  korea_10_year  korea_20_year  \
0         3.440          4.09          4.14           4.57           4.73   
1         3.440          4.09          4.14           4.57           4.73   
2         3.440          4.09          4.14           4.57           4.73   
3         3.495          4.16          4.20           4.58           4.74   
4         3.495          4.15          4.17           4.63           4.75   

   year  month  day  
0  2011      1    1  
1  2011      1    2  
2  2011      1    3  
3  2011      1    4  
4  2011      1    5

### 부동산지수와 한국국채금리 시각화

In [ ]:
fig = go.Figure()
fig.add_trace(go.Scatter(x=df_final['date'], y=df_final['korea_rp'],
                    mode='lines',
                    name='korea_rp',yaxis='y1'))

fig.add_trace(go.Scatter(x=df_final['date'], y=df_final['korea_1_year'],
                    mode='lines',
                    name='korea_1_year',yaxis='y1'))

fig.add_trace(go.Scatter(x=df_final['date'], y=df_final['korea_2_year'],
                    mode='lines',
                    name='korea_2_year',yaxis='y1'))

fig.add_trace(go.Scatter(x=df_final['date'], y=df_final['korea_3_year'],
                    mode='lines',
                    name='korea_3_year',yaxis='y1'))

fig.add_trace(go.Scatter(x=df_final['date'], y=df_final['korea_4_year'],
                    mode='lines',
                    name='korea_4_year',yaxis='y1'))

fig.add_trace(go.Scatter(x=df_final['date'], y=df_final['korea_5_year'],
                    mode='lines',
                    name='korea_5_year',yaxis='y1'))

fig.add_trace(go.Scatter(x=df_final['date'], y=df_final['korea_10_year'],
                    mode='lines',
                    name='korea_10_year',yaxis='y1'))

fig.add_trace(go.Scatter(x=df_final['date'], y=df_final['korea_20_year'],
                    mode='lines',
                    name='korea_20_year',yaxis='y1'))

# 앞에서의 그래프들은 뒤집기
fig.update_layout(
    yaxis = dict(autorange="reversed")
)
fig.add_trace(go.Scatter(x=df_final['date'], y=df_final['seoul_index'],
                    mode='lines',
                    name='seoul_index',
                    yaxis="y2"))
fig.update_layout(

   # create first Y-axis
   yaxis=dict(
      title="rate index",
      titlefont=dict(color="black"),
      tickfont=dict(color="black")
   ),

   # create second Y-axis
   yaxis2=dict(
      title="apartment index",
      overlaying="y",
      side="right")
)

> 한국국채금리(역)과 부동산지수는 연관이 있는듯

In [ ]:
# 금리들이 얼추 비슷한 흐름을 보임으로 국채에서 3년과 10년만 사용
df_final = df_final[['date','year','month','day','seoul_index','kospi_index','korea_rp',
                    'korea_3_year','korea_10_year']]
df_final.head()

date  year  month  day  seoul_index  kospi_index  korea_rp  \
0 2011-01-01  2011      1    1        59.42      2051.00       2.5   
1 2011-01-02  2011      1    2        59.43      2051.00       2.5   
2 2011-01-03  2011      1    3        59.43      2070.08       2.5   
3 2011-01-04  2011      1    4        59.43      2085.14       2.5   
4 2011-01-05  2011      1    5        59.44      2082.55       2.5   

   korea_3_year  korea_10_year  
0         3.440           4.57  
1         3.440           4.57  
2         3.440           4.57  
3         3.495           4.58  
4         3.495           4.63

## 미국금채 금리 데이터 추가

- 한국국채금리 데이터프레임 생성과정과 거의 동일

In [ ]:
# 변수들 초기화
dir_path = "/content/drive/MyDrive/house_price/original_data/us_bond"
file_list = os.listdir(dir_path)
file_list.sort()
name_list = list()
df_list = list()

# 해당 폴더 안에 있는 csv 파일들을 읽어서 리스트 안에 데이터프레임들을 담음
for csv_file in file_list:
    df_list.append(pd.read_csv(dir_path+"/"+csv_file , encoding='UTF8'))
    name_list.append(csv_file.split('.')[0])
for i in range(len(df_list)):
    df_us = df_list[i]
    df_us=df_us.sort_index(ascending=False) # 날짜가 역순으로 되어 있어서 정렬
    df_us.reset_index(drop=True, inplace=True) # index 재설정
    df_us = df_us[['날짜','종가']]
    df_us.columns = ['us_date',name_list[i]]
    df_us['us_date'] = pd.to_datetime(df_us['us_date'])
    df_final=pd.merge(df_final, df_us, left_on='date', right_on='us_date', how='left')
    df_final[name_list[i]]=df_final[name_list[i]].fillna(method='ffill') # 중간 공휴일들을 처리
    df_final[name_list[i]]=df_final[name_list[i]].fillna(method='bfill') # 제일 위의 있는 값을 근처 값으로 처리
    df_final = df_final.drop(['us_date'], axis=1)

In [ ]:
df_final.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 4686 entries, 0 to 4685
Data columns (total 17 columns):
 #   Column         Non-Null Count  Dtype         
---  ------         --------------  -----         
 0   date           4686 non-null   datetime64[ns]
 1   year           4686 non-null   int64         
 2   month          4686 non-null   int64         
 3   day            4686 non-null   int64         
 4   seoul_index    4686 non-null   float64       
 5   kospi_index    4686 non-null   float64       
 6   korea_rp       4686 non-null   float64       
 7   korea_3_year   4686 non-null   float64       
 8   korea_10_year  4686 non-null   float64       
 9   us_10_year     4686 non-null   float64       
 10  us_1_month     4686 non-null   float64       
 11  us_2_year      4686 non-null   float64       
 12  us_30_year     4686 non-null   float64       
 13  us_3_month     4686 non-null   float64       
 14  us_3_year      4686 non-null   float64       
 15  us_5_year      4686 n

In [ ]:
df_final = df_final[['date','year','month','day','seoul_index','kospi_index','korea_rp',
                    'korea_3_year','korea_10_year','us_1_month','us_3_month',
                    'us_6_month','us_2_year', 'us_3_year', 'us_5_year',
                    'us_10_year','us_30_year']]

In [ ]:
df_final.head()

date  year  month  day  seoul_index  kospi_index  korea_rp  \
0 2011-01-01  2011      1    1        59.42      2051.00       2.5   
1 2011-01-02  2011      1    2        59.43      2051.00       2.5   
2 2011-01-03  2011      1    3        59.43      2070.08       2.5   
3 2011-01-04  2011      1    4        59.43      2085.14       2.5   
4 2011-01-05  2011      1    5        59.44      2082.55       2.5   

   korea_3_year  korea_10_year  us_1_month  us_3_month  us_6_month  us_2_year  \
0         3.440           4.57       0.096       0.124       0.183      0.601   
1         3.440           4.57       0.096       0.124       0.183      0.601   
2         3.440           4.57       0.096       0.124       0.183      0.601   
3         3.495           4.58       0.106       0.142       0.187      0.621   
4         3.495           4.63       0.129       0.142       0.184      0.708   

   us_3_year  us_5_year  us_10_year  us_30_year  
0      1.006      2.011       3.334       4.401  
1      1.006      2.011       3.334       4.401  
2      1.006      2.011       3.334       4.401  
3      1.026      2.016       3.338       4.422  
4      1.129      2.133       3.463       4.541

### 미국국채금리와 부동산 지수 비교

In [ ]:
fig = go.Figure()
fig.add_trace(go.Scatter(x=df_final['date'], y=df_final['us_1_month'],
                    mode='lines',
                    name='us_1_month',yaxis='y1'))

fig.add_trace(go.Scatter(x=df_final['date'], y=df_final['us_3_month'],
                    mode='lines',
                    name='us_3_month',yaxis='y1'))

fig.add_trace(go.Scatter(x=df_final['date'], y=df_final['us_6_month'],
                    mode='lines',
                    name='us_6_month',yaxis='y1'))

fig.add_trace(go.Scatter(x=df_final['date'], y=df_final['us_2_year'],
                    mode='lines',
                    name='us_2_year',yaxis='y1'))

fig.add_trace(go.Scatter(x=df_final['date'], y=df_final['us_3_year'],
                    mode='lines',
                    name='us_3_year',yaxis='y1'))

fig.add_trace(go.Scatter(x=df_final['date'], y=df_final['us_5_year'],
                    mode='lines',
                    name='us_5_year',yaxis='y1'))

fig.add_trace(go.Scatter(x=df_final['date'], y=df_final['us_10_year'],
                    mode='lines',
                    name='us_10_year',yaxis='y1'))

fig.add_trace(go.Scatter(x=df_final['date'], y=df_final['us_30_year'],
                    mode='lines',
                    name='us_30_year',yaxis='y1'))

# 앞에서의 그래프들은 뒤집기
fig.update_layout(
    yaxis = dict(autorange="reversed")
)
fig.add_trace(go.Scatter(x=df_final['date'], y=df_final['seoul_index'],
                    mode='lines',
                    name='seoul_index',
                    yaxis="y2"))
fig.update_layout(

   # create first Y-axis
   yaxis=dict(
      title="rate index",
      titlefont=dict(color="black"),
      tickfont=dict(color="black")
   ),

   # create second Y-axis
   yaxis2=dict(
      title="seoul index",
      overlaying="y",
      side="right")
)

> 미국 국채금리(역)은 한국 국채금리(역)보다는 부동산지수와 어느정도 연관이 있는듯?

In [ ]:
# 금리들이 얼추 비슷한 흐름을 보임으로 국채에서 3개월, 2년, 10년 데이터프레임을 생성
df_final = df_final[['date','year','month','day','kospi_index','korea_rp',
                    'korea_3_year','korea_10_year','us_3_month', 'us_2_year', 'us_10_year']]
df_final.head()

date  year  month  day  kospi_index  korea_rp  korea_3_year  \
0 2011-01-01  2011      1    1      2051.00       2.5         3.440   
1 2011-01-02  2011      1    2      2051.00       2.5         3.440   
2 2011-01-03  2011      1    3      2070.08       2.5         3.440   
3 2011-01-04  2011      1    4      2085.14       2.5         3.495   
4 2011-01-05  2011      1    5      2082.55       2.5         3.495   

   korea_10_year  us_3_month  us_2_year  us_10_year  
0           4.57       0.124      0.601       3.334  
1           4.57       0.124      0.601       3.334  
2           4.57       0.124      0.601       3.334  
3           4.58       0.142      0.621       3.338  
4           4.63       0.142      0.708       3.463

## 파일저장

In [ ]:
df_final.to_csv('/content/drive/MyDrive/house_price/after_data/economic_data.csv',index=False)

# economic_data2.csv 파일생성

- economic_data2 파일은 economic_data 파일에 금리차, 아파트 분양 공급량, 미분양 정보들을 추가한 파일

In [ ]:
import pandas as pd
df_economic = pd.read_csv('/content/drive/MyDrive/house_price/after_data/economic_data.csv')
df_economic

date  year  month  day  kospi_index  korea_rp  korea_3_year  \
0     2011-01-01  2011      1    1      2051.00       2.5         3.440   
1     2011-01-02  2011      1    2      2051.00       2.5         3.440   
2     2011-01-03  2011      1    3      2070.08       2.5         3.440   
3     2011-01-04  2011      1    4      2085.14       2.5         3.495   
4     2011-01-05  2011      1    5      2082.55       2.5         3.495   
...          ...   ...    ...  ...          ...       ...           ...   
4681  2023-10-26  2023     10   26      2299.08       3.5         3.692   
4682  2023-10-27  2023     10   27      2302.81       3.5         3.692   
4683  2023-10-28  2023     10   28      2302.81       3.5         3.692   
4684  2023-10-29  2023     10   29      2302.81       3.5         3.692   
4685  2023-10-30  2023     10   30      2310.55       3.5         3.692   

      korea_10_year  us_3_month  us_2_year  us_10_year  
0             4.570       0.124      0.601       3.334  
1             4.570       0.124      0.601       3.334  
2             4.570       0.124      0.601       3.334  
3             4.580       0.142      0.621       3.338  
4             4.630       0.142      0.708       3.463  
...             ...         ...        ...         ...  
4681          3.977       5.479      5.046       4.849  
4682          3.977       5.477      5.015       4.845  
4683          3.977       5.477      5.015       4.845  
4684          3.977       5.477      5.015       4.845  
4685          3.977       5.481      5.050       4.888  

[4686 rows x 11 columns]


## 금리차 컬럼들 추가

In [ ]:
# 금리차 컬럼들을 추가
df_economic['korea_10-3_year'] = df_economic['korea_10_year'] - df_economic['korea_3_year']
df_economic['us_10-2_year'] = df_economic['us_10_year'] - df_economic['us_2_year']
df_economic['us_10-3_year_month'] = df_economic['us_10_year'] - df_economic['us_3_month']
df_economic

date  year  month  day  kospi_index  korea_rp  korea_3_year  \
0     2011-01-01  2011      1    1      2051.00       2.5         3.440   
1     2011-01-02  2011      1    2      2051.00       2.5         3.440   
2     2011-01-03  2011      1    3      2070.08       2.5         3.440   
3     2011-01-04  2011      1    4      2085.14       2.5         3.495   
4     2011-01-05  2011      1    5      2082.55       2.5         3.495   
...          ...   ...    ...  ...          ...       ...           ...   
4681  2023-10-26  2023     10   26      2299.08       3.5         3.692   
4682  2023-10-27  2023     10   27      2302.81       3.5         3.692   
4683  2023-10-28  2023     10   28      2302.81       3.5         3.692   
4684  2023-10-29  2023     10   29      2302.81       3.5         3.692   
4685  2023-10-30  2023     10   30      2310.55       3.5         3.692   

      korea_10_year  us_3_month  us_2_year  us_10_year  korea_10-3_year  \
0             4.570       0.124      0.601       3.334            1.130   
1             4.570       0.124      0.601       3.334            1.130   
2             4.570       0.124      0.601       3.334            1.130   
3             4.580       0.142      0.621       3.338            1.085   
4             4.630       0.142      0.708       3.463            1.135   
...             ...         ...        ...         ...              ...   
4681          3.977       5.479      5.046       4.849            0.285   
4682          3.977       5.477      5.015       4.845            0.285   
4683          3.977       5.477      5.015       4.845            0.285   
4684          3.977       5.477      5.015       4.845            0.285   
4685          3.977       5.481      5.050       4.888            0.285   

      us_10-2_year  us_10-3_year_month  
0            2.733               3.210  
1            2.733               3.210  
2            2.733               3.210  
3            2.717               3.196  
4            2.755               3.321  
...            ...                 ...  
4681        -0.197              -0.630  
4682        -0.170              -0.632  
4683        -0.170              -0.632  
4684        -0.170              -0.632  
4685        -0.162              -0.593  

[4686 rows x 14 columns]

## 아파트 공급량 관련 데이터 추가

### 아파트 분양 공급 데이터 추가

- https://data.kbland.kr/publicdata/housing-supply 사이트를 통해서 아파트 공급량의 정보를 직접 얻음

In [ ]:
import pandas as pd
# txt 파일을 불러옴옴
df_apartment_supply = pd.read_csv("/content/drive/MyDrive/house_price/original_data/apartment_supply.csv",  encoding='cp949')
df_apartment_supply = df_apartment_supply.dropna()
print(df_apartment_supply.info())
df_apartment_supply

<class 'pandas.core.frame.DataFrame'>
Int64Index: 168 entries, 0 to 167
Data columns (total 4 columns):
 #   Column       Non-Null Count  Dtype  
---  ------       --------------  -----  
 0   year_month   168 non-null    float64
 1   general      168 non-null    object 
 2   combination  168 non-null    object 
 3   etc          168 non-null    object 
dtypes: float64(1), object(3)
memory usage: 6.6+ KB
None


year_month general combination    etc
0         10.01       0           0      0
1         10.02   1,199         147    506
2         10.03      31          96      0
3         10.04     148           0      0
4         10.05     102           0      0
..          ...     ...         ...    ...
163       23.08   1,191         167    127
164       23.09     222         492      0
165       23.10   2,242         452  5,215
166       23.11     299          70      0
167       23.12     187           0    294

[168 rows x 4 columns]

In [ ]:
df_apartment_supply["general"] = df_apartment_supply["general"].str.replace(",", "")
df_apartment_supply["combination"] = df_apartment_supply["combination"].str.replace(",", "")
df_apartment_supply["etc"] = df_apartment_supply["etc"].str.replace(",", "")
df_apartment_supply[['general', 'combination', 'etc']] = df_apartment_supply[['general', 'combination', 'etc']].astype(int)
df_apartment_supply['year_month'] = df_apartment_supply['year_month'].astype(str)
print(df_apartment_supply.info())

<class 'pandas.core.frame.DataFrame'>
Int64Index: 168 entries, 0 to 167
Data columns (total 4 columns):
 #   Column       Non-Null Count  Dtype 
---  ------       --------------  ----- 
 0   year_month   168 non-null    object
 1   general      168 non-null    int64 
 2   combination  168 non-null    int64 
 3   etc          168 non-null    int64 
dtypes: int64(3), object(1)
memory usage: 6.6+ KB
None


In [ ]:
df_apartment_supply['year_month'].unique()

array(['10.01', '10.02', '10.03', '10.04', '10.05', '10.06', '10.07',
       '10.08', '10.09', '10.1', '10.11', '10.12', '11.01', '11.02',
       '11.03', '11.04', '11.05', '11.06', '11.07', '11.08', '11.09',
       '11.1', '11.11', '11.12', '12.01', '12.02', '12.03', '12.04',
       '12.05', '12.06', '12.07', '12.08', '12.09', '12.1', '12.11',
       '12.12', '13.01', '13.02', '13.03', '13.04', '13.05', '13.06',
       '13.07', '13.08', '13.09', '13.1', '13.11', '13.12', '14.01',
       '14.02', '14.03', '14.04', '14.05', '14.06', '14.07', '14.08',
       '14.09', '14.1', '14.11', '14.12', '15.01', '15.02', '15.03',
       '15.04', '15.05', '15.06', '15.07', '15.08', '15.09', '15.1',
       '15.11', '15.12', '16.01', '16.02', '16.03', '16.04', '16.05',
       '16.06', '16.07', '16.08', '16.09', '16.1', '16.11', '16.12',
       '17.01', '17.02', '17.03', '17.04', '17.05', '17.06', '17.07',
       '17.08', '17.09', '17.1', '17.11', '17.12', '18.01', '18.02',
       '18.03', '18.04', '18

In [ ]:
df_apartment_supply.loc[df_apartment_supply['year_month'].str.len() == 4, 'year_month'] = df_apartment_supply['year_month']+'0'

In [ ]:
df_apartment_supply['year_month'].unique()

array(['10.01', '10.02', '10.03', '10.04', '10.05', '10.06', '10.07',
       '10.08', '10.09', '10.10', '10.11', '10.12', '11.01', '11.02',
       '11.03', '11.04', '11.05', '11.06', '11.07', '11.08', '11.09',
       '11.10', '11.11', '11.12', '12.01', '12.02', '12.03', '12.04',
       '12.05', '12.06', '12.07', '12.08', '12.09', '12.10', '12.11',
       '12.12', '13.01', '13.02', '13.03', '13.04', '13.05', '13.06',
       '13.07', '13.08', '13.09', '13.10', '13.11', '13.12', '14.01',
       '14.02', '14.03', '14.04', '14.05', '14.06', '14.07', '14.08',
       '14.09', '14.10', '14.11', '14.12', '15.01', '15.02', '15.03',
       '15.04', '15.05', '15.06', '15.07', '15.08', '15.09', '15.10',
       '15.11', '15.12', '16.01', '16.02', '16.03', '16.04', '16.05',
       '16.06', '16.07', '16.08', '16.09', '16.10', '16.11', '16.12',
       '17.01', '17.02', '17.03', '17.04', '17.05', '17.06', '17.07',
       '17.08', '17.09', '17.10', '17.11', '17.12', '18.01', '18.02',
       '18.03', '18.

In [ ]:
df_apartment_supply['total'] = df_apartment_supply['general'] + df_apartment_supply['combination'] + df_apartment_supply['etc']

print(df_apartment_supply.info())
df_apartment_supply

<class 'pandas.core.frame.DataFrame'>
Int64Index: 168 entries, 0 to 167
Data columns (total 5 columns):
 #   Column       Non-Null Count  Dtype 
---  ------       --------------  ----- 
 0   year_month   168 non-null    object
 1   general      168 non-null    int64 
 2   combination  168 non-null    int64 
 3   etc          168 non-null    int64 
 4   total        168 non-null    int64 
dtypes: int64(4), object(1)
memory usage: 11.9+ KB
None


year_month  general  combination   etc  total
0        10.01        0            0     0      0
1        10.02     1199          147   506   1852
2        10.03       31           96     0    127
3        10.04      148            0     0    148
4        10.05      102            0     0    102
..         ...      ...          ...   ...    ...
163      23.08     1191          167   127   1485
164      23.09      222          492     0    714
165      23.10     2242          452  5215   7909
166      23.11      299           70     0    369
167      23.12      187            0   294    481

[168 rows x 5 columns]

In [ ]:
# 연, 월 컬럼 생성
df_apartment_supply['year'] =df_apartment_supply["year_month"].str.split('.',expand=True)[0]
df_apartment_supply['month'] =df_apartment_supply["year_month"].str.split('.',expand=True)[1]

# 연 컬럼 수정 및 사용할 컬럼 선택
df_apartment_supply['year'] = '20'+df_apartment_supply['year']

df_apartment_supply = df_apartment_supply.astype({'year':'int', 'month':'int'})

df_apartment_supply = df_apartment_supply[['year','month','general',	'combination',	'etc',	'total']]

print(df_apartment_supply.info())
display(df_apartment_supply.head())

<class 'pandas.core.frame.DataFrame'>
Int64Index: 168 entries, 0 to 167
Data columns (total 6 columns):
 #   Column       Non-Null Count  Dtype
---  ------       --------------  -----
 0   year         168 non-null    int64
 1   month        168 non-null    int64
 2   general      168 non-null    int64
 3   combination  168 non-null    int64
 4   etc          168 non-null    int64
 5   total        168 non-null    int64
dtypes: int64(6)
memory usage: 13.3 KB
None


year  month  general  combination  etc  total
0  2010      1        0            0    0      0
1  2010      2     1199          147  506   1852
2  2010      3       31           96    0    127
3  2010      4      148            0    0    148
4  2010      5      102            0    0    102

- 해당 달의 수치의 결과는 다음달에 발표한다고 가정(예를들어 2011년 1월의 거래수치는 2011년 1월동안에는 알 수 없고 2월이 되어야 1월의 결과를 종합해서 수치를 알 수 있다)

In [ ]:
# 한 칸씩 옮
df_apartment_supply[['general','combination', 'etc', 'total']] = df_apartment_supply[['general','combination', 'etc', 'total']].shift(1)
df_apartment_supply

year  month  general  combination     etc   total
0    2010      1      NaN          NaN     NaN     NaN
1    2010      2      0.0          0.0     0.0     0.0
2    2010      3   1199.0        147.0   506.0  1852.0
3    2010      4     31.0         96.0     0.0   127.0
4    2010      5    148.0          0.0     0.0   148.0
..    ...    ...      ...          ...     ...     ...
163  2023      8   1169.0        226.0   432.0  1827.0
164  2023      9   1191.0        167.0   127.0  1485.0
165  2023     10    222.0        492.0     0.0   714.0
166  2023     11   2242.0        452.0  5215.0  7909.0
167  2023     12    299.0         70.0     0.0   369.0

[168 rows x 6 columns]

In [ ]:
df_apartment_supply = df_apartment_supply.dropna()
df_apartment_supply = df_apartment_supply.reset_index(drop=True)
df_apartment_supply

year  month  general  combination     etc   total
0    2010      2      0.0          0.0     0.0     0.0
1    2010      3   1199.0        147.0   506.0  1852.0
2    2010      4     31.0         96.0     0.0   127.0
3    2010      5    148.0          0.0     0.0   148.0
4    2010      6    102.0          0.0     0.0   102.0
..    ...    ...      ...          ...     ...     ...
162  2023      8   1169.0        226.0   432.0  1827.0
163  2023      9   1191.0        167.0   127.0  1485.0
164  2023     10    222.0        492.0     0.0   714.0
165  2023     11   2242.0        452.0  5215.0  7909.0
166  2023     12    299.0         70.0     0.0   369.0

[167 rows x 6 columns]

In [ ]:
df_apartment_supply = df_apartment_supply.rename(columns={'year':'announcement_year', 'month':'announcement_month', 'general':'general_supply',
                                                          'combination':'combination_supply', 'etc':'etc_supply', 'total':'total_supply'})
df_apartment_supply.head()

announcement_year  announcement_month  general_supply  combination_supply  \
0               2010                   2             0.0                 0.0   
1               2010                   3          1199.0               147.0   
2               2010                   4            31.0                96.0   
3               2010                   5           148.0                 0.0   
4               2010                   6           102.0                 0.0   

   etc_supply  total_supply  
0         0.0           0.0  
1       506.0        1852.0  
2         0.0         127.0  
3         0.0         148.0  
4         0.0         102.0

###| 아파트 미분양 데이터 추가

- https://data.kbland.kr/publicdata/unsold-apartments 사이트를 통해서 미분양 데이터 정보를 확보

In [ ]:
df_apartment_unsold = pd.read_excel("/content/drive/MyDrive/house_price/original_data/unsold/서울 미분양 현황.xlsx")
df_apartment_unsold.head()

구분 '07.01    '07.02    '07.03    '07.04    '07.05    '07.06    '07.07  \
0  미분양  72831  73546.00  73162.00  73393.00  78571.00  89924.00  90658.00   
1  변동률      -      0.98     -0.52      0.32      7.06     14.45      0.82   

     '07.08    '07.09  ...    '22.12    '23.01   '23.02    '23.03    '23.04  \
0  91714.00  98235.00  ...  68107.00  75359.00  75438.0  72104.00  71365.00   
1      1.16      7.11  ...     17.37     10.65      0.1     -4.42     -1.02   

    '23.05   '23.06    '23.07    '23.08    '23.09  
0  68865.0  66388.0  63087.00  61811.00  59806.00  
1     -3.5     -3.6     -4.97     -2.02     -3.24  

[2 rows x 202 columns]

In [ ]:
import numpy as np
df_apartment_unsold["'23.10"] = [0,np.nan]
df_apartment_unsold.head()

구분 '07.01    '07.02    '07.03    '07.04    '07.05    '07.06    '07.07  \
0  미분양  72831  73546.00  73162.00  73393.00  78571.00  89924.00  90658.00   
1  변동률      -      0.98     -0.52      0.32      7.06     14.45      0.82   

     '07.08    '07.09  ...    '23.01   '23.02    '23.03    '23.04   '23.05  \
0  91714.00  98235.00  ...  75359.00  75438.0  72104.00  71365.00  68865.0   
1      1.16      7.11  ...     10.65      0.1     -4.42     -1.02     -3.5   

    '23.06    '23.07    '23.08    '23.09  '23.10  
0  66388.0  63087.00  61811.00  59806.00     0.0  
1     -3.6     -4.97     -2.02     -3.24     NaN  

[2 rows x 203 columns]

In [ ]:
df_apartment_unsold = df_apartment_unsold.set_index('구분') # '구분'커럼을 인덱스로 설정
df_apartment_unsold.head()

'07.01    '07.02    '07.03    '07.04    '07.05    '07.06    '07.07  \
구분                                                                       
미분양  72831  73546.00  73162.00  73393.00  78571.00  89924.00  90658.00   
변동률      -      0.98     -0.52      0.32      7.06     14.45      0.82   

       '07.08    '07.09    '07.10  ...    '23.01   '23.02    '23.03    '23.04  \
구분                                 ...                                          
미분양  91714.00  98235.00  100887.0  ...  75359.00  75438.0  72104.00  71365.00   
변동률      1.16      7.11       2.7  ...     10.65      0.1     -4.42     -1.02   

      '23.05   '23.06    '23.07    '23.08    '23.09  '23.10  
구분                                                           
미분양  68865.0  66388.0  63087.00  61811.00  59806.00     0.0  
변동률     -3.5     -3.6     -4.97     -2.02     -3.24     NaN  

[2 rows x 202 columns]

In [ ]:
# T 매소드를 통해서 row와 column을 교환환
df_apartment_unsold=df_apartment_unsold.T
df_apartment_unsold.head()

구분          미분양   변동률
'07.01    72831     -
'07.02  73546.0  0.98
'07.03  73162.0 -0.52
'07.04  73393.0  0.32
'07.05  78571.0  7.06

In [ ]:
df_apartment_unsold.info()

<class 'pandas.core.frame.DataFrame'>
Index: 202 entries, '07.01 to '23.10
Data columns (total 2 columns):
 #   Column  Non-Null Count  Dtype 
---  ------  --------------  ----- 
 0   미분양     202 non-null    object
 1   변동률     201 non-null    object
dtypes: object(2)
memory usage: 12.8+ KB


In [ ]:
# index가 날짜의 정보를 가지고 있음으로 reset_index를 통해서 날짜 정보를 컬럼으로 생성성
df_apartment_unsold = df_apartment_unsold.reset_index()
df_apartment_unsold.head()

구분   index      미분양   변동률
0   '07.01    72831     -
1   '07.02  73546.0  0.98
2   '07.03  73162.0 -0.52
3   '07.04  73393.0  0.32
4   '07.05  78571.0  7.06

In [ ]:
# 컬럼명 수정정
df_apartment_unsold.columns=['year_month','unsold_count','ratio']
df_apartment_unsold.head()

year_month unsold_count ratio
0     '07.01        72831     -
1     '07.02      73546.0  0.98
2     '07.03      73162.0 -0.52
3     '07.04      73393.0  0.32
4     '07.05      78571.0  7.06

In [ ]:
# year_month 컬럼에서 ' 부분을 제거
df_apartment_unsold["year_month"] = df_apartment_unsold["year_month"].str.replace("'", "")
df_apartment_unsold.head()

year_month unsold_count ratio
0      07.01        72831     -
1      07.02      73546.0  0.98
2      07.03      73162.0 -0.52
3      07.04      73393.0  0.32
4      07.05      78571.0  7.06

In [ ]:
# 연, 월 컬럼 생성
df_apartment_unsold['year'] =df_apartment_unsold["year_month"].str.split('.',expand=True)[0]
df_apartment_unsold['month'] =df_apartment_unsold["year_month"].str.split('.',expand=True)[1]
df_apartment_unsold.head()

year_month unsold_count ratio year month
0      07.01        72831     -   07    01
1      07.02      73546.0  0.98   07    02
2      07.03      73162.0 -0.52   07    03
3      07.04      73393.0  0.32   07    04
4      07.05      78571.0  7.06   07    05

In [ ]:
# 연 컬럼 수정 및 사용할 컬럼 선택
df_apartment_unsold['year'] = '20'+df_apartment_unsold['year']
df_apartment_unsold = df_apartment_unsold[['year','month','unsold_count']]
df_apartment_unsold

year month unsold_count
0    2007    01        72831
1    2007    02      73546.0
2    2007    03      73162.0
3    2007    04      73393.0
4    2007    05      78571.0
..    ...   ...          ...
197  2023    06      66388.0
198  2023    07      63087.0
199  2023    08      61811.0
200  2023    09      59806.0
201  2023    10          0.0

[202 rows x 3 columns]

In [ ]:
import datetime

# 미분양에 대한 정보는 한달이 지나야 결과를 알 수 있다 가정
df_apartment_unsold['date'] = pd.to_datetime(df_apartment_unsold['year']+'-'+df_apartment_unsold['month'], format="%Y-%m")
df_apartment_unsold['date_column'] = df_apartment_unsold['date'] + datetime.timedelta(days=32) # 한달 뒤의 날짜를 구함(발표날짜)
df_apartment_unsold['announcement_year'] = df_apartment_unsold['date_column'].dt.year
df_apartment_unsold['announcement_month'] = df_apartment_unsold['date_column'].dt.month
df_apartment_unsold = df_apartment_unsold[['announcement_year','announcement_month','unsold_count']]
df_apartment_unsold = df_apartment_unsold.astype({'unsold_count': 'int64'})
df_apartment_unsold

announcement_year  announcement_month  unsold_count
0                 2007                   2         72831
1                 2007                   3         73546
2                 2007                   4         73162
3                 2007                   5         73393
4                 2007                   6         78571
..                 ...                 ...           ...
197               2023                   7         66388
198               2023                   8         63087
199               2023                   9         61811
200               2023                  10         59806
201               2023                  11             0

[202 rows x 3 columns]

In [ ]:
# 사용할 연도의 범위를 설정
df_apartment_unsold=df_apartment_unsold[df_apartment_unsold['announcement_year']>=2011]
df_apartment_unsold = df_apartment_unsold.drop(df_apartment_unsold[(df_apartment_unsold['announcement_year'] == 2023) & (df_apartment_unsold['announcement_month'] == 11)].index)

df_apartment_unsold

announcement_year  announcement_month  unsold_count
47                2011                   1         88706
48                2011                   2         84923
49                2011                   3         80588
50                2011                   4         77572
51                2011                   5         72232
..                 ...                 ...           ...
196               2023                   6         68865
197               2023                   7         66388
198               2023                   8         63087
199               2023                   9         61811
200               2023                  10         59806

[154 rows x 3 columns]

In [ ]:
df_apartment_unsold.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 154 entries, 47 to 200
Data columns (total 3 columns):
 #   Column              Non-Null Count  Dtype
---  ------              --------------  -----
 0   announcement_year   154 non-null    int64
 1   announcement_month  154 non-null    int64
 2   unsold_count        154 non-null    int64
dtypes: int64(3)
memory usage: 4.8 KB


### 아파트 분양 & 미분양 데이터 프레임 병합

In [ ]:
df_apartment_supply.head(20)

announcement_year  announcement_month  general_supply  combination_supply  \
0                2010                   2             0.0                 0.0   
1                2010                   3          1199.0               147.0   
2                2010                   4            31.0                96.0   
3                2010                   5           148.0                 0.0   
4                2010                   6           102.0                 0.0   
5                2010                   7           472.0                 0.0   
6                2010                   8           331.0                22.0   
7                2010                   9           974.0                 0.0   
8                2010                  10           312.0               631.0   
9                2010                  11           124.0                 0.0   
10               2010                  12          1100.0                 0.0   
11               2011                   1          2956.0               615.0   
12               2011                   2           647.0                 0.0   
13               2011                   3           307.0               154.0   
14               2011                   4           558.0                 0.0   
15               2011                   5           633.0               310.0   
16               2011                   6          1939.0                81.0   
17               2011                   7           739.0                70.0   
18               2011                   8           880.0                 0.0   
19               2011                   9          1030.0                96.0   

    etc_supply  total_supply  
0          0.0           0.0  
1        506.0        1852.0  
2          0.0         127.0  
3          0.0         148.0  
4          0.0         102.0  
5          0.0         472.0  
6          0.0         353.0  
7          0.0         974.0  
8          0.0         943.0  
9          0.0         124.0  
10         0.0        1100.0  
11         0.0        3571.0  
12         0.0         647.0  
13         2.0         463.0  
14         0.0         558.0  
15         0.0         943.0  
16      1724.0        3744.0  
17       442.0        1251.0  
18         0.0         880.0  
19         0.0        1126.0

In [ ]:
df_apartment_supply.loc[df_apartment_supply['announcement_year']==2011,:]

announcement_year  announcement_month  general_supply  combination_supply  \
11               2011                   1          2956.0               615.0   
12               2011                   2           647.0                 0.0   
13               2011                   3           307.0               154.0   
14               2011                   4           558.0                 0.0   
15               2011                   5           633.0               310.0   
16               2011                   6          1939.0                81.0   
17               2011                   7           739.0                70.0   
18               2011                   8           880.0                 0.0   
19               2011                   9          1030.0                96.0   
20               2011                  10             0.0                 0.0   
21               2011                  11          1083.0               413.0   
22               2011                  12          4682.0                 0.0   

    etc_supply  total_supply  
11         0.0        3571.0  
12         0.0         647.0  
13         2.0         463.0  
14         0.0         558.0  
15         0.0         943.0  
16      1724.0        3744.0  
17       442.0        1251.0  
18         0.0         880.0  
19         0.0        1126.0  
20         0.0           0.0  
21         0.0        1496.0  
22         0.0        4682.0

In [ ]:
df_apartment_supply.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 167 entries, 0 to 166
Data columns (total 6 columns):
 #   Column              Non-Null Count  Dtype  
---  ------              --------------  -----  
 0   announcement_year   167 non-null    int64  
 1   announcement_month  167 non-null    int64  
 2   general_supply      167 non-null    float64
 3   combination_supply  167 non-null    float64
 4   etc_supply          167 non-null    float64
 5   total_supply        167 non-null    float64
dtypes: float64(4), int64(2)
memory usage: 8.0 KB


In [ ]:
df_apartment_unsold.head()

announcement_year  announcement_month  unsold_count
47               2011                   1         88706
48               2011                   2         84923
49               2011                   3         80588
50               2011                   4         77572
51               2011                   5         72232

In [ ]:
df_apartment_unsold.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 154 entries, 47 to 200
Data columns (total 3 columns):
 #   Column              Non-Null Count  Dtype
---  ------              --------------  -----
 0   announcement_year   154 non-null    int64
 1   announcement_month  154 non-null    int64
 2   unsold_count        154 non-null    int64
dtypes: int64(3)
memory usage: 4.8 KB


In [ ]:
# 데이터 프레임 병합합
df_apartment_supply_unsold=pd.merge(df_apartment_supply, df_apartment_unsold, on=['announcement_year',	'announcement_month'])
df_apartment_supply_unsold.head()

announcement_year  announcement_month  general_supply  combination_supply  \
0               2011                   1          2956.0               615.0   
1               2011                   2           647.0                 0.0   
2               2011                   3           307.0               154.0   
3               2011                   4           558.0                 0.0   
4               2011                   5           633.0               310.0   

   etc_supply  total_supply  unsold_count  
0         0.0        3571.0         88706  
1         0.0         647.0         84923  
2         2.0         463.0         80588  
3         0.0         558.0         77572  
4         0.0         943.0         72232

In [ ]:
df_apartment_supply_unsold.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 154 entries, 0 to 153
Data columns (total 7 columns):
 #   Column              Non-Null Count  Dtype  
---  ------              --------------  -----  
 0   announcement_year   154 non-null    int64  
 1   announcement_month  154 non-null    int64  
 2   general_supply      154 non-null    float64
 3   combination_supply  154 non-null    float64
 4   etc_supply          154 non-null    float64
 5   total_supply        154 non-null    float64
 6   unsold_count        154 non-null    int64  
dtypes: float64(4), int64(3)
memory usage: 9.6 KB


#### 미분양 비율 컬럼 추가

In [ ]:
# 미분양 비율을 구함
df_apartment_supply_unsold['unsold_ratio'] = 100*(df_apartment_supply_unsold['unsold_count'] / df_apartment_supply_unsold['total_supply'])
df_apartment_supply_unsold

announcement_year  announcement_month  general_supply  \
0                 2011                   1          2956.0   
1                 2011                   2           647.0   
2                 2011                   3           307.0   
3                 2011                   4           558.0   
4                 2011                   5           633.0   
..                 ...                 ...             ...   
149               2023                   6           327.0   
150               2023                   7           206.0   
151               2023                   8          1169.0   
152               2023                   9          1191.0   
153               2023                  10           222.0   

     combination_supply  etc_supply  total_supply  unsold_count  unsold_ratio  
0                 615.0         0.0        3571.0         88706   2484.066088  
1                   0.0         0.0         647.0         84923  13125.656878  
2                 154.0         2.0         463.0         80588  17405.615551  
3                   0.0         0.0         558.0         77572  13901.792115  
4                 310.0         0.0         943.0         72232   7659.809120  
..                  ...         ...           ...           ...           ...  
149               454.0       191.0         972.0         68865   7084.876543  
150               148.0       389.0         743.0         66388   8935.127860  
151               226.0       432.0        1827.0         63087   3453.037767  
152               167.0       127.0        1485.0         61811   4162.356902  
153               492.0         0.0         714.0         59806   8376.190476  

[154 rows x 8 columns]

In [ ]:
df_apartment_supply_unsold.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 154 entries, 0 to 153
Data columns (total 8 columns):
 #   Column              Non-Null Count  Dtype  
---  ------              --------------  -----  
 0   announcement_year   154 non-null    int64  
 1   announcement_month  154 non-null    int64  
 2   general_supply      154 non-null    float64
 3   combination_supply  154 non-null    float64
 4   etc_supply          154 non-null    float64
 5   total_supply        154 non-null    float64
 6   unsold_count        154 non-null    int64  
 7   unsold_ratio        154 non-null    float64
dtypes: float64(5), int64(3)
memory usage: 10.8 KB


### 최종 테이블에 병합

In [ ]:
# 데이터 병합
df_economic=pd.merge(df_economic, df_apartment_supply_unsold, left_on=['year','month'], right_on=['announcement_year','announcement_month'], how='left')
df_economic = df_economic.drop(["announcement_year", "announcement_month"], axis=1)
df_economic

date  year  month  day  kospi_index  korea_rp  korea_3_year  \
0     2011-01-01  2011      1    1      2051.00       2.5         3.440   
1     2011-01-02  2011      1    2      2051.00       2.5         3.440   
2     2011-01-03  2011      1    3      2070.08       2.5         3.440   
3     2011-01-04  2011      1    4      2085.14       2.5         3.495   
4     2011-01-05  2011      1    5      2082.55       2.5         3.495   
...          ...   ...    ...  ...          ...       ...           ...   
4681  2023-10-26  2023     10   26      2299.08       3.5         3.692   
4682  2023-10-27  2023     10   27      2302.81       3.5         3.692   
4683  2023-10-28  2023     10   28      2302.81       3.5         3.692   
4684  2023-10-29  2023     10   29      2302.81       3.5         3.692   
4685  2023-10-30  2023     10   30      2310.55       3.5         3.692   

      korea_10_year  us_3_month  us_2_year  us_10_year  korea_10-3_year  \
0             4.570       0.124      0.601       3.334            1.130   
1             4.570       0.124      0.601       3.334            1.130   
2             4.570       0.124      0.601       3.334            1.130   
3             4.580       0.142      0.621       3.338            1.085   
4             4.630       0.142      0.708       3.463            1.135   
...             ...         ...        ...         ...              ...   
4681          3.977       5.479      5.046       4.849            0.285   
4682          3.977       5.477      5.015       4.845            0.285   
4683          3.977       5.477      5.015       4.845            0.285   
4684          3.977       5.477      5.015       4.845            0.285   
4685          3.977       5.481      5.050       4.888            0.285   

      us_10-2_year  us_10-3_year_month  general_supply  combination_supply  \
0            2.733               3.210          2956.0               615.0   
1            2.733               3.210          2956.0               615.0   
2            2.733               3.210          2956.0               615.0   
3            2.717               3.196          2956.0               615.0   
4            2.755               3.321          2956.0               615.0   
...            ...                 ...             ...                 ...   
4681        -0.197              -0.630           222.0               492.0   
4682        -0.170              -0.632           222.0               492.0   
4683        -0.170              -0.632           222.0               492.0   
4684        -0.170              -0.632           222.0               492.0   
4685        -0.162              -0.593           222.0               492.0   

      etc_supply  total_supply  unsold_count  unsold_ratio  
0            0.0        3571.0         88706   2484.066088  
1            0.0        3571.0         88706   2484.066088  
2            0.0        3571.0         88706   2484.066088  
3            0.0        3571.0         88706   2484.066088  
4            0.0        3571.0         88706   2484.066088  
...          ...           ...           ...           ...  
4681         0.0         714.0         59806   8376.190476  
4682         0.0         714.0         59806   8376.190476  
4683         0.0         714.0         59806   8376.190476  
4684         0.0         714.0         59806   8376.190476  
4685         0.0         714.0         59806   8376.190476  

[4686 rows x 20 columns]

In [ ]:
df_economic.info() # 데이터프레임 정보 확인

<class 'pandas.core.frame.DataFrame'>
Int64Index: 4686 entries, 0 to 4685
Data columns (total 20 columns):
 #   Column              Non-Null Count  Dtype  
---  ------              --------------  -----  
 0   date                4686 non-null   object 
 1   year                4686 non-null   int64  
 2   month               4686 non-null   int64  
 3   day                 4686 non-null   int64  
 4   kospi_index         4686 non-null   float64
 5   korea_rp            4686 non-null   float64
 6   korea_3_year        4686 non-null   float64
 7   korea_10_year       4686 non-null   float64
 8   us_3_month          4686 non-null   float64
 9   us_2_year           4686 non-null   float64
 10  us_10_year          4686 non-null   float64
 11  korea_10-3_year     4686 non-null   float64
 12  us_10-2_year        4686 non-null   float64
 13  us_10-3_year_month  4686 non-null   float64
 14  general_supply      4686 non-null   float64
 15  combination_supply  4686 non-null   float64
 16  etc_su

In [ ]:
df_economic.isnull().sum() # null data 있는지 확인

date                  0
year                  0
month                 0
day                   0
kospi_index           0
korea_rp              0
korea_3_year          0
korea_10_year         0
us_3_month            0
us_2_year             0
us_10_year            0
korea_10-3_year       0
us_10-2_year          0
us_10-3_year_month    0
general_supply        0
combination_supply    0
etc_supply            0
total_supply          0
unsold_count          0
unsold_ratio          0
dtype: int64

In [ ]:
df_economic.to_csv('/content/drive/MyDrive/house_price/after_data/economic_data2.csv',index=False)

# economic_data3 파일 생성


- economic_data3 파일은 economic_data2 파일에 월별 아파트 거래체결량들(매매체결량, 전세체결량,월세체결량) 정보를 추가한 파일
- '아파트 거래' 는 '아파트 매매', '아파트 전세', '아파트 월세' 를 합친 개념
- 아파트 월별 거래량은 이전 달에 체결된 서울 총 아파트 거래량을 의미

In [ ]:
import pandas as pd
import numpy as np
# 데이터들 불러오기
df_deal = pd.read_csv("/content/drive/MyDrive/house_price/after_data/apartment_deal.csv",  encoding='UTF8')
df_month_rent = pd.read_csv("/content/drive/MyDrive/house_price/after_data/apartment_month_rent.csv",  encoding='UTF8')
df_full_rent = pd.read_csv("/content/drive/MyDrive/house_price/after_data/apartment_full_rent.csv",  encoding='UTF8')
df_economic2 = pd.read_csv("/content/drive/MyDrive/house_price/after_data/economic_data2.csv",  encoding='UTF8')

## 아파트 매매 체결량 데이터프레임 생성

In [ ]:
df_deal.head()

date  year  month  day address_0 address_1 address_2  address_3  \
0  2011-07-09  2011      7    9     서울특별시       강남구       개포동      655.0   
1  2011-07-28  2011      7   28     서울특별시       강남구       개포동      655.0   
2  2011-01-19  2011      1   19     서울특별시       강남구       개포동      658.0   
3  2011-09-02  2011      9    2     서울특별시       강남구       개포동      658.0   
4  2011-12-17  2011     12   17     서울특별시       강남구       개포동      658.0   

   address_4            name   area  deal_price  
0        2.0  개포2차현대아파트(220)  77.75       64000  
1        2.0  개포2차현대아파트(220)  77.75       65500  
2        1.0  개포6차우성아파트1동~8동  67.28       70500  
3        1.0  개포6차우성아파트1동~8동  79.97       85000  
4        1.0  개포6차우성아파트1동~8동  67.28       68000

In [ ]:
# 서울 아파트 월별 거래량을 group by를 이용하여여 계산
df_count = df_deal.groupby(["year","month"])["name"].agg('count').copy()
df_count = df_count.reset_index(["year","month"]) # index로 있던 컬럼들을 다시 컬럼화
df_count.columns = ["year","month","deal_count"] # 컬럼명들 수정
df_count

year  month  deal_count
0    2011      1        7179
1    2011      2        6026
2    2011      3        5419
3    2011      4        4028
4    2011      5        3836
..    ...    ...         ...
149  2023      6        4009
150  2023      7        3733
151  2023      8        3996
152  2023      9        3448
153  2023     10        1948

[154 rows x 3 columns]

In [ ]:
df_count.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 154 entries, 0 to 153
Data columns (total 3 columns):
 #   Column      Non-Null Count  Dtype
---  ------      --------------  -----
 0   year        154 non-null    int64
 1   month       154 non-null    int64
 2   deal_count  154 non-null    int64
dtypes: int64(3)
memory usage: 3.7 KB


## 아파트 전세 체결량 정보 추가

- 아파트 매매 체결량 부분 참조

In [ ]:
df_full_rent.head()

date  year  month  day address_0 address_1 address_2  address_3  \
0  2011-01-05  2011      1    5     서울특별시       강남구       개포동      655.0   
1  2011-01-18  2011      1   18     서울특별시       강남구       개포동      655.0   
2  2011-02-01  2011      2    1     서울특별시       강남구       개포동      655.0   
3  2011-02-11  2011      2   11     서울특별시       강남구       개포동      655.0   
4  2011-02-24  2011      2   24     서울특별시       강남구       개포동      655.0   

   address_4            name   area  full_rent_price  
0        2.0  개포2차현대아파트(220)  77.75            35000  
1        2.0  개포2차현대아파트(220)  77.75            20000  
2        2.0  개포2차현대아파트(220)  77.75            24000  
3        2.0  개포2차현대아파트(220)  77.75            31000  
4        2.0  개포2차현대아파트(220)  77.75            30500

In [ ]:
# 월별 전세 체결량을 group과 count를 통해서 구함
df_temp = df_full_rent.groupby(["year","month"])["name"].agg('count').copy()
df_temp = df_temp.reset_index(["year","month"])
df_temp.columns = ["year","month","full_rent_count"]
df_temp

year  month  full_rent_count
0    2011      1            12336
1    2011      2            12261
2    2011      3            12121
3    2011      4             9754
4    2011      5             9280
..    ...    ...              ...
149  2023      6            13228
150  2023      7            12965
151  2023      8            12526
152  2023      9            11173
153  2023     10            10169

[154 rows x 3 columns]

In [ ]:
# 아파트 매매 체결량 데이터프레임과 아파트 전세 체결량 데이터프레임을 병합
df_count=pd.merge(df_count,df_temp, left_on=["year","month"], right_on=["year","month"], how="inner")
df_count.head()

year  month  deal_count  full_rent_count
0  2011      1        7179            12336
1  2011      2        6026            12261
2  2011      3        5419            12121
3  2011      4        4028             9754
4  2011      5        3836             9280

In [ ]:
df_count.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 154 entries, 0 to 153
Data columns (total 4 columns):
 #   Column           Non-Null Count  Dtype
---  ------           --------------  -----
 0   year             154 non-null    int64
 1   month            154 non-null    int64
 2   deal_count       154 non-null    int64
 3   full_rent_count  154 non-null    int64
dtypes: int64(4)
memory usage: 6.0 KB


## 아파트 월세 체결량 정보 추가

- 아파트 매매 체결량 데이터프레임 참조

In [ ]:
df_month_rent.head()

date  year  month  day address_0 address_1 address_2  address_3  \
0  2011-03-18  2011      3   18     서울특별시       강남구       개포동      658.0   
1  2011-04-09  2011      4    9     서울특별시       강남구       개포동      658.0   
2  2011-07-09  2011      7    9     서울특별시       강남구       개포동      658.0   
3  2011-09-19  2011      9   19     서울특별시       강남구       개포동      658.0   
4  2011-09-20  2011      9   20     서울특별시       강남구       개포동      658.0   

   address_4            name   area  rent_deposit  month_rent_price  
0        1.0  개포6차우성아파트1동~8동  79.97         19000                63  
1        1.0  개포6차우성아파트1동~8동  79.97         21000                35  
2        1.0  개포6차우성아파트1동~8동  79.97          3000               160  
3        1.0  개포6차우성아파트1동~8동  79.97          6000               140  
4        1.0  개포6차우성아파트1동~8동  79.97          5000               160

In [ ]:
df_temp = df_month_rent.groupby(["year","month"])["name"].agg('count').copy()
df_temp = df_temp.reset_index(["year","month"])
df_temp.columns = ["year","month","month_rent_count"]
df_temp

year  month  month_rent_count
0    2011      1              2514
1    2011      2              2711
2    2011      3              2775
3    2011      4              2210
4    2011      5              2168
..    ...    ...               ...
149  2023      6              9829
150  2023      7              8594
151  2023      8              8170
152  2023      9              7342
153  2023     10              6270

[154 rows x 3 columns]

In [ ]:
# 아파트 월세 거래량 데이터프레임을 추가하여 병합
df_count=pd.merge(df_count,df_temp, left_on=["year","month"], right_on=["year","month"], how="inner")
df_count.head()

year  month  deal_count  full_rent_count  month_rent_count
0  2011      1        7179            12336              2514
1  2011      2        6026            12261              2711
2  2011      3        5419            12121              2775
3  2011      4        4028             9754              2210
4  2011      5        3836             9280              2168

In [ ]:
df_count.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 154 entries, 0 to 153
Data columns (total 5 columns):
 #   Column            Non-Null Count  Dtype
---  ------            --------------  -----
 0   year              154 non-null    int64
 1   month             154 non-null    int64
 2   deal_count        154 non-null    int64
 3   full_rent_count   154 non-null    int64
 4   month_rent_count  154 non-null    int64
dtypes: int64(5)
memory usage: 7.2 KB


## 월 정보들 shift

- 해당 달의 거래량은 다음달에 알 수 있음으로 한칸씩 shift(1달씩 미룸)

In [ ]:
df_count['deal_count'] = df_count['deal_count'].shift(1)
df_count['month_rent_count'] = df_count['month_rent_count'].shift(1)
df_count['full_rent_count'] = df_count['full_rent_count'].shift(1)
# 컬럼명 수정
df_count.columns = ['year','month','last_month_total_deal_count','last_month_total_full_rent_count', 'last_month_total_month_rent_count']
df_count

year  month  last_month_total_deal_count  \
0    2011      1                          NaN   
1    2011      2                       7179.0   
2    2011      3                       6026.0   
3    2011      4                       5419.0   
4    2011      5                       4028.0   
..    ...    ...                          ...   
149  2023      6                       3561.0   
150  2023      7                       4009.0   
151  2023      8                       3733.0   
152  2023      9                       3996.0   
153  2023     10                       3448.0   

     last_month_total_full_rent_count  last_month_total_month_rent_count  
0                                 NaN                                NaN  
1                             12336.0                             2514.0  
2                             12261.0                             2711.0  
3                             12121.0                             2775.0  
4                              9754.0                             2210.0  
..                                ...                                ...  
149                           13314.0                             9700.0  
150                           13228.0                             9829.0  
151                           12965.0                             8594.0  
152                           12526.0                             8170.0  
153                           11173.0                             7342.0  

[154 rows x 5 columns]

In [ ]:
# null 값이 있는 row를 제거한 후,
df_count.dropna(axis=0,inplace=True)
df_count.reset_index(inplace=True,drop=True) # 인덱스 초기화
df_count

year  month  last_month_total_deal_count  \
0    2011      2                       7179.0   
1    2011      3                       6026.0   
2    2011      4                       5419.0   
3    2011      5                       4028.0   
4    2011      6                       3836.0   
..    ...    ...                          ...   
148  2023      6                       3561.0   
149  2023      7                       4009.0   
150  2023      8                       3733.0   
151  2023      9                       3996.0   
152  2023     10                       3448.0   

     last_month_total_full_rent_count  last_month_total_month_rent_count  
0                             12336.0                             2514.0  
1                             12261.0                             2711.0  
2                             12121.0                             2775.0  
3                              9754.0                             2210.0  
4                              9280.0                             2168.0  
..                                ...                                ...  
148                           13314.0                             9700.0  
149                           13228.0                             9829.0  
150                           12965.0                             8594.0  
151                           12526.0                             8170.0  
152                           11173.0                             7342.0  

[153 rows x 5 columns]

In [ ]:
df_count.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 153 entries, 0 to 152
Data columns (total 5 columns):
 #   Column                             Non-Null Count  Dtype  
---  ------                             --------------  -----  
 0   year                               153 non-null    int64  
 1   month                              153 non-null    int64  
 2   last_month_total_deal_count        153 non-null    float64
 3   last_month_total_full_rent_count   153 non-null    float64
 4   last_month_total_month_rent_count  153 non-null    float64
dtypes: float64(3), int64(2)
memory usage: 6.1 KB


In [ ]:
df_economic.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 4686 entries, 0 to 4685
Data columns (total 20 columns):
 #   Column              Non-Null Count  Dtype  
---  ------              --------------  -----  
 0   date                4686 non-null   object 
 1   year                4686 non-null   int64  
 2   month               4686 non-null   int64  
 3   day                 4686 non-null   int64  
 4   kospi_index         4686 non-null   float64
 5   korea_rp            4686 non-null   float64
 6   korea_3_year        4686 non-null   float64
 7   korea_10_year       4686 non-null   float64
 8   us_3_month          4686 non-null   float64
 9   us_2_year           4686 non-null   float64
 10  us_10_year          4686 non-null   float64
 11  korea_10-3_year     4686 non-null   float64
 12  us_10-2_year        4686 non-null   float64
 13  us_10-3_year_month  4686 non-null   float64
 14  general_supply      4686 non-null   float64
 15  combination_supply  4686 non-null   float64
 16  etc_su

## economic_data2 와의 통합

In [ ]:
# 거시경제 지표가 모든 날짜들에 대한 정보를 가지고 있음으로, year과 month를 통해서 병합
df_economic3 = pd.merge(df_economic2, df_count, left_on=["year","month"], right_on=["year","month"], how="inner")

df_economic3 = df_economic3.rename(columns={'unsold_count' : 'last_month_total_unsold_count',
                                          'unsold_ratio' : 'last_month_total_unsold_ratio','general_supply':'last_month_general_supply', 'combination_supply':'last_month_combination_supply',
                                            'etc_supply':'last_month_etc_supply','total_supply':'last_month_total_supply'})



print(df_economic3.info())
df_economic3.head()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 4655 entries, 0 to 4654
Data columns (total 23 columns):
 #   Column                             Non-Null Count  Dtype  
---  ------                             --------------  -----  
 0   date                               4655 non-null   object 
 1   year                               4655 non-null   int64  
 2   month                              4655 non-null   int64  
 3   day                                4655 non-null   int64  
 4   kospi_index                        4655 non-null   float64
 5   korea_rp                           4655 non-null   float64
 6   korea_3_year                       4655 non-null   float64
 7   korea_10_year                      4655 non-null   float64
 8   us_3_month                         4655 non-null   float64
 9   us_2_year                          4655 non-null   float64
 10  us_10_year                         4655 non-null   float64
 11  korea_10-3_year                    4655 non-null   float

date  year  month  day  kospi_index  korea_rp  korea_3_year  \
0  2011-02-01  2011      2    1      2072.03      2.75          3.97   
1  2011-02-02  2011      2    2      2072.03      2.75          3.97   
2  2011-02-03  2011      2    3      2072.03      2.75          3.97   
3  2011-02-04  2011      2    4      2072.03      2.75          3.97   
4  2011-02-05  2011      2    5      2072.03      2.75          3.97   

   korea_10_year  us_3_month  us_2_year  ...  us_10-3_year_month  \
0           4.71       0.157      0.605  ...               3.278   
1           4.71       0.157      0.664  ...               3.322   
2           4.71       0.152      0.712  ...               3.395   
3           4.71       0.152      0.752  ...               3.486   
4           4.71       0.152      0.752  ...               3.486   

   last_month_general_supply  last_month_combination_supply  \
0                      647.0                            0.0   
1                      647.0                            0.0   
2                      647.0                            0.0   
3                      647.0                            0.0   
4                      647.0                            0.0   

   last_month_etc_supply  last_month_total_supply  \
0                    0.0                    647.0   
1                    0.0                    647.0   
2                    0.0                    647.0   
3                    0.0                    647.0   
4                    0.0                    647.0   

   last_month_total_unsold_count  last_month_total_unsold_ratio  \
0                          84923                   13125.656878   
1                          84923                   13125.656878   
2                          84923                   13125.656878   
3                          84923                   13125.656878   
4                          84923                   13125.656878   

   last_month_total_deal_count  last_month_total_full_rent_count  \
0                       7179.0                           12336.0   
1                       7179.0                           12336.0   
2                       7179.0                           12336.0   
3                       7179.0                           12336.0   
4                       7179.0                           12336.0   

   last_month_total_month_rent_count  
0                             2514.0  
1                             2514.0  
2                             2514.0  
3                             2514.0  
4                             2514.0  

[5 rows x 23 columns]

In [ ]:
df_economic3.tail()

date  year  month  day  kospi_index  korea_rp  korea_3_year  \
4650  2023-10-26  2023     10   26      2299.08       3.5         3.692   
4651  2023-10-27  2023     10   27      2302.81       3.5         3.692   
4652  2023-10-28  2023     10   28      2302.81       3.5         3.692   
4653  2023-10-29  2023     10   29      2302.81       3.5         3.692   
4654  2023-10-30  2023     10   30      2310.55       3.5         3.692   

      korea_10_year  us_3_month  us_2_year  ...  us_10-3_year_month  \
4650          3.977       5.479      5.046  ...              -0.630   
4651          3.977       5.477      5.015  ...              -0.632   
4652          3.977       5.477      5.015  ...              -0.632   
4653          3.977       5.477      5.015  ...              -0.632   
4654          3.977       5.481      5.050  ...              -0.593   

      last_month_general_supply  last_month_combination_supply  \
4650                      222.0                          492.0   
4651                      222.0                          492.0   
4652                      222.0                          492.0   
4653                      222.0                          492.0   
4654                      222.0                          492.0   

      last_month_etc_supply  last_month_total_supply  \
4650                    0.0                    714.0   
4651                    0.0                    714.0   
4652                    0.0                    714.0   
4653                    0.0                    714.0   
4654                    0.0                    714.0   

      last_month_total_unsold_count  last_month_total_unsold_ratio  \
4650                          59806                    8376.190476   
4651                          59806                    8376.190476   
4652                          59806                    8376.190476   
4653                          59806                    8376.190476   
4654                          59806                    8376.190476   

      last_month_total_deal_count  last_month_total_full_rent_count  \
4650                       3448.0                           11173.0   
4651                       3448.0                           11173.0   
4652                       3448.0                           11173.0   
4653                       3448.0                           11173.0   
4654                       3448.0                           11173.0   

      last_month_total_month_rent_count  
4650                             7342.0  
4651                             7342.0  
4652                             7342.0  
4653                             7342.0  
4654                             7342.0  

[5 rows x 23 columns]

In [ ]:
# 파일 저장
df_economic3.to_pickle('/content/drive/MyDrive/house_price/after_data/economic_data3.pkl')

# final_economic 파일 생성

- economic_data3 은 '해당 월'에 대한 거시경제 지표들을 가지고 있다.
- final_economic 파일은 economic_data3 파일에 추가적으로 과거 수치대비 변화에 대한 정보들을 추가한 파일

## 기본정보 파악

In [ ]:
import pandas as pd
# 데이터 프레임 불러오기기
df_economic = pd.read_pickle('/content/drive/MyDrive/house_price/after_data/economic_data3.pkl')
df_economic.head()

date  year  month  day  kospi_index  korea_rp  korea_3_year  \
0  2011-02-01  2011      2    1      2072.03      2.75          3.97   
1  2011-02-02  2011      2    2      2072.03      2.75          3.97   
2  2011-02-03  2011      2    3      2072.03      2.75          3.97   
3  2011-02-04  2011      2    4      2072.03      2.75          3.97   
4  2011-02-05  2011      2    5      2072.03      2.75          3.97   

   korea_10_year  us_3_month  us_2_year  ...  us_10-3_year_month  \
0           4.71       0.157      0.605  ...               3.278   
1           4.71       0.157      0.664  ...               3.322   
2           4.71       0.152      0.712  ...               3.395   
3           4.71       0.152      0.752  ...               3.486   
4           4.71       0.152      0.752  ...               3.486   

   last_month_general_supply  last_month_combination_supply  \
0                      647.0                            0.0   
1                      647.0                            0.0   
2                      647.0                            0.0   
3                      647.0                            0.0   
4                      647.0                            0.0   

   last_month_etc_supply  last_month_total_supply  \
0                    0.0                    647.0   
1                    0.0                    647.0   
2                    0.0                    647.0   
3                    0.0                    647.0   
4                    0.0                    647.0   

   last_month_total_unsold_count  last_month_total_unsold_ratio  \
0                          84923                   13125.656878   
1                          84923                   13125.656878   
2                          84923                   13125.656878   
3                          84923                   13125.656878   
4                          84923                   13125.656878   

   last_month_total_deal_count  last_month_total_full_rent_count  \
0                       7179.0                           12336.0   
1                       7179.0                           12336.0   
2                       7179.0                           12336.0   
3                       7179.0                           12336.0   
4                       7179.0                           12336.0   

   last_month_total_month_rent_count  
0                             2514.0  
1                             2514.0  
2                             2514.0  
3                             2514.0  
4                             2514.0  

[5 rows x 23 columns]

In [ ]:
df_economic.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 4655 entries, 0 to 4654
Data columns (total 23 columns):
 #   Column                             Non-Null Count  Dtype  
---  ------                             --------------  -----  
 0   date                               4655 non-null   object 
 1   year                               4655 non-null   int64  
 2   month                              4655 non-null   int64  
 3   day                                4655 non-null   int64  
 4   kospi_index                        4655 non-null   float64
 5   korea_rp                           4655 non-null   float64
 6   korea_3_year                       4655 non-null   float64
 7   korea_10_year                      4655 non-null   float64
 8   us_3_month                         4655 non-null   float64
 9   us_2_year                          4655 non-null   float64
 10  us_10_year                         4655 non-null   float64
 11  korea_10-3_year                    4655 non-null   float

## 6,12개월 전 대비 변화정도 계산

In [ ]:
# 월별 평균 값을 구한 데이터프레임 2개 구함(추후 병합에 사용)
# 'korea_10-3_year', 'us_10-2_year', 'us_10-3_year_month', 'last_month_total_unsold_ratio' 은 컬럼별 계산을 통해 계산된 값들임으로, 월별 평균값을 구할 때는
# 추가적으로 계산 필요
df_economic_month = df_economic.drop(['date','day','korea_10-3_year', 'us_10-2_year', 'us_10-3_year_month', 'last_month_total_unsold_ratio'],axis=1).copy()


# 일 단위여서 월단위로 묶어서 평균을 할 필요가 있음음
df_economic_month = df_economic_month.groupby(['year','month']).agg('mean').reset_index()

df_economic_month['korea_10-3_year'] = df_economic_month['korea_10_year'] - df_economic_month['korea_3_year']
df_economic_month['us_10-2_year'] = df_economic_month['us_10_year'] - df_economic_month['us_2_year']
df_economic_month['us_10-3_year_month'] = df_economic_month['us_10_year'] - df_economic_month['us_3_month']
df_economic_month['last_month_total_unsold_ratio'] = (100*df_economic_month['last_month_total_unsold_count']) / df_economic_month['last_month_total_supply']

display(df_economic_month.head())

year  month  kospi_index  korea_rp  korea_3_year  korea_10_year  \
0  2011      2  2011.301786  2.750000      3.939286       4.745714   
1  2011      3  1999.638710  2.927419      3.745968       4.518387   
2  2011      4  2152.758000  3.000000      3.747000       4.483333   
3  2011      5  2126.069355  3.000000      3.673710       4.347742   
4  2011      6  2074.891667  3.175000      3.638500       4.240667   

   us_3_month  us_2_year  us_10_year  last_month_general_supply  ...  \
0    0.127536   0.762071    3.565429                      647.0  ...   
1    0.095839   0.679452    3.404226                      307.0  ...   
2    0.056200   0.719767    3.434600                      558.0  ...   
3    0.035581   0.536161    3.152774                      633.0  ...   
4    0.032667   0.402067    2.976833                     1939.0  ...   

   last_month_etc_supply  last_month_total_supply  \
0                    0.0                    647.0   
1                    2.0                    463.0   
2                    0.0                    558.0   
3                    0.0                    943.0   
4                 1724.0                   3744.0   

   last_month_total_unsold_count  last_month_total_deal_count  \
0                        84923.0                       7179.0   
1                        80588.0                       6026.0   
2                        77572.0                       5419.0   
3                        72232.0                       4028.0   
4                        71360.0                       3836.0   

   last_month_total_full_rent_count  last_month_total_month_rent_count  \
0                           12336.0                             2514.0   
1                           12261.0                             2711.0   
2                           12121.0                             2775.0   
3                            9754.0                             2210.0   
4                            9280.0                             2168.0   

   korea_10-3_year  us_10-2_year  us_10-3_year_month  \
0         0.806429      2.803357            3.437893   
1         0.772419      2.724774            3.308387   
2         0.736333      2.714833            3.378400   
3         0.674032      2.616613            3.117194   
4         0.602167      2.574767            2.944167   

   last_month_total_unsold_ratio  
0                   13125.656878  
1                   17405.615551  
2                   13901.792115  
3                    7659.809120  
4                    1905.982906  

[5 rows x 21 columns]

In [ ]:
## 6달전 날짜들 구한
df_economic.loc[df_economic['month']<7, '6m_before_year'] = df_economic['year']-1
df_economic.loc[df_economic['month']<7, '6m_before_month'] = 12-(6-df_economic['month'])
df_economic.loc[df_economic['month']>=7, '6m_before_year'] = df_economic['year']
df_economic.loc[df_economic['month']>=7, '6m_before_month'] = df_economic['month']-6

# 12달전 날짜들 구한
df_economic.loc[:, '12m_before_year'] = df_economic['year']-1
df_economic.loc[:, '12m_before_month'] = df_economic['month']

df_economic

date  year  month  day  kospi_index  korea_rp  korea_3_year  \
0     2011-02-01  2011      2    1      2072.03      2.75         3.970   
1     2011-02-02  2011      2    2      2072.03      2.75         3.970   
2     2011-02-03  2011      2    3      2072.03      2.75         3.970   
3     2011-02-04  2011      2    4      2072.03      2.75         3.970   
4     2011-02-05  2011      2    5      2072.03      2.75         3.970   
...          ...   ...    ...  ...          ...       ...           ...   
4650  2023-10-26  2023     10   26      2299.08      3.50         3.692   
4651  2023-10-27  2023     10   27      2302.81      3.50         3.692   
4652  2023-10-28  2023     10   28      2302.81      3.50         3.692   
4653  2023-10-29  2023     10   29      2302.81      3.50         3.692   
4654  2023-10-30  2023     10   30      2310.55      3.50         3.692   

      korea_10_year  us_3_month  us_2_year  ...  last_month_total_supply  \
0             4.710       0.157      0.605  ...                    647.0   
1             4.710       0.157      0.664  ...                    647.0   
2             4.710       0.152      0.712  ...                    647.0   
3             4.710       0.152      0.752  ...                    647.0   
4             4.710       0.152      0.752  ...                    647.0   
...             ...         ...        ...  ...                      ...   
4650          3.977       5.479      5.046  ...                    714.0   
4651          3.977       5.477      5.015  ...                    714.0   
4652          3.977       5.477      5.015  ...                    714.0   
4653          3.977       5.477      5.015  ...                    714.0   
4654          3.977       5.481      5.050  ...                    714.0   

      last_month_total_unsold_count  last_month_total_unsold_ratio  \
0                             84923                   13125.656878   
1                             84923                   13125.656878   
2                             84923                   13125.656878   
3                             84923                   13125.656878   
4                             84923                   13125.656878   
...                             ...                            ...   
4650                          59806                    8376.190476   
4651                          59806                    8376.190476   
4652                          59806                    8376.190476   
4653                          59806                    8376.190476   
4654                          59806                    8376.190476   

      last_month_total_deal_count  last_month_total_full_rent_count  \
0                          7179.0                           12336.0   
1                          7179.0                           12336.0   
2                          7179.0                           12336.0   
3                          7179.0                           12336.0   
4                          7179.0                           12336.0   
...                           ...                               ...   
4650                       3448.0                           11173.0   
4651                       3448.0                           11173.0   
4652                       3448.0                           11173.0   
4653                       3448.0                           11173.0   
4654                       3448.0                           11173.0   

      last_month_total_month_rent_count  6m_before_year  6m_before_month  \
0                                2514.0          2010.0              8.0   
1                                2514.0          2010.0              8.0   
2                                2514.0          2010.0              8.0   
3                                2514.0          2010.0              8.0   
4                                2514.0          2010.0              8.0   
...                                 ...         

In [ ]:
pd.set_option('display.max_columns', 100)
# df_economic의 '6m_before_year', '6m_before_month' 과 df_economic_6m_before의 'year_6m_before','month_6m_before' 이 매칭이 됨
df_economic = pd.merge(df_economic, df_economic_month, left_on=['6m_before_year', '6m_before_month'], right_on=['year','month'], how='inner', suffixes=('', '_6m_before'))
df_economic = pd.merge(df_economic, df_economic_month, left_on=['12m_before_year', '12m_before_month'], right_on=['year','month'], how='inner', suffixes=('', '_12m_before'))
df_economic = df_economic.drop(["6m_before_year", "6m_before_month", "12m_before_year", "12m_before_month", "year_6m_before", "month_6m_before","year_12m_before", "month_12m_before"], axis=1)
df_economic.head(20)

date  year  month  day  kospi_index  korea_rp  korea_3_year  \
0   2012-02-01  2012      2    1      1959.24      3.25         3.380   
1   2012-02-02  2012      2    2      1984.30      3.25         3.380   
2   2012-02-03  2012      2    3      1972.34      3.25         3.380   
3   2012-02-04  2012      2    4      1972.34      3.25         3.380   
4   2012-02-05  2012      2    5      1972.34      3.25         3.380   
5   2012-02-06  2012      2    6      1973.13      3.25         3.390   
6   2012-02-07  2012      2    7      1981.59      3.25         3.410   
7   2012-02-08  2012      2    8      2003.73      3.25         3.440   
8   2012-02-09  2012      2    9      2014.62      3.25         3.450   
9   2012-02-10  2012      2   10      1993.71      3.25         3.455   
10  2012-02-11  2012      2   11      1993.71      3.25         3.455   
11  2012-02-12  2012      2   12      1993.71      3.25         3.455   
12  2012-02-13  2012      2   13      2005.74      3.25         3.440   
13  2012-02-14  2012      2   14      2002.64      3.25         3.445   
14  2012-02-15  2012      2   15      2025.32      3.25         3.445   
15  2012-02-16  2012      2   16      1997.45      3.25         3.375   
16  2012-02-17  2012      2   17      2023.47      3.25         3.455   
17  2012-02-18  2012      2   18      2023.47      3.25         3.455   
18  2012-02-19  2012      2   19      2023.47      3.25         3.455   
19  2012-02-20  2012      2   20      2024.90      3.25         3.470   

    korea_10_year  us_3_month  us_2_year  us_10_year  korea_10-3_year  \
0            3.75       0.061      0.226       1.830            0.370   
1            3.76       0.084      0.226       1.823            0.380   
2            3.76       0.079      0.238       1.924            0.380   
3            3.76       0.079      0.238       1.924            0.380   
4            3.76       0.079      0.238       1.924            0.380   
5            3.78       0.086      0.234       1.901            0.390   
6            3.81       0.081      0.250       1.977            0.400   
7            3.83       0.081      0.258       1.982            0.390   
8            3.81       0.091      0.266       2.036            0.360   
9            3.82       0.089      0.278       1.984            0.365   
10           3.82       0.089      0.278       1.984            0.365   
11           3.82       0.089      0.278       1.984            0.365   
12           3.83       0.102      0.290       1.978            0.390   
13           3.82       0.117      0.290       1.938            0.375   
14           3.83       0.112      0.270       1.933            0.385   
15           3.81       0.104      0.294       1.984            0.435   
16           3.83       0.081      0.294       2.000            0.375   
17           3.83       0.081      0.294       2.000            0.375   
18           3.83       0.081      0.294       2.000            0.375   
19           3.85       0.076      0.294       2.038            0.380   

    us_10-2_year  us_10-3_year_month  last_month_general_supply  \
0          1.604               1.769                      912.0   
1          1.597               1.739                      912.0   
2          1.686               1.845                      912.0   
3          1.686               1.845                      912.0   
4          1.686               1.845                      912.0   
5          1.667               1.815                      912.0   
6          1.727               1.896                      912.0   
7          1.724               1.901                      912.0   
8          1.770               1.945                      912.0   
9          1.706               1.895                      912.0   
10         1.706               1.895                      912.0   
11         1.706               1.895                      912.0   
12         1.688               1.876                      912.0   
13  

> 처음에 변화율을 구하려 했지만, 수치가 0인 값들이 있어서 계산을 할 때 null이나 inf가 되는 경우들이 있어서 변화율보다는 변화정도로 진행을 하기로 함

>> 계산식을 생성할 때, 0으로 나누거나 나누어지는 경우들에 대해서 조심해야 한다

In [ ]:
df_economic_columns = list(df_economic.columns)
df_economic_columns_now = df_economic_columns[4:23]
df_economic_columns_6m_before = df_economic_columns[23:42]
df_economic_columns_12m_before = df_economic_columns[42:]

In [ ]:
df_economic_columns_now  = sorted(df_economic_columns_now)
print(len(df_economic_columns_now))
df_economic_columns_now

19


['korea_10-3_year',
 'korea_10_year',
 'korea_3_year',
 'korea_rp',
 'kospi_index',
 'last_month_combination_supply',
 'last_month_etc_supply',
 'last_month_general_supply',
 'last_month_total_deal_count',
 'last_month_total_full_rent_count',
 'last_month_total_month_rent_count',
 'last_month_total_supply',
 'last_month_total_unsold_count',
 'last_month_total_unsold_ratio',
 'us_10-2_year',
 'us_10-3_year_month',
 'us_10_year',
 'us_2_year',
 'us_3_month']

In [ ]:
df_economic_columns_6m_before = sorted(df_economic_columns_6m_before)
print(len(df_economic_columns_6m_before))
df_economic_columns_6m_before

19


['korea_10-3_year_6m_before',
 'korea_10_year_6m_before',
 'korea_3_year_6m_before',
 'korea_rp_6m_before',
 'kospi_index_6m_before',
 'last_month_combination_supply_6m_before',
 'last_month_etc_supply_6m_before',
 'last_month_general_supply_6m_before',
 'last_month_total_deal_count_6m_before',
 'last_month_total_full_rent_count_6m_before',
 'last_month_total_month_rent_count_6m_before',
 'last_month_total_supply_6m_before',
 'last_month_total_unsold_count_6m_before',
 'last_month_total_unsold_ratio_6m_before',
 'us_10-2_year_6m_before',
 'us_10-3_year_month_6m_before',
 'us_10_year_6m_before',
 'us_2_year_6m_before',
 'us_3_month_6m_before']

In [ ]:
df_economic_columns_12m_before = sorted(df_economic_columns_12m_before)
print(len(df_economic_columns_12m_before))
df_economic_columns_12m_before

19


['korea_10-3_year_12m_before',
 'korea_10_year_12m_before',
 'korea_3_year_12m_before',
 'korea_rp_12m_before',
 'kospi_index_12m_before',
 'last_month_combination_supply_12m_before',
 'last_month_etc_supply_12m_before',
 'last_month_general_supply_12m_before',
 'last_month_total_deal_count_12m_before',
 'last_month_total_full_rent_count_12m_before',
 'last_month_total_month_rent_count_12m_before',
 'last_month_total_supply_12m_before',
 'last_month_total_unsold_count_12m_before',
 'last_month_total_unsold_ratio_12m_before',
 'us_10-2_year_12m_before',
 'us_10-3_year_month_12m_before',
 'us_10_year_12m_before',
 'us_2_year_12m_before',
 'us_3_month_12m_before']

In [ ]:
# 변화정도 = 현재데이터 - 과거데이터
# 반복문을 통해서 변화정도들을 계산
for i in range(len(df_economic_columns_now)):
  df_economic[df_economic_columns_6m_before[i]] = df_economic[df_economic_columns_now[i]] - df_economic[df_economic_columns_6m_before[i]]
  df_economic[df_economic_columns_12m_before[i]] = df_economic[df_economic_columns_now[i]] - df_economic[df_economic_columns_12m_before[i]]
df_economic

date  year  month  day  kospi_index  korea_rp  korea_3_year  \
0     2012-02-01  2012      2    1      1959.24      3.25         3.380   
1     2012-02-02  2012      2    2      1984.30      3.25         3.380   
2     2012-02-03  2012      2    3      1972.34      3.25         3.380   
3     2012-02-04  2012      2    4      1972.34      3.25         3.380   
4     2012-02-05  2012      2    5      1972.34      3.25         3.380   
...          ...   ...    ...  ...          ...       ...           ...   
4285  2023-10-26  2023     10   26      2299.08      3.50         3.692   
4286  2023-10-27  2023     10   27      2302.81      3.50         3.692   
4287  2023-10-28  2023     10   28      2302.81      3.50         3.692   
4288  2023-10-29  2023     10   29      2302.81      3.50         3.692   
4289  2023-10-30  2023     10   30      2310.55      3.50         3.692   

      korea_10_year  us_3_month  us_2_year  us_10_year  korea_10-3_year  \
0             3.750       0.061      0.226       1.830            0.370   
1             3.760       0.084      0.226       1.823            0.380   
2             3.760       0.079      0.238       1.924            0.380   
3             3.760       0.079      0.238       1.924            0.380   
4             3.760       0.079      0.238       1.924            0.380   
...             ...         ...        ...         ...              ...   
4285          3.977       5.479      5.046       4.849            0.285   
4286          3.977       5.477      5.015       4.845            0.285   
4287          3.977       5.477      5.015       4.845            0.285   
4288          3.977       5.477      5.015       4.845            0.285   
4289          3.977       5.481      5.050       4.888            0.285   

      us_10-2_year  us_10-3_year_month  last_month_general_supply  \
0            1.604               1.769                      912.0   
1            1.597               1.739                      912.0   
2            1.686               1.845                      912.0   
3            1.686               1.845                      912.0   
4            1.686               1.845                      912.0   
...            ...                 ...                        ...   
4285        -0.197              -0.630                      222.0   
4286        -0.170              -0.632                      222.0   
4287        -0.170              -0.632                      222.0   
4288        -0.170              -0.632                      222.0   
4289        -0.162              -0.593                      222.0   

      last_month_combination_supply  last_month_etc_supply  \
0                               0.0                    0.0   
1                               0.0                    0.0   
2                               0.0                    0.0   
3                               0.0                    0.0   
4                               0.0                    0.0   
...                             ...                    ...   
4285                          492.0                    0.0   
4286                          492.0                    0.0   
4287                          492.0                    0.0   
4288                          492.0                    0.0   
4289                          492.0                    0.0   

      last_month_total_supply  last_month_total_unsold_count  \
0                       912.0                          67786   
1                       912.0                          67786   
2                       912.0                          67786   
3                       912.0                          67786   
4                       912.0                          67786   
...                       ...                            ...   
4285                    714.0                          59806   
4286                    714.0                          59806   
4287                    714.0                          59806

In [ ]:
df_economic.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 4290 entries, 0 to 4289
Data columns (total 61 columns):
 #   Column                                        Non-Null Count  Dtype  
---  ------                                        --------------  -----  
 0   date                                          4290 non-null   object 
 1   year                                          4290 non-null   int64  
 2   month                                         4290 non-null   int64  
 3   day                                           4290 non-null   int64  
 4   kospi_index                                   4290 non-null   float64
 5   korea_rp                                      4290 non-null   float64
 6   korea_3_year                                  4290 non-null   float64
 7   korea_10_year                                 4290 non-null   float64
 8   us_3_month                                    4290 non-null   float64
 9   us_2_year                                     4290 non-null   f

In [ ]:
df_economic.to_pickle('/content/drive/MyDrive/house_price/after_data/final_economic.pkl')

>> 메모리 용량을 줄이기 위해서 타입들을 변환할 수도 있다.

>> 값들을 병합하거나 수정한 후, null 값이나 inf 값들이 존재하는 확인을 해야 한다 -> 나중에 진행이 된 다음에 발견을 하면 많은 부분을 수정해야 한다

# df_area_deal, df_area_full_rent, df_area_year_rent 파일들 생성

- '아파트 거래'가 체결된 날 이외의 날들은 가장 최근에 체결된 거래가격이 유지된다고 가정

## 필요한 데이터들 불러오기

In [ ]:
import pandas as pd
import numpy as np
# 데이터들 불러오기
df_deal = pd.read_csv("/content/drive/MyDrive/house_price/after_data/apartment_deal.csv",  encoding='UTF8')
df_month_rent = pd.read_csv("/content/drive/MyDrive/house_price/after_data/apartment_month_rent.csv",  encoding='UTF8')
df_full_rent = pd.read_csv("/content/drive/MyDrive/house_price/after_data/apartment_full_rent.csv",  encoding='UTF8')

## df_area_deal 파일 생성

- 아파트별로 가장 최근에 체결된 '평당 매매가격' 정보를 가진 데이터프레임 생성

### 아파트 월별 매매 피봇 테이블 생성

In [ ]:
# 대표 데이터 파악
df_deal.head()

date  year  month  day address_0 address_1 address_2  address_3  \
0  2011-07-09  2011      7    9     서울특별시       강남구       개포동      655.0   
1  2011-07-28  2011      7   28     서울특별시       강남구       개포동      655.0   
2  2011-01-19  2011      1   19     서울특별시       강남구       개포동      658.0   
3  2011-09-02  2011      9    2     서울특별시       강남구       개포동      658.0   
4  2011-12-17  2011     12   17     서울특별시       강남구       개포동      658.0   

   address_4            name   area  deal_price  
0        2.0  개포2차현대아파트(220)  77.75       64000  
1        2.0  개포2차현대아파트(220)  77.75       65500  
2        1.0  개포6차우성아파트1동~8동  67.28       70500  
3        1.0  개포6차우성아파트1동~8동  79.97       85000  
4        1.0  개포6차우성아파트1동~8동  67.28       68000

In [ ]:
df_deal.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 913327 entries, 0 to 913326
Data columns (total 12 columns):
 #   Column      Non-Null Count   Dtype  
---  ------      --------------   -----  
 0   date        913327 non-null  object 
 1   year        913327 non-null  int64  
 2   month       913327 non-null  int64  
 3   day         913327 non-null  int64  
 4   address_0   913327 non-null  object 
 5   address_1   913327 non-null  object 
 6   address_2   913327 non-null  object 
 7   address_3   913327 non-null  float64
 8   address_4   913327 non-null  float64
 9   name        913327 non-null  object 
 10  area        913327 non-null  float64
 11  deal_price  913327 non-null  int64  
dtypes: float64(3), int64(4), object(5)
memory usage: 83.6+ MB


In [ ]:
# 면적당 가격 컬럼을 추가
df_deal['area_deal_price'] = df_deal['deal_price'] / df_deal['area']
df_deal.head()

date  year  month  day address_0 address_1 address_2  address_3  \
0  2011-07-09  2011      7    9     서울특별시       강남구       개포동      655.0   
1  2011-07-28  2011      7   28     서울특별시       강남구       개포동      655.0   
2  2011-01-19  2011      1   19     서울특별시       강남구       개포동      658.0   
3  2011-09-02  2011      9    2     서울특별시       강남구       개포동      658.0   
4  2011-12-17  2011     12   17     서울특별시       강남구       개포동      658.0   

   address_4            name   area  deal_price  area_deal_price  
0        2.0  개포2차현대아파트(220)  77.75       64000       823.151125  
1        2.0  개포2차현대아파트(220)  77.75       65500       842.443730  
2        1.0  개포6차우성아파트1동~8동  67.28       70500      1047.859691  
3        1.0  개포6차우성아파트1동~8동  79.97       85000      1062.898587  
4        1.0  개포6차우성아파트1동~8동  67.28       68000      1010.701546

In [ ]:
# 최근에 체결된 가격이 계속 유지된다고 생각을 하고 모든 날짜의 가격들을 결정
import numpy as np
pivot_table_area_deal = df_deal.pivot_table(index=['year','month','day'], columns=['address_1','address_2','address_3','address_4'], values='area_deal_price')
pivot_table_area_deal


address_1               강남구                                               \
address_2               개포동                                                
address_3            12.0              138.0  140.0        141.0  166.0    
address_4              0.0  2.0          0.0    0.0          0.0    4.0    
year month day                                                             
2011 1     1            NaN  NaN          NaN    NaN          NaN    NaN   
           2            NaN  NaN          NaN    NaN          NaN    NaN   
           3            NaN  NaN          NaN    NaN          NaN    NaN   
           4    1018.685955  NaN          NaN    NaN          NaN    NaN   
           5    1087.781432  NaN  2101.057579    NaN  1887.191539    NaN   
...                     ...  ...          ...    ...          ...    ...   
2023 10    27           NaN  NaN          NaN    NaN          NaN    NaN   
           28           NaN  NaN          NaN    NaN          NaN    NaN   
           29           NaN  NaN          NaN    NaN          NaN    NaN   
           30           NaN  NaN          NaN    NaN          NaN    NaN   
           31           NaN  NaN          NaN    NaN          NaN    NaN   

address_1                                                                     \
address_2                                                                      
address_3      172.0  176.0  177.0  179.0        185.0  187.0  189.0  649.0    
address_4        3.0    1.0    0.0    0.0          0.0    0.0    0.0    0.0    
year month day                                                                 
2011 1     1      NaN    NaN    NaN    NaN          NaN    NaN    NaN    NaN   
           2      NaN    NaN    NaN    NaN          NaN    NaN    NaN    NaN   
           3      NaN    NaN    NaN    NaN          NaN    NaN    NaN    NaN   
           4      NaN    NaN    NaN    NaN          NaN    NaN    NaN    NaN   
           5      NaN    NaN    NaN    NaN  1218.844152    NaN    NaN    NaN   
...               ...    ...    ...    ...          ...    ...    ...    ...   
2023 10    27     NaN    NaN    NaN    NaN          NaN    NaN    NaN    NaN   
           28     NaN    NaN    NaN    NaN          NaN    NaN    NaN    NaN   
           29     NaN    NaN    NaN    NaN          NaN    NaN    NaN    NaN   
           30     NaN    NaN    NaN    NaN          NaN    NaN    NaN    NaN   
           31     NaN    NaN    NaN    NaN          NaN    NaN    NaN    NaN   

address_1                                                                 \
address_2                                                                  
address_3      651.0  652.0        653.0  654.0  655.0            656.0    
address_4        1.0    0.0          0.0    0.0    1.0  2.0  3.0    0.0    
year month day                                                             
2011 1     1      NaN    NaN          NaN    NaN    NaN  NaN  NaN    NaN   
           2      NaN    NaN          NaN    NaN    NaN  NaN  NaN    NaN   
           3      NaN    NaN          NaN    NaN    NaN  NaN  NaN    NaN   
           4      NaN    NaN          NaN    NaN    NaN  NaN  NaN    NaN   
           5      NaN    NaN  1026.278961    NaN    NaN  NaN  NaN    NaN   
...               ...    ...          ...    ...    ...  ...  ...    ...   
2023 10    27     NaN    NaN          NaN    NaN    NaN  NaN  NaN    NaN   
           28     NaN    NaN          NaN    NaN    NaN  NaN  NaN    NaN   
           29     NaN    NaN          NaN    NaN    NaN  NaN  NaN    NaN   
           30     NaN    NaN          NaN    NaN    NaN  NaN  NaN    NaN   
           31     NaN    NaN          NaN    NaN    NaN  NaN  NaN    NaN   

address_1                                                                      \
address_2                                                                       
address_3      658.0  1164.0                                    1165.0 1167.0   
address_4        1.0    7.0  12.0 13.0 14.

In [ ]:
pivot_table_area_deal.info()

<class 'pandas.core.frame.DataFrame'>
MultiIndex: 4685 entries, (2011, 1, 1) to (2023, 10, 31)
Columns: 8933 entries, ('강남구', '개포동', 12.0, 0.0) to ('중랑구', '중화동', 454.0, 0.0)
dtypes: float64(8933)
memory usage: 319.3 MB


In [ ]:
# 2011년 1월 1일부터 2023년 10월 30일 까지의 모든 일자들을 리스트에 선언
from datetime import datetime, timedelta

start_date = datetime(2011, 1, 1)  # 시작 날짜
end_date = datetime(2023, 10, 31)  # 끝 날짜

date_list = []
current_date = start_date
while current_date <= end_date:
    date_tuple = (current_date.year, current_date.month, current_date.day)
    date_list.append(date_tuple)
    current_date += timedelta(days=1)

print(date_list)

[(2011, 1, 1), (2011, 1, 2), (2011, 1, 3), (2011, 1, 4), (2011, 1, 5), (2011, 1, 6), (2011, 1, 7), (2011, 1, 8), (2011, 1, 9), (2011, 1, 10), (2011, 1, 11), (2011, 1, 12), (2011, 1, 13), (2011, 1, 14), (2011, 1, 15), (2011, 1, 16), (2011, 1, 17), (2011, 1, 18), (2011, 1, 19), (2011, 1, 20), (2011, 1, 21), (2011, 1, 22), (2011, 1, 23), (2011, 1, 24), (2011, 1, 25), (2011, 1, 26), (2011, 1, 27), (2011, 1, 28), (2011, 1, 29), (2011, 1, 30), (2011, 1, 31), (2011, 2, 1), (2011, 2, 2), (2011, 2, 3), (2011, 2, 4), (2011, 2, 5), (2011, 2, 6), (2011, 2, 7), (2011, 2, 8), (2011, 2, 9), (2011, 2, 10), (2011, 2, 11), (2011, 2, 12), (2011, 2, 13), (2011, 2, 14), (2011, 2, 15), (2011, 2, 16), (2011, 2, 17), (2011, 2, 18), (2011, 2, 19), (2011, 2, 20), (2011, 2, 21), (2011, 2, 22), (2011, 2, 23), (2011, 2, 24), (2011, 2, 25), (2011, 2, 26), (2011, 2, 27), (2011, 2, 28), (2011, 3, 1), (2011, 3, 2), (2011, 3, 3), (2011, 3, 4), (2011, 3, 5), (2011, 3, 6), (2011, 3, 7), (2011, 3, 8), (2011, 3, 9), (2011,

In [ ]:
len(date_list)

4687

In [ ]:
pivot_table_area_deal.index

MultiIndex([(2011,  1,  1),
            (2011,  1,  2),
            (2011,  1,  3),
            (2011,  1,  4),
            (2011,  1,  5),
            (2011,  1,  6),
            (2011,  1,  7),
            (2011,  1,  8),
            (2011,  1,  9),
            (2011,  1, 10),
            ...
            (2023, 10, 22),
            (2023, 10, 23),
            (2023, 10, 24),
            (2023, 10, 25),
            (2023, 10, 26),
            (2023, 10, 27),
            (2023, 10, 28),
            (2023, 10, 29),
            (2023, 10, 30),
            (2023, 10, 31)],
           names=['year', 'month', 'day'], length=4685)

In [ ]:
# 기간 내 모든 날짜들에서 '거래날짜'들 빼서 '거래날짜'에서 없는 날짜들을 고름
print(set(date_list) - set(pivot_table_area_deal.index)) # '모든날짜'에 있고 '거래날짜'에 없는 날짜
print(set(pivot_table_area_deal.index) - set(date_list)) # 잘못 추가 생성된 날짜

{(2016, 2, 9), (2022, 9, 11)}
set()


In [ ]:
# 빈 날짜 들(거래날짜에서 포함되지 않은 날짜의 거래가격들)을 null 로 채워서 row로 추가
pivot_table_area_deal.loc[(2016, 2, 9)]=np.nan
pivot_table_area_deal.loc[(2022, 9, 11)]=np.nan

In [ ]:
# 연, 월, 일 로 정렬을 함 - 정렬을 하지 않으면 바로 위에서 추가한 row들이 적절한 위치에 들어가 있지 않는다
pivot_table_area_deal = pivot_table_area_deal.sort_values(by=['year','month','day'])
pivot_table_area_deal

address_1               강남구                                               \
address_2               개포동                                                
address_3            12.0              138.0  140.0        141.0  166.0    
address_4              0.0  2.0          0.0    0.0          0.0    4.0    
year month day                                                             
2011 1     1            NaN  NaN          NaN    NaN          NaN    NaN   
           2            NaN  NaN          NaN    NaN          NaN    NaN   
           3            NaN  NaN          NaN    NaN          NaN    NaN   
           4    1018.685955  NaN          NaN    NaN          NaN    NaN   
           5    1087.781432  NaN  2101.057579    NaN  1887.191539    NaN   
...                     ...  ...          ...    ...          ...    ...   
2023 10    27           NaN  NaN          NaN    NaN          NaN    NaN   
           28           NaN  NaN          NaN    NaN          NaN    NaN   
           29           NaN  NaN          NaN    NaN          NaN    NaN   
           30           NaN  NaN          NaN    NaN          NaN    NaN   
           31           NaN  NaN          NaN    NaN          NaN    NaN   

address_1                                                                     \
address_2                                                                      
address_3      172.0  176.0  177.0  179.0        185.0  187.0  189.0  649.0    
address_4        3.0    1.0    0.0    0.0          0.0    0.0    0.0    0.0    
year month day                                                                 
2011 1     1      NaN    NaN    NaN    NaN          NaN    NaN    NaN    NaN   
           2      NaN    NaN    NaN    NaN          NaN    NaN    NaN    NaN   
           3      NaN    NaN    NaN    NaN          NaN    NaN    NaN    NaN   
           4      NaN    NaN    NaN    NaN          NaN    NaN    NaN    NaN   
           5      NaN    NaN    NaN    NaN  1218.844152    NaN    NaN    NaN   
...               ...    ...    ...    ...          ...    ...    ...    ...   
2023 10    27     NaN    NaN    NaN    NaN          NaN    NaN    NaN    NaN   
           28     NaN    NaN    NaN    NaN          NaN    NaN    NaN    NaN   
           29     NaN    NaN    NaN    NaN          NaN    NaN    NaN    NaN   
           30     NaN    NaN    NaN    NaN          NaN    NaN    NaN    NaN   
           31     NaN    NaN    NaN    NaN          NaN    NaN    NaN    NaN   

address_1                                                                 \
address_2                                                                  
address_3      651.0  652.0        653.0  654.0  655.0            656.0    
address_4        1.0    0.0          0.0    0.0    1.0  2.0  3.0    0.0    
year month day                                                             
2011 1     1      NaN    NaN          NaN    NaN    NaN  NaN  NaN    NaN   
           2      NaN    NaN          NaN    NaN    NaN  NaN  NaN    NaN   
           3      NaN    NaN          NaN    NaN    NaN  NaN  NaN    NaN   
           4      NaN    NaN          NaN    NaN    NaN  NaN  NaN    NaN   
           5      NaN    NaN  1026.278961    NaN    NaN  NaN  NaN    NaN   
...               ...    ...          ...    ...    ...  ...  ...    ...   
2023 10    27     NaN    NaN          NaN    NaN    NaN  NaN  NaN    NaN   
           28     NaN    NaN          NaN    NaN    NaN  NaN  NaN    NaN   
           29     NaN    NaN          NaN    NaN    NaN  NaN  NaN    NaN   
           30     NaN    NaN          NaN    NaN    NaN  NaN  NaN    NaN   
           31     NaN    NaN          NaN    NaN    NaN  NaN  NaN    NaN   

address_1                                                                      \
address_2                                                                       
address_3      658.0  1164.0                                    1165.0 1167.0   
address_4        1.0    7.0  12.0 13.0 14.

In [ ]:
# 가장 최근에 체결된 값이 거래가격으로 유지 됨으로 ffill()을 사용
pivot_table_area_deal=pivot_table_area_deal.ffill()
pivot_table_area_deal

address_1               강남구                                         \
address_2               개포동                                          
address_3            12.0                      138.0        140.0    
address_4              0.0          2.0          0.0          0.0    
year month day                                                       
2011 1     1            NaN          NaN          NaN          NaN   
           2            NaN          NaN          NaN          NaN   
           3            NaN          NaN          NaN          NaN   
           4    1018.685955          NaN          NaN          NaN   
           5    1087.781432          NaN  2101.057579          NaN   
...                     ...          ...          ...          ...   
2023 10    27   3134.418324  1842.889054  3481.293903  2487.219819   
           28   3134.418324  1842.889054  3481.293903  2487.219819   
           29   3134.418324  1842.889054  3481.293903  2487.219819   
           30   3134.418324  1842.889054  3481.293903  2487.219819   
           31   3134.418324  1842.889054  3481.293903  2487.219819   

address_1                                                           \
address_2                                                            
address_3            141.0        166.0        172.0        176.0    
address_4              0.0          4.0          3.0          1.0    
year month day                                                       
2011 1     1            NaN          NaN          NaN          NaN   
           2            NaN          NaN          NaN          NaN   
           3            NaN          NaN          NaN          NaN   
           4            NaN          NaN          NaN          NaN   
           5    1887.191539          NaN          NaN          NaN   
...                     ...          ...          ...          ...   
2023 10    27   4324.324324  1413.594063  1342.758827  2172.968275   
           28   4324.324324  1413.594063  1342.758827  2172.968275   
           29   4324.324324  1413.594063  1342.758827  2172.968275   
           30   4324.324324  1413.594063  1342.758827  2172.968275   
           31   4324.324324  1413.594063  1342.758827  2172.968275   

address_1                                                                      \
address_2                                                                       
address_3            177.0        179.0        185.0       187.0       189.0    
address_4              0.0          0.0          0.0         0.0         0.0    
year month day                                                                  
2011 1     1            NaN          NaN          NaN         NaN         NaN   
           2            NaN          NaN          NaN         NaN         NaN   
           3            NaN          NaN          NaN         NaN         NaN   
           4            NaN          NaN          NaN         NaN         NaN   
           5            NaN          NaN  1218.844152         NaN         NaN   
...                     ...          ...          ...         ...         ...   
2023 10    27   2768.940733  2386.634845  3385.203385  2639.73064  3656.21874   
           28   2768.940733  2386.634845  3385.203385  2639.73064  3656.21874   
           29   2768.940733  2386.634845  3385.203385  2639.73064  3656.21874   
           30   2768.940733  2386.634845  3385.203385  2639.73064  3656.21874   
           31   2768.940733  2386.634845  3385.203385  2639.73064  3656.21874   

address_1                                                           \
address_2                                                            
address_3            649.0        651.0        652.0        653.0    
address_4              0.0          1.0          0.0          0.0    
year month day                                                       
2011 1     1            NaN          NaN          NaN          NaN   
           2            NaN          NaN 

In [ ]:
# null 값을 채움 - 값을 채우지 않으면 추후 stack을 할 때 null 값을 계산을 안함
pivot_table_area_deal = pivot_table_area_deal.fillna(0)
pivot_table_area_deal

address_1               강남구                                         \
address_2               개포동                                          
address_3            12.0                      138.0        140.0    
address_4              0.0          2.0          0.0          0.0    
year month day                                                       
2011 1     1       0.000000     0.000000     0.000000     0.000000   
           2       0.000000     0.000000     0.000000     0.000000   
           3       0.000000     0.000000     0.000000     0.000000   
           4    1018.685955     0.000000     0.000000     0.000000   
           5    1087.781432     0.000000  2101.057579     0.000000   
...                     ...          ...          ...          ...   
2023 10    27   3134.418324  1842.889054  3481.293903  2487.219819   
           28   3134.418324  1842.889054  3481.293903  2487.219819   
           29   3134.418324  1842.889054  3481.293903  2487.219819   
           30   3134.418324  1842.889054  3481.293903  2487.219819   
           31   3134.418324  1842.889054  3481.293903  2487.219819   

address_1                                                           \
address_2                                                            
address_3            141.0        166.0        172.0        176.0    
address_4              0.0          4.0          3.0          1.0    
year month day                                                       
2011 1     1       0.000000     0.000000     0.000000     0.000000   
           2       0.000000     0.000000     0.000000     0.000000   
           3       0.000000     0.000000     0.000000     0.000000   
           4       0.000000     0.000000     0.000000     0.000000   
           5    1887.191539     0.000000     0.000000     0.000000   
...                     ...          ...          ...          ...   
2023 10    27   4324.324324  1413.594063  1342.758827  2172.968275   
           28   4324.324324  1413.594063  1342.758827  2172.968275   
           29   4324.324324  1413.594063  1342.758827  2172.968275   
           30   4324.324324  1413.594063  1342.758827  2172.968275   
           31   4324.324324  1413.594063  1342.758827  2172.968275   

address_1                                                                      \
address_2                                                                       
address_3            177.0        179.0        185.0       187.0       189.0    
address_4              0.0          0.0          0.0         0.0         0.0    
year month day                                                                  
2011 1     1       0.000000     0.000000     0.000000     0.00000     0.00000   
           2       0.000000     0.000000     0.000000     0.00000     0.00000   
           3       0.000000     0.000000     0.000000     0.00000     0.00000   
           4       0.000000     0.000000     0.000000     0.00000     0.00000   
           5       0.000000     0.000000  1218.844152     0.00000     0.00000   
...                     ...          ...          ...         ...         ...   
2023 10    27   2768.940733  2386.634845  3385.203385  2639.73064  3656.21874   
           28   2768.940733  2386.634845  3385.203385  2639.73064  3656.21874   
           29   2768.940733  2386.634845  3385.203385  2639.73064  3656.21874   
           30   2768.940733  2386.634845  3385.203385  2639.73064  3656.21874   
           31   2768.940733  2386.634845  3385.203385  2639.73064  3656.21874   

address_1                                                           \
address_2                                                            
address_3            649.0        651.0        652.0        653.0    
address_4              0.0          1.0          0.0          0.0    
year month day                                                       
2011 1     1       0.000000     0.000000     0.000000     0.000000   
           2       0.000000     0.000000 

### 피봇테이블 -> 데이터프레임

In [ ]:
# 컬럼을 slice해서 값을 처리할 때, 컬럼의 개수가 많으면, row가 많을 때 보다 메모리를 많이 소모함으로 전치를 시킴
pivot_table_area_deal = pivot_table_area_deal.T
pivot_table_area_deal

year                                    2011                          \
month                                     1                            
day                                       1           2           3    
address_1 address_2 address_3 address_4                                
강남구       개포동       12.0      0.0        0.0    0.000000    0.000000   
                              2.0        0.0    0.000000    0.000000   
                    138.0     0.0        0.0    0.000000    0.000000   
                    140.0     0.0        0.0    0.000000    0.000000   
                    141.0     0.0        0.0    0.000000    0.000000   
...                                      ...         ...         ...   
중랑구       중화동       438.0     0.0        0.0    0.000000    0.000000   
                    450.0     0.0        0.0  431.726908  431.726908   
                    452.0     0.0        0.0    0.000000    0.000000   
                    453.0     0.0        0.0    0.000000    0.000000   
                    454.0     0.0        0.0    0.000000    0.000000   

year                                                               \
month                                                               
day                                               4            5    
address_1 address_2 address_3 address_4                             
강남구       개포동       12.0      0.0        1018.685955  1087.781432   
                              2.0           0.000000     0.000000   
                    138.0     0.0           0.000000  2101.057579   
                    140.0     0.0           0.000000     0.000000   
                    141.0     0.0           0.000000  1887.191539   
...                                              ...          ...   
중랑구       중화동       438.0     0.0           0.000000     0.000000   
                    450.0     0.0         431.726908   431.726908   
                    452.0     0.0           0.000000     0.000000   
                    453.0     0.0           0.000000     0.000000   
                    454.0     0.0           0.000000     0.000000   

year                                                               \
month                                                               
day                                               6            7    
address_1 address_2 address_3 address_4                             
강남구       개포동       12.0      0.0        1040.914561  1054.852321   
                              2.0           0.000000     0.000000   
                    138.0     0.0        2101.057579  2101.057579   
                    140.0     0.0           0.000000     0.000000   
                    141.0     0.0        1887.191539  1887.191539   
...                                              ...          ...   
중랑구       중화동       438.0     0.0           0.000000     0.000000   
                    450.0     0.0         485.274431   485.274431   
                    452.0     0.0           0.000000     0.000000   
                    453.0     0.0           0.000000     0.000000   
                    454.0     0.0           0.000000     0.000000   

year                                                               \
month                                                               
day                                               8            9    
address_1 address_2 address_3 address_4                             
강남구       개포동       12.0      0.0        1054.852321  1054.852321   
                              2.0           0.000000     0.000000   
                    138.0     0.0        2101.057579  2101.057579   
                    140.0     0.0           0.000000  1565.991903   
                    141.0     0.0        1887.191539  1887.191539   
...                                              ...          ...   
중랑구       중화동       438.0     0.0           0.000000     0.000000   
                    450.0     0.0         485.274431   485.274431   
                   

- pandas는 row 개수가 많은것이, column의 개수가 많은 것보다 더 메모리 부담이 크다

In [ ]:
# 피봇테이블을 일반데이터프레임화
df_area_deal = pivot_table_area_deal.stack(level=[0,1,2])
df_area_deal =df_area_deal.reset_index()
df_area_deal

address_1 address_2  address_3  address_4  year  month  day  \
0              강남구       개포동       12.0        0.0  2011      1    1   
1              강남구       개포동       12.0        0.0  2011      1    2   
2              강남구       개포동       12.0        0.0  2011      1    3   
3              강남구       개포동       12.0        0.0  2011      1    4   
4              강남구       개포동       12.0        0.0  2011      1    5   
...            ...       ...        ...        ...   ...    ...  ...   
41868966       중랑구       중화동      454.0        0.0  2023     10   27   
41868967       중랑구       중화동      454.0        0.0  2023     10   28   
41868968       중랑구       중화동      454.0        0.0  2023     10   29   
41868969       중랑구       중화동      454.0        0.0  2023     10   30   
41868970       중랑구       중화동      454.0        0.0  2023     10   31   

                    0  
0            0.000000  
1            0.000000  
2            0.000000  
3         1018.685955  
4         1087.781432  
...               ...  
41868966  1131.141746  
41868967  1131.141746  
41868968  1131.141746  
41868969  1131.141746  
41868970  1131.141746  

[41868971 rows x 8 columns]

In [ ]:
df_area_deal.columns = ['address_1','address_2','address_3','address_4','year','month','day','area_deal'] # 컬럼명 수정
df_area_deal = df_area_deal.astype({'address_3': 'int16', 'address_4': 'int16','year':'int16', 'month':'int16', 'day':'int16', 'area_deal':'float32'}) # 데이터 타입 변경
df_area_deal = df_area_deal.drop(df_area_deal[df_area_deal.area_deal == 0].index) # 위에서 값이 null인 값들을 0으로 처리했으므로, 0인 값들을 제거한다
df_area_deal

address_1 address_2  address_3  address_4  year  month  day  \
3              강남구       개포동         12          0  2011      1    4   
4              강남구       개포동         12          0  2011      1    5   
5              강남구       개포동         12          0  2011      1    6   
6              강남구       개포동         12          0  2011      1    7   
7              강남구       개포동         12          0  2011      1    8   
...            ...       ...        ...        ...   ...    ...  ...   
41868966       중랑구       중화동        454          0  2023     10   27   
41868967       중랑구       중화동        454          0  2023     10   28   
41868968       중랑구       중화동        454          0  2023     10   29   
41868969       중랑구       중화동        454          0  2023     10   30   
41868970       중랑구       중화동        454          0  2023     10   31   

            area_deal  
3         1018.685974  
4         1087.781372  
5         1040.914551  
6         1054.852295  
7         1054.852295  
...               ...  
41868966  1131.141724  
41868967  1131.141724  
41868968  1131.141724  
41868969  1131.141724  
41868970  1131.141724  

[35550086 rows x 8 columns]

In [ ]:
df_area_deal.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 35550086 entries, 3 to 41868970
Data columns (total 8 columns):
 #   Column     Dtype  
---  ------     -----  
 0   address_1  object 
 1   address_2  object 
 2   address_3  int16  
 3   address_4  int16  
 4   year       int16  
 5   month      int16  
 6   day        int16  
 7   area_deal  float32
dtypes: float32(1), int16(5), object(2)
memory usage: 1.3+ GB


### 파일저장

In [ ]:
df_area_deal.to_pickle('/content/drive/MyDrive/house_price/after_data/df_area_deal.pkl')

## df_area_full_rent 파일 생성

- 아파트별로 가장 최근에 체결된 '평당 전세가격' 정보를 가진 데이터프레임 생성

- df_area_deal 파일생성 부분 참조

In [ ]:
df_full_rent.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1580989 entries, 0 to 1580988
Data columns (total 12 columns):
 #   Column           Non-Null Count    Dtype  
---  ------           --------------    -----  
 0   date             1580989 non-null  object 
 1   year             1580989 non-null  int64  
 2   month            1580989 non-null  int64  
 3   day              1580989 non-null  int64  
 4   address_0        1580989 non-null  object 
 5   address_1        1580989 non-null  object 
 6   address_2        1580989 non-null  object 
 7   address_3        1580989 non-null  float64
 8   address_4        1580989 non-null  float64
 9   name             1580989 non-null  object 
 10  area             1580989 non-null  float64
 11  full_rent_price  1580989 non-null  int64  
dtypes: float64(3), int64(4), object(5)
memory usage: 144.7+ MB


In [ ]:
import numpy as np
# 면적당 가격을 추가
df_full_rent['area_full_rent_price'] = df_full_rent['full_rent_price'] / df_full_rent['area']
pivot_table_area_full_rent = df_full_rent.pivot_table(index=['year','month','day'], columns=['address_1','address_2','address_3','address_4'], values='area_full_rent_price')
pivot_table_area_full_rent

address_1              강남구                                                   \
address_2              개포동                                                    
address_3            12.0                     138.0       140.0       141.0   
address_4             0.0         2.0          0.0         0.0         0.0    
year month day                                                                
2011 1     1           NaN         NaN          NaN         NaN         NaN   
           2           NaN         NaN          NaN         NaN         NaN   
           3    430.053124  469.099032          NaN         NaN  190.044764   
           4    416.009890         NaN          NaN  259.109312  159.620342   
           5           NaN         NaN   217.090981  267.487606  212.476466   
...                    ...         ...          ...         ...         ...   
2023 10    27   802.246290         NaN  1706.688512         NaN         NaN   
           28   848.576322         NaN          NaN         NaN         NaN   
           29          NaN         NaN          NaN         NaN         NaN   
           30   806.208559         NaN          NaN         NaN         NaN   
           31          NaN         NaN          NaN         NaN         NaN   

address_1                                           ...   중랑구        \
address_2                                           ...   중화동         
address_3      166.0 172.0 176.0       177.0 179.0  ... 307.0 314.0   
address_4       4.0   3.0   1.0         0.0   0.0   ...  76.0  1.0    
year month day                                      ...               
2011 1     1     NaN   NaN   NaN         NaN   NaN  ...   NaN   NaN   
           2     NaN   NaN   NaN         NaN   NaN  ...   NaN   NaN   
           3     NaN   NaN   NaN         NaN   NaN  ...   NaN   NaN   
           4     NaN   NaN   NaN         NaN   NaN  ...   NaN   NaN   
           5     NaN   NaN   NaN         NaN   NaN  ...   NaN   NaN   
...              ...   ...   ...         ...   ...  ...   ...   ...   
2023 10    27    NaN   NaN   NaN         NaN   NaN  ...   NaN   NaN   
           28    NaN   NaN   NaN  883.704489   NaN  ...   NaN   NaN   
           29    NaN   NaN   NaN         NaN   NaN  ...   NaN   NaN   
           30    NaN   NaN   NaN         NaN   NaN  ...   NaN   NaN   
           31    NaN   NaN   NaN         NaN   NaN  ...   NaN   NaN   

address_1                                                                   
address_2                                                                   
address_3            318.0 331.0 413.0 438.0       450.0 452.0 453.0 454.0  
address_4             81.0  64.0  8.0   0.0         0.0   0.0   0.0   0.0   
year month day                                                              
2011 1     1           NaN   NaN   NaN   NaN         NaN   NaN   NaN   NaN  
           2           NaN   NaN   NaN   NaN         NaN   NaN   NaN   NaN  
           3           NaN   NaN   NaN   NaN         NaN   NaN   NaN   NaN  
           4    203.665988   NaN   NaN   NaN  251.004016   NaN   NaN   NaN  
           5           NaN   NaN   NaN   NaN  190.408188   NaN   NaN   NaN  
...                    ...   ...   ...   ...         ...   ...   ...   ...  
2023 10    27          NaN   NaN   NaN   NaN         NaN   NaN   NaN   NaN  
           28          NaN   NaN   NaN   NaN  669.344043   NaN   NaN   NaN  
           29          NaN   NaN   NaN   NaN  568.942436   NaN   NaN   NaN  
           30          NaN   NaN   NaN   NaN  491.967871   NaN   NaN   NaN  
           31          NaN   NaN   NaN   NaN         NaN   NaN   NaN   NaN  

[4687 rows x 9340 columns]

In [ ]:
from datetime import datetime, timedelta

start_date = datetime(2011, 1, 1)  # 시작 날짜
end_date = datetime(2023, 10, 31)  # 끝 날짜

date_list = []
current_date = start_date
while current_date <= end_date:
    date_tuple = (current_date.year, current_date.month, current_date.day)
    date_list.append(date_tuple)
    current_date += timedelta(days=1)

# 기간 내 모든 날짜들에서 '거래날짜'들 빼서 '거래날짜'에서 없는 날짜들을 고름
print(set(date_list) - set(pivot_table_area_full_rent.index)) # '모든날짜'에 있고 '거래날짜'에 없는 날짜
print(set(pivot_table_area_full_rent.index) - set(date_list)) # 잘못 추가 생성된 날짜

set()
set()


In [ ]:
pivot_table_area_full_rent = pivot_table_area_full_rent.ffill()
pivot_table_area_full_rent = pivot_table_area_full_rent.fillna(0)
pivot_table_area_full_rent = pivot_table_area_full_rent.T
df_area_full_rent = pivot_table_area_full_rent.stack(level=[0,1,2])
df_area_full_rent =df_area_full_rent.reset_index()
df_area_full_rent.columns = ['address_1','address_2','address_3','address_4','year','month','day','area_full_rent'] # 컬럼명 수정
df_area_full_rent = df_area_full_rent.drop(df_area_full_rent[df_area_full_rent.area_full_rent == 0].index) # 위에서 값이 null인 값들을 0으로 처리했으므로, 0인 값들을 제거한다
df_area_full_rent = df_area_full_rent.astype({'address_3': 'int16', 'address_4': 'int16','year':'int16', 'month':'int16', 'day':'int16', 'area_full_rent':'float32'})
df_area_full_rent

address_1 address_2  address_3  address_4  year  month  day  \
2              강남구       개포동         12          0  2011      1    3   
3              강남구       개포동         12          0  2011      1    4   
4              강남구       개포동         12          0  2011      1    5   
5              강남구       개포동         12          0  2011      1    6   
6              강남구       개포동         12          0  2011      1    7   
...            ...       ...        ...        ...   ...    ...  ...   
43776575       중랑구       중화동        454          0  2023     10   27   
43776576       중랑구       중화동        454          0  2023     10   28   
43776577       중랑구       중화동        454          0  2023     10   29   
43776578       중랑구       중화동        454          0  2023     10   30   
43776579       중랑구       중화동        454          0  2023     10   31   

          area_full_rent  
2             430.053131  
3             416.009888  
4             416.009888  
5             416.009888  
6             400.000000  
...                  ...  
43776575      571.462219  
43776576      571.462219  
43776577      571.462219  
43776578      571.462219  
43776579      571.462219  

[37345835 rows x 8 columns]

In [ ]:
df_area_full_rent.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 37345835 entries, 2 to 43776579
Data columns (total 8 columns):
 #   Column          Dtype  
---  ------          -----  
 0   address_1       object 
 1   address_2       object 
 2   address_3       int16  
 3   address_4       int16  
 4   year            int16  
 5   month           int16  
 6   day             int16  
 7   area_full_rent  float32
dtypes: float32(1), int16(5), object(2)
memory usage: 1.3+ GB


In [ ]:
df_area_full_rent.to_pickle('/content/drive/MyDrive/house_price/after_data/df_area_full_rent.pkl')

## df_area_year_rent 파일 생성

- 아파트별로 가장 최근에 체결된 '평당 월세가격' 정보를 가진 데이터프레임 생성

- df_area_deal 파일 생성 참조
- 아파트월세 피봇테이블 -> 아파트 월별 연세 피봇테이블
- 보증금은 계약시의 상황마다 다를 것
- 전월세전환률을 적용하여서 월세에서의 보증금을 변환
- 거래들마다 상황에 따라 보증금과 월세금액은 다를 수 있음으로, 보증금의 5.8% 값에 월세*12을 더하여 1년간 들어가는 금액인 연세를 계산

In [ ]:
df_month_rent.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 729704 entries, 0 to 729703
Data columns (total 13 columns):
 #   Column            Non-Null Count   Dtype  
---  ------            --------------   -----  
 0   date              729704 non-null  object 
 1   year              729704 non-null  int64  
 2   month             729704 non-null  int64  
 3   day               729704 non-null  int64  
 4   address_0         729704 non-null  object 
 5   address_1         729704 non-null  object 
 6   address_2         729704 non-null  object 
 7   address_3         729704 non-null  float64
 8   address_4         729704 non-null  float64
 9   name              729704 non-null  object 
 10  area              729704 non-null  float64
 11  rent_deposit      729704 non-null  int64  
 12  month_rent_price  729704 non-null  int64  
dtypes: float64(3), int64(5), object(5)
memory usage: 72.4+ MB


In [ ]:
# 보증금의 5.8% 값에 월세*12을 더하여 1년간 들어가는 금액인 연세를 계산
df_month_rent['year_rent_price'] = (df_month_rent['rent_deposit']*0.058)+(df_month_rent['month_rent_price']*12)
df_month_rent['area_year_rent_price'] = df_month_rent['year_rent_price'] / df_month_rent['area']
pivot_table_area_year_rent = df_month_rent.pivot_table(index=['year','month','day'], columns=['address_1','address_2','address_3','address_4'], values='area_year_rent_price')
pivot_table_area_year_rent

address_1             강남구                                                      \
address_2             개포동                                                       
address_3           12.0            138.0 140.0 141.0 172.0 176.0 177.0 179.0   
address_4            0.0  2.0        0.0   0.0   0.0   3.0   1.0   0.0   0.0    
year month day                                                                  
2011 1     1          NaN  NaN        NaN   NaN   NaN   NaN   NaN   NaN   NaN   
           2          NaN  NaN        NaN   NaN   NaN   NaN   NaN   NaN   NaN   
           3          NaN  NaN        NaN   NaN   NaN   NaN   NaN   NaN   NaN   
           4          NaN  NaN        NaN   NaN   NaN   NaN   NaN   NaN   NaN   
           5          NaN  NaN  18.284371   NaN   NaN   NaN   NaN   NaN   NaN   
...                   ...  ...        ...   ...   ...   ...   ...   ...   ...   
2023 10    27         NaN  NaN        NaN   NaN   NaN   NaN   NaN   NaN   NaN   
           28         NaN  NaN        NaN   NaN   NaN   NaN   NaN   NaN   NaN   
           29         NaN  NaN        NaN   NaN   NaN   NaN   NaN   NaN   NaN   
           30         NaN  NaN        NaN   NaN   NaN   NaN   NaN   NaN   NaN   
           31   53.124209  NaN  89.874814   NaN   NaN   NaN   NaN   NaN   NaN   

address_1                  ...   중랑구                                           \
address_2                  ...   중화동                                            
address_3           185.0  ... 307.0      314.0 318.0 331.0 438.0 450.0 452.0   
address_4            0.0   ...  6.0  76.0  1.0   81.0  64.0  0.0   0.0   0.0    
year month day             ...                                                  
2011 1     1          NaN  ...   NaN  NaN   NaN   NaN   NaN   NaN   NaN   NaN   
           2          NaN  ...   NaN  NaN   NaN   NaN   NaN   NaN   NaN   NaN   
           3          NaN  ...   NaN  NaN   NaN   NaN   NaN   NaN   NaN   NaN   
           4    29.702312  ...   NaN  NaN   NaN   NaN   NaN   NaN   NaN   NaN   
           5          NaN  ...   NaN  NaN   NaN   NaN   NaN   NaN   NaN   NaN   
...                   ...  ...   ...  ...   ...   ...   ...   ...   ...   ...   
2023 10    27         NaN  ...   NaN  NaN   NaN   NaN   NaN   NaN   NaN   NaN   
           28   30.885711  ...   NaN  NaN   NaN   NaN   NaN   NaN   NaN   NaN   
           29         NaN  ...   NaN  NaN   NaN   NaN   NaN   NaN   NaN   NaN   
           30   38.070109  ...   NaN  NaN   NaN   NaN   NaN   NaN   NaN   NaN   
           31         NaN  ...   NaN  NaN   NaN   NaN   NaN   NaN   NaN   NaN   

address_1                   
address_2                   
address_3      453.0 454.0  
address_4       0.0   0.0   
year month day              
2011 1     1     NaN   NaN  
           2     NaN   NaN  
           3     NaN   NaN  
           4     NaN   NaN  
           5     NaN   NaN  
...              ...   ...  
2023 10    27    NaN   NaN  
           28    NaN   NaN  
           29    NaN   NaN  
           30    NaN   NaN  
           31    NaN   NaN  

[4687 rows x 8571 columns]

In [ ]:
from datetime import datetime, timedelta

start_date = datetime(2011, 1, 1)  # 시작 날짜
end_date = datetime(2023, 10, 31)  # 끝 날짜

date_list = []
current_date = start_date
while current_date <= end_date:
    date_tuple = (current_date.year, current_date.month, current_date.day)
    date_list.append(date_tuple)
    current_date += timedelta(days=1)

# 기간 내 모든 날짜들에서 '거래날짜'들 빼서 '거래날짜'에서 없는 날짜들을 고름
print(set(date_list) - set(pivot_table_area_year_rent.index)) # '모든날짜'에 있고 '거래날짜'에 없는 날짜
print(set(pivot_table_area_year_rent.index) - set(date_list)) # 잘못 추가 생성된 날짜

set()
set()


In [ ]:
pivot_table_area_year_rent=pivot_table_area_year_rent.ffill()
pivot_table_area_year_rent = pivot_table_area_year_rent.fillna(0)

# 피봇테이블을 일반데이터프레임화
pivot_table_area_year_rent = pivot_table_area_year_rent.T
df_area_year_rent = pivot_table_area_year_rent.stack(level=[0,1,2])
df_area_year_rent = df_area_year_rent.reset_index()
df_area_year_rent.columns = ['address_1','address_2','address_3','address_4','year','month','day','area_year_rent'] # 컬럼명 수정
df_area_year_rent = df_area_year_rent.drop(df_area_year_rent[df_area_year_rent.area_year_rent == 0].index) # 위에서 값이 null인 값들을 0으로 처리했으므로, 0인 값들을 제거한다
df_area_year_rent = df_area_year_rent.astype({'address_3': 'int16', 'address_4': 'int16','year':'int16', 'month':'int16', 'day':'int16', 'area_year_rent':'float32'})
df_area_year_rent

address_1 address_2  address_3  address_4  year  month  day  \
6              강남구       개포동         12          0  2011      1    7   
7              강남구       개포동         12          0  2011      1    8   
8              강남구       개포동         12          0  2011      1    9   
9              강남구       개포동         12          0  2011      1   10   
10             강남구       개포동         12          0  2011      1   11   
...            ...       ...        ...        ...   ...    ...  ...   
40172272       중랑구       중화동        454          0  2023     10   27   
40172273       중랑구       중화동        454          0  2023     10   28   
40172274       중랑구       중화동        454          0  2023     10   29   
40172275       중랑구       중화동        454          0  2023     10   30   
40172276       중랑구       중화동        454          0  2023     10   31   

          area_year_rent  
6              30.255503  
7              30.255503  
8              30.255503  
9              30.255503  
10             30.255503  
...                  ...  
40172272       30.705395  
40172273       30.705395  
40172274       30.705395  
40172275       30.705395  
40172276       30.705395  

[29822452 rows x 8 columns]

In [ ]:
df_area_year_rent.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 29822452 entries, 6 to 40172276
Data columns (total 8 columns):
 #   Column          Dtype  
---  ------          -----  
 0   address_1       object 
 1   address_2       object 
 2   address_3       int16  
 3   address_4       int16  
 4   year            int16  
 5   month           int16  
 6   day             int16  
 7   area_year_rent  float32
dtypes: float32(1), int16(5), object(2)
memory usage: 1.1+ GB


In [ ]:
df_area_year_rent.to_pickle('/content/drive/MyDrive/house_price/after_data/df_area_year_rent.pkl')

## df_area_all 파일 생성

- df_area_deal, df_area_full_rent, df_area_year_rent 3개의 파일 병합하여 df_area_all을 생성
- 가치평가 컬럼들을 구하기 위해서 merge를 통해, 매매가, 전세가, 연세가 기록이 다 있는 아파트 만을 선택

In [ ]:
import pandas as pd

df_area_deal = pd.read_pickle('/content/drive/MyDrive/house_price/after_data/df_area_deal.pkl')
df_area_full_rent = pd.read_pickle('/content/drive/MyDrive/house_price/after_data/df_area_full_rent.pkl')

In [ ]:
df_area_deal_full_rent = pd.merge(df_area_deal,df_area_full_rent, on=['address_1', 'address_2', 'address_3', 'address_4', 'year', 'month','day'])

In [ ]:
df_area_deal_full_rent.to_pickle('/content/drive/MyDrive/house_price/after_data/df_area_deal_full_rent.pkl')

- 메모리 부족 이슈로 나누어서 실행

In [ ]:
import pandas as pd

df_area_deal_full_rent = pd.read_pickle('/content/drive/MyDrive/house_price/after_data/df_area_deal_full_rent.pkl')
df_area_year_rent = pd.read_pickle('/content/drive/MyDrive/house_price/after_data/df_area_year_rent.pkl')

In [ ]:
df_area_all = pd.merge(df_area_deal_full_rent, df_area_year_rent , on=['address_1', 'address_2', 'address_3', 'address_4', 'year', 'month','day'])

In [ ]:
df_area_all.to_pickle('/content/drive/MyDrive/house_price/after_data/df_area_all.pkl')

# df_original_dataset 생성

- df_original_dataset은 df_area_all의 정보 추가적인 변화 정보들을 추가하고, final_economic 들까지 병합한 데이터프레임

## 일별로 종합 수치들을 확인

In [ ]:
import pandas as pd

df_area_all = pd.read_pickle('/content/drive/MyDrive/house_price/after_data/df_area_all.pkl')
df_area_all.head()

address_1 address_2  address_3  address_4  year  month  day    area_deal  \
0       강남구       개포동         12          0  2011      1    7  1054.852295   
1       강남구       개포동         12          0  2011      1    8  1054.852295   
2       강남구       개포동         12          0  2011      1    9  1054.852295   
3       강남구       개포동         12          0  2011      1   10  1054.852295   
4       강남구       개포동         12          0  2011      1   11  1006.830261   

   area_full_rent  area_year_rent  
0      400.000000       30.255503  
1      400.000000       30.255503  
2      400.000000       30.255503  
3      420.425629       30.255503  
4      434.408142       30.255503

In [ ]:
df_area_all.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 26467941 entries, 0 to 26467940
Data columns (total 10 columns):
 #   Column          Dtype  
---  ------          -----  
 0   address_1       object 
 1   address_2       object 
 2   address_3       int16  
 3   address_4       int16  
 4   year            int16  
 5   month           int16  
 6   day             int16  
 7   area_deal       float32
 8   area_full_rent  float32
 9   area_year_rent  float32
dtypes: float32(3), int16(5), object(2)
memory usage: 1.1+ GB


In [ ]:
# 실제 메모리 사용량 확인
real_memory_usage = df_area_all.memory_usage(deep=True).sum() # deep 옵션을 통해서 정확한 메모리 사용량을 확인
print(real_memory_usage/(1024**3),'GB')

5.086982175707817 GB


## 데이터 필터링

- 일별로 초반의 데이터들은 계약체결의 개수가 적어서 데이터의 신빙성이 확보되기가 어렵다 판단
- 일별 거래(매매,전세, 월세) 체결 개수들을 파악해서 너무 개수가 적은 데이터 들을 제거하는 과정 필요
- 개수가 적은 기준은 IQR를 사용하여서 이상치에 해당하는 개수가 적은 기준을 세움

In [ ]:
df_area_all_count = df_area_all.groupby(["year","month","day"])[["area_deal","area_full_rent","area_year_rent"]].count()
df_area_all_count

area_deal  area_full_rent  area_year_rent
year month day                                           
2011 1     2            1               1               1
           3            6               6               6
           4           18              18              18
           5           43              43              43
           6           79              79              79
...                   ...             ...             ...
2023 10    27        7728            7728            7728
           28        7728            7728            7728
           29        7728            7728            7728
           30        7729            7729            7729
           31        7730            7730            7730

[4686 rows x 3 columns]

>> 데이터셋을 사용할 때, 각 수치들을 도출한 표본이 어느정도 이상이어야지 데이터로서의 가치가 있다

In [ ]:
df_area_all_count.describe() # min의 값과 1분위수의 차이가 매우 큼을 확인

area_deal  area_full_rent  area_year_rent
count  4686.000000     4686.000000     4686.000000
mean   5648.301536     5648.301536     5648.301536
std    1663.565707     1663.565707     1663.565707
min       1.000000        1.000000        1.000000
25%    4544.250000     4544.250000     4544.250000
50%    6106.500000     6106.500000     6106.500000
75%    7007.750000     7007.750000     7007.750000
max    7730.000000     7730.000000     7730.000000

In [ ]:
# boxplot 을 통해서 이상치가 있음을 확인
import plotly.express as px
fig = px.box(df_area_all_count, y="area_deal")
fig.show()

In [ ]:
# 막대그래프를 통해서 체결 개수는 순차적으로 증가함을 확인
# 즉, 특정 개수 이하인 value 기준으로 row들을 제거하면, 과거일자들의 value들도 특정개수 이하일 것이므로, 제거해도 괜찮음을 확인
import plotly.express as px

df_area_all_count_2 = df_area_all_count.reset_index()
fig = px.bar(df_area_all_count, x=df_area_all_count_2.index, y='area_deal')
fig.show()

In [ ]:
# 이상치 제거를 위한 변수들을 선언
q1=df_area_all_count['area_deal'].quantile(0.25)
q2=df_area_all_count['area_deal'].quantile(0.5)
q3=df_area_all_count['area_deal'].quantile(0.75)
iqr=q3-q1
iqr

2463.5

In [ ]:
# 이상치의 인덱스들을 확인
df_area_all_count.loc[df_area_all_count['area_deal']<q1-1.5*iqr,'area_deal'].index


MultiIndex([(2011, 1,  2),
            (2011, 1,  3),
            (2011, 1,  4),
            (2011, 1,  5),
            (2011, 1,  6),
            (2011, 1,  7),
            (2011, 1,  8),
            (2011, 1,  9),
            (2011, 1, 10),
            (2011, 1, 11),
            (2011, 1, 12),
            (2011, 1, 13),
            (2011, 1, 14),
            (2011, 1, 15),
            (2011, 1, 16),
            (2011, 1, 17),
            (2011, 1, 18),
            (2011, 1, 19),
            (2011, 1, 20),
            (2011, 1, 21),
            (2011, 1, 22),
            (2011, 1, 23),
            (2011, 1, 24),
            (2011, 1, 25),
            (2011, 1, 26),
            (2011, 1, 27),
            (2011, 1, 28),
            (2011, 1, 29),
            (2011, 1, 30),
            (2011, 1, 31),
            (2011, 2,  1),
            (2011, 2,  2),
            (2011, 2,  3),
            (2011, 2,  4),
            (2011, 2,  5),
            (2011, 2,  6),
            (2011, 2,  7),
 

## df_area_micro 생성

- df_area_micro는 df_original_dataset을 만드는 과정 중에 생기는 데이터프레임으로, df_area_all 에 가치평가 지표와 과거수치 대비 변화율들의 정보를 추가한 데이터프레임

### 일별로 그룹화 진행


- 우선, 일별로 거래정보들을 그룹화 해서 평균 가격들을 도출

In [ ]:
df_area_micro=df_area_all.groupby(["year","month","day"])[["area_deal","area_full_rent","area_year_rent"]].mean()
df_area_micro

area_deal  area_full_rent  area_year_rent
year month day                                             
2011 1     2     595.000000      259.771637       18.880535
           3     519.548096      274.167999       16.547453
           4     704.231018      326.309021       21.519497
           5     768.772095      326.750854       21.022175
           6     709.595642      303.017273       19.990875
...                     ...             ...             ...
2023 10    27   1029.540405      596.237915       30.427759
           28   1029.958740      596.546021       30.465477
           29   1029.966797      596.627197       30.464407
           30   1030.069458      596.618347       30.486279
           31   1029.982300      596.441956       30.495527

[4686 rows x 3 columns]

In [ ]:
# 위에서 구한 데이터의 개수가 적어서 데이터로서의 가치가 떨어지는 데이터들을 제거
df_area_micro.drop(df_area_all_count.loc[df_area_all_count['area_deal']<q1-1.5*iqr,'area_deal'].index,inplace=True)
df_area_micro

area_deal  area_full_rent  area_year_rent
year month day                                             
2011 2     10    649.267273      303.338654       21.142321
           11    644.917053      302.780884       21.052322
           12    641.195679      300.848663       21.090029
           13    640.122192      300.396454       21.067911
           14    638.963379      298.462372       20.963787
...                     ...             ...             ...
2023 10    27   1029.540405      596.237915       30.427759
           28   1029.958740      596.546021       30.465477
           29   1029.966797      596.627197       30.464407
           30   1030.069458      596.618347       30.486279
           31   1029.982300      596.441956       30.495527

[4647 rows x 3 columns]

In [ ]:
df_area_micro.reset_index(inplace=True)
df_area_micro

year  month  day    area_deal  area_full_rent  area_year_rent
0     2011      2   10   649.267273      303.338654       21.142321
1     2011      2   11   644.917053      302.780884       21.052322
2     2011      2   12   641.195679      300.848663       21.090029
3     2011      2   13   640.122192      300.396454       21.067911
4     2011      2   14   638.963379      298.462372       20.963787
...    ...    ...  ...          ...             ...             ...
4642  2023     10   27  1029.540405      596.237915       30.427759
4643  2023     10   28  1029.958740      596.546021       30.465477
4644  2023     10   29  1029.966797      596.627197       30.464407
4645  2023     10   30  1030.069458      596.618347       30.486279
4646  2023     10   31  1029.982300      596.441956       30.495527

[4647 rows x 6 columns]

#### 가치평가 지표 컬럼 추가

- 전세가율(deal_full_rent_rate), 연세멀티플(deal_year_rent_multiple) 을 계산함

In [ ]:
df_area_micro['deal_full_rent_rate'] = 100*(df_area_micro['area_full_rent'] / df_area_micro['area_deal'])
df_area_micro['deal_year_rent_multiple'] = df_area_micro['area_deal']/ df_area_micro['area_year_rent']
df_area_micro

year  month  day    area_deal  area_full_rent  area_year_rent  \
0     2011      2   10   649.267273      303.338654       21.142321   
1     2011      2   11   644.917053      302.780884       21.052322   
2     2011      2   12   641.195679      300.848663       21.090029   
3     2011      2   13   640.122192      300.396454       21.067911   
4     2011      2   14   638.963379      298.462372       20.963787   
...    ...    ...  ...          ...             ...             ...   
4642  2023     10   27  1029.540405      596.237915       30.427759   
4643  2023     10   28  1029.958740      596.546021       30.465477   
4644  2023     10   29  1029.966797      596.627197       30.464407   
4645  2023     10   30  1030.069458      596.618347       30.486279   
4646  2023     10   31  1029.982300      596.441956       30.495527   

      deal_full_rent_rate  deal_year_rent_multiple  
0               46.720150                30.709366  
1               46.948811                30.634010  
2               46.919945                30.402788  
3               46.927986                30.383753  
4               46.710403                30.479387  
...                   ...                      ...  
4642            57.913017                33.835564  
4643            57.919407                33.807407  
4644            57.926838                33.808857  
4645            57.920204                33.787971  
4646            57.907982                33.774864  

[4647 rows x 8 columns]

### 월별 평균 종합 수치들을 확인

- 6개월, 12개월전 수치들을 일별을 기준으로 하면, 너무 특정일자 기준으로 하는 것 같아서, 월별을 기준으로 변화율을 계산하기 위해서 월별 평균 종합 수치들을 확인

In [ ]:
df_area_micro_month = df_area_micro.groupby(["year","month"])[["area_deal","area_full_rent","area_year_rent"]].mean().copy()
df_area_micro_month.reset_index(inplace=True)
df_area_micro_month

year  month    area_deal  area_full_rent  area_year_rent
0    2011      2   636.811462      298.967072       20.891218
1    2011      3   615.491150      297.227692       20.475676
2    2011      4   600.585022      295.111023       20.246986
3    2011      5   589.073303      295.179962       20.066994
4    2011      6   581.239624      297.469910       19.992504
..    ...    ...          ...             ...             ...
148  2023      6  1021.233032      582.908325       29.696184
149  2023      7  1021.891541      584.898132       29.837887
150  2023      8  1024.649536      588.286255       30.112097
151  2023      9  1027.772583      591.920471       30.319450
152  2023     10  1029.624878      595.448975       30.425653

[153 rows x 5 columns]

In [ ]:
# 체결일자의 발표일자가 1달 씩 미뤄진다 생각하고 1칸씩 미룸
df_area_micro_month['area_deal'] = df_area_micro_month['area_deal'].shift(1)
df_area_micro_month['area_full_rent'] = df_area_micro_month['area_full_rent'].shift(1)
df_area_micro_month['area_year_rent'] = df_area_micro_month['area_year_rent'].shift(1)
df_area_micro_month = df_area_micro_month.dropna()
df_area_micro_month.columns = ['year','month','last_month_area_deal','last_month_area_full_count', 'last_month_area_year_rent']
df_area_micro_month

year  month  last_month_area_deal  last_month_area_full_count  \
1    2011      3            636.811462                  298.967072   
2    2011      4            615.491150                  297.227692   
3    2011      5            600.585022                  295.111023   
4    2011      6            589.073303                  295.179962   
5    2011      7            581.239624                  297.469910   
..    ...    ...                   ...                         ...   
148  2023      6           1021.817688                  581.627808   
149  2023      7           1021.233032                  582.908325   
150  2023      8           1021.891541                  584.898132   
151  2023      9           1024.649536                  588.286255   
152  2023     10           1027.772583                  591.920471   

     last_month_area_year_rent  
1                    20.891218  
2                    20.475676  
3                    20.246986  
4                    20.066994  
5                    19.992504  
..                         ...  
148                  29.655708  
149                  29.696184  
150                  29.837887  
151                  30.112097  
152                  30.319450  

[152 rows x 5 columns]

#### 6개월전 종합 수치 병합

In [ ]:
# df_area_micro_month의 6개월 후, 연, 월을 컬럼으로 구한후, df_area_micro의 year, month와 merge 하면 6개월 전 수치들을 구할 수 있음
df_area_micro_month_6m = df_area_micro_month.copy()
df_area_micro_month_6m.loc[df_area_micro_month_6m['month']<7, '6m_after_year'] = df_area_micro_month_6m['year']
df_area_micro_month_6m.loc[df_area_micro_month_6m['month']<7, '6m_after_month'] = df_area_micro_month_6m['month'] + 6
df_area_micro_month_6m.loc[df_area_micro_month_6m['month']>=7, '6m_after_year'] = df_area_micro_month_6m['year'] + 1
df_area_micro_month_6m.loc[df_area_micro_month_6m['month']>=7, '6m_after_month'] = df_area_micro_month_6m['month'] - 6

df_area_micro_month_6m



year  month  last_month_area_deal  last_month_area_full_count  \
1    2011      3            636.811462                  298.967072   
2    2011      4            615.491150                  297.227692   
3    2011      5            600.585022                  295.111023   
4    2011      6            589.073303                  295.179962   
5    2011      7            581.239624                  297.469910   
..    ...    ...                   ...                         ...   
148  2023      6           1021.817688                  581.627808   
149  2023      7           1021.233032                  582.908325   
150  2023      8           1021.891541                  584.898132   
151  2023      9           1024.649536                  588.286255   
152  2023     10           1027.772583                  591.920471   

     last_month_area_year_rent  6m_after_year  6m_after_month  
1                    20.891218         2011.0             9.0  
2                    20.475676         2011.0            10.0  
3                    20.246986         2011.0            11.0  
4                    20.066994         2011.0            12.0  
5                    19.992504         2012.0             1.0  
..                         ...            ...             ...  
148                  29.655708         2023.0            12.0  
149                  29.696184         2024.0             1.0  
150                  29.837887         2024.0             2.0  
151                  30.112097         2024.0             3.0  
152                  30.319450         2024.0             4.0  

[152 rows x 7 columns]

In [ ]:
df_area_micro_month_6m = df_area_micro_month_6m.drop(['year','month'],axis=1)
df_area_micro_month_6m = df_area_micro_month_6m.astype({'6m_after_year':'int16', '6m_after_month' : 'int16'})
df_area_micro_month_6m.rename(columns = {'last_month_area_deal' : '6m_before_area_deal_mean', 'last_month_area_full_count' : '6m_before_area_full_rent_mean',
                                      'last_month_area_year_rent' : '6m_before_area_year_rent_mean'}, inplace = True)
df_area_micro_month_6m

6m_before_area_deal_mean  6m_before_area_full_rent_mean  \
1                  636.811462                     298.967072   
2                  615.491150                     297.227692   
3                  600.585022                     295.111023   
4                  589.073303                     295.179962   
5                  581.239624                     297.469910   
..                        ...                            ...   
148               1021.817688                     581.627808   
149               1021.233032                     582.908325   
150               1021.891541                     584.898132   
151               1024.649536                     588.286255   
152               1027.772583                     591.920471   

     6m_before_area_year_rent_mean  6m_after_year  6m_after_month  
1                        20.891218           2011               9  
2                        20.475676           2011              10  
3                        20.246986           2011              11  
4                        20.066994           2011              12  
5                        19.992504           2012               1  
..                             ...            ...             ...  
148                      29.655708           2023              12  
149                      29.696184           2024               1  
150                      29.837887           2024               2  
151                      30.112097           2024               3  
152                      30.319450           2024               4  

[152 rows x 5 columns]

In [ ]:
df_area_micro_month_6m['6m_before_deal_full_rent_rate'] = 100*(df_area_micro_month_6m['6m_before_area_full_rent_mean'] / df_area_micro_month_6m['6m_before_area_deal_mean'])
df_area_micro_month_6m['6m_before_deal_year_rent_multiple'] = df_area_micro_month_6m['6m_before_area_deal_mean']/ df_area_micro_month_6m['6m_before_area_year_rent_mean']
df_area_micro_month_6m

6m_before_area_deal_mean  6m_before_area_full_rent_mean  \
1                  636.811462                     298.967072   
2                  615.491150                     297.227692   
3                  600.585022                     295.111023   
4                  589.073303                     295.179962   
5                  581.239624                     297.469910   
..                        ...                            ...   
148               1021.817688                     581.627808   
149               1021.233032                     582.908325   
150               1021.891541                     584.898132   
151               1024.649536                     588.286255   
152               1027.772583                     591.920471   

     6m_before_area_year_rent_mean  6m_after_year  6m_after_month  \
1                        20.891218           2011               9   
2                        20.475676           2011              10   
3                        20.246986           2011              11   
4                        20.066994           2011              12   
5                        19.992504           2012               1   
..                             ...            ...             ...   
148                      29.655708           2023              12   
149                      29.696184           2024               1   
150                      29.837887           2024               2   
151                      30.112097           2024               3   
152                      30.319450           2024               4   

     6m_before_deal_full_rent_rate  6m_before_deal_year_rent_multiple  
1                        46.947502                          30.482256  
2                        48.291142                          30.059626  
3                        49.137260                          29.662933  
4                        50.109207                          29.355333  
5                        51.178532                          29.072878  
..                             ...                                ...  
148                      56.920898                          34.456020  
149                      57.078873                          34.389370  
150                      57.236809                          34.248119  
151                      57.413410                          34.027836  
152                      57.592552                          33.898129  

[152 rows x 7 columns]

In [ ]:
df_area_micro = pd.merge(df_area_micro,df_area_micro_month_6m, left_on=['year','month'], right_on=['6m_after_year','6m_after_month'],how = 'left') # inner로 하면, 12개월 파트를 병합할 때 사라지는 데이터가 더 많아짐 ㅠㅠㅠ
df_area_micro

year  month  day    area_deal  area_full_rent  area_year_rent  \
0     2011      2   10   649.267273      303.338654       21.142321   
1     2011      2   11   644.917053      302.780884       21.052322   
2     2011      2   12   641.195679      300.848663       21.090029   
3     2011      2   13   640.122192      300.396454       21.067911   
4     2011      2   14   638.963379      298.462372       20.963787   
...    ...    ...  ...          ...             ...             ...   
4642  2023     10   27  1029.540405      596.237915       30.427759   
4643  2023     10   28  1029.958740      596.546021       30.465477   
4644  2023     10   29  1029.966797      596.627197       30.464407   
4645  2023     10   30  1030.069458      596.618347       30.486279   
4646  2023     10   31  1029.982300      596.441956       30.495527   

      deal_full_rent_rate  deal_year_rent_multiple  6m_before_area_deal_mean  \
0               46.720150                30.709366                       NaN   
1               46.948811                30.634010                       NaN   
2               46.919945                30.402788                       NaN   
3               46.927986                30.383753                       NaN   
4               46.710403                30.479387                       NaN   
...                   ...                      ...                       ...   
4642            57.913017                33.835564               1030.953491   
4643            57.919407                33.807407               1030.953491   
4644            57.926838                33.808857               1030.953491   
4645            57.920204                33.787971               1030.953491   
4646            57.907982                33.774864               1030.953491   

      6m_before_area_full_rent_mean  6m_before_area_year_rent_mean  \
0                               NaN                            NaN   
1                               NaN                            NaN   
2                               NaN                            NaN   
3                               NaN                            NaN   
4                               NaN                            NaN   
...                             ...                            ...   
4642                     583.086731                      29.516256   
4643                     583.086731                      29.516256   
4644                     583.086731                      29.516256   
4645                     583.086731                      29.516256   
4646                     583.086731                      29.516256   

      6m_after_year  6m_after_month  6m_before_deal_full_rent_rate  \
0               NaN             NaN                            NaN   
1               NaN             NaN                            NaN   
2               NaN             NaN                            NaN   
3               NaN             NaN                            NaN   
4               NaN             NaN                            NaN   
...             ...             ...                            ...   
4642         2023.0            10.0                      56.558006   
4643         2023.0            10.0                      56.558006   
4644         2023.0            10.0                      56.558006   
4645         2023.0            10.0                      56.558006   
4646         2023.0            10.0                      56.558006   

      6m_before_deal_year_rent_multiple  
0                                   NaN  
1                                   NaN  
2                                   NaN  
3                                   NaN  
4                                   NaN  
...                                 ...  
4642                          34.928329  
4643                          34.928329  
4644                          34.928329  
4645                          34.928329  
4646                          34.928329  

[4647

#### 12개월전 종합 수치 병합

In [ ]:
df_area_micro_month_12m = df_area_micro_month.copy()
df_area_micro_month_12m['12m_after_year'] = df_area_micro_month_12m['year']+1
df_area_micro_month_12m['12m_after_month'] = df_area_micro_month_12m['month']

df_area_micro_month_12m = df_area_micro_month_12m.drop(['year','month'],axis=1)
df_area_micro_month_12m = df_area_micro_month_12m.astype({'12m_after_year':'int16', '12m_after_month' : 'int16'})
df_area_micro_month_12m.rename(columns = {'last_month_area_deal' : '12m_before_area_deal_mean', 'last_month_area_full_count' : '12m_before_area_full_rent_mean',
                                      'last_month_area_year_rent' : '12m_before_area_year_rent_mean'}, inplace = True)

df_area_micro_month_12m['12m_before_deal_full_rent_rate'] = 100*(df_area_micro_month_12m['12m_before_area_full_rent_mean'] / df_area_micro_month_12m['12m_before_area_deal_mean'])
df_area_micro_month_12m['12m_before_deal_year_rent_multiple'] =df_area_micro_month_12m['12m_before_area_deal_mean']/ df_area_micro_month_12m['12m_before_area_year_rent_mean']


df_area_micro = pd.merge(df_area_micro, df_area_micro_month_12m, left_on=['year','month'], right_on=['12m_after_year','12m_after_month'],how = 'left')
df_area_micro

year  month  day    area_deal  area_full_rent  area_year_rent  \
0     2011      2   10   649.267273      303.338654       21.142321   
1     2011      2   11   644.917053      302.780884       21.052322   
2     2011      2   12   641.195679      300.848663       21.090029   
3     2011      2   13   640.122192      300.396454       21.067911   
4     2011      2   14   638.963379      298.462372       20.963787   
...    ...    ...  ...          ...             ...             ...   
4642  2023     10   27  1029.540405      596.237915       30.427759   
4643  2023     10   28  1029.958740      596.546021       30.465477   
4644  2023     10   29  1029.966797      596.627197       30.464407   
4645  2023     10   30  1030.069458      596.618347       30.486279   
4646  2023     10   31  1029.982300      596.441956       30.495527   

      deal_full_rent_rate  deal_year_rent_multiple  6m_before_area_deal_mean  \
0               46.720150                30.709366                       NaN   
1               46.948811                30.634010                       NaN   
2               46.919945                30.402788                       NaN   
3               46.927986                30.383753                       NaN   
4               46.710403                30.479387                       NaN   
...                   ...                      ...                       ...   
4642            57.913017                33.835564               1030.953491   
4643            57.919407                33.807407               1030.953491   
4644            57.926838                33.808857               1030.953491   
4645            57.920204                33.787971               1030.953491   
4646            57.907982                33.774864               1030.953491   

      6m_before_area_full_rent_mean  ...  6m_after_month  \
0                               NaN  ...             NaN   
1                               NaN  ...             NaN   
2                               NaN  ...             NaN   
3                               NaN  ...             NaN   
4                               NaN  ...             NaN   
...                             ...  ...             ...   
4642                     583.086731  ...            10.0   
4643                     583.086731  ...            10.0   
4644                     583.086731  ...            10.0   
4645                     583.086731  ...            10.0   
4646                     583.086731  ...            10.0   

      6m_before_deal_full_rent_rate  6m_before_deal_year_rent_multiple  \
0                               NaN                                NaN   
1                               NaN                                NaN   
2                               NaN                                NaN   
3                               NaN                                NaN   
4                               NaN                                NaN   
...                             ...                                ...   
4642                      56.558006                          34.928329   
4643                      56.558006                          34.928329   
4644                      56.558006                          34.928329   
4645                      56.558006                          34.928329   
4646                      56.558006                          34.928329   

      12m_before_area_deal_mean  12m_before_area_full_rent_mean  \
0                           NaN                             NaN   
1                           NaN                             NaN   
2                           NaN                             NaN   
3                           NaN                             NaN   
4                           NaN                             NaN   
...                         ...                             ...   
4642                1079.784546                      619.757629   
4643                1079.784546               

### df_area_micro 컬럼 수정

- 6개월, 12개월 전 수치들을 변화율들로 계산하여 교체

In [ ]:
df_area_micro = df_area_micro.drop(['6m_after_year','6m_after_month', '12m_after_year', '12m_after_month'], axis=1)

df_area_micro['6m_before_area_deal_mean'] = 100*((df_area_micro['area_deal'] - df_area_micro['6m_before_area_deal_mean'])/ df_area_micro['6m_before_area_deal_mean'])
df_area_micro['6m_before_area_full_rent_mean'] = 100*((df_area_micro['area_full_rent'] - df_area_micro['6m_before_area_full_rent_mean'])/ df_area_micro['6m_before_area_full_rent_mean'])
df_area_micro['6m_before_area_year_rent_mean'] = 100*((df_area_micro['area_year_rent'] - df_area_micro['6m_before_area_year_rent_mean'])/ df_area_micro['6m_before_area_year_rent_mean'])
df_area_micro['6m_before_deal_full_rent_rate'] = 100*((df_area_micro['deal_full_rent_rate'] - df_area_micro['6m_before_deal_full_rent_rate'])/ df_area_micro['6m_before_deal_full_rent_rate'])
df_area_micro['6m_before_deal_year_rent_multiple'] = 100*((df_area_micro['deal_year_rent_multiple'] - df_area_micro['6m_before_deal_year_rent_multiple'])/ df_area_micro['6m_before_deal_year_rent_multiple'])


df_area_micro['12m_before_area_deal_mean'] = 100*((df_area_micro['area_deal'] - df_area_micro['12m_before_area_deal_mean'])/ df_area_micro['12m_before_area_deal_mean'])
df_area_micro['12m_before_area_full_rent_mean'] = 100*((df_area_micro['area_full_rent'] - df_area_micro['12m_before_area_full_rent_mean'])/ df_area_micro['12m_before_area_full_rent_mean'])
df_area_micro['12m_before_area_year_rent_mean'] = 100*((df_area_micro['area_year_rent'] - df_area_micro['12m_before_area_year_rent_mean'])/ df_area_micro['12m_before_area_year_rent_mean'])
df_area_micro['12m_before_deal_full_rent_rate'] = 100*((df_area_micro['deal_full_rent_rate'] - df_area_micro['12m_before_deal_full_rent_rate'])/ df_area_micro['12m_before_deal_full_rent_rate'])
df_area_micro['12m_before_deal_year_rent_multiple'] = 100*((df_area_micro['deal_year_rent_multiple'] - df_area_micro['12m_before_deal_year_rent_multiple'])/ df_area_micro['12m_before_deal_year_rent_multiple'])

df_area_micro.head()

year  month  day   area_deal  area_full_rent  area_year_rent  \
0  2011      2   10  649.267273      303.338654       21.142321   
1  2011      2   11  644.917053      302.780884       21.052322   
2  2011      2   12  641.195679      300.848663       21.090029   
3  2011      2   13  640.122192      300.396454       21.067911   
4  2011      2   14  638.963379      298.462372       20.963787   

   deal_full_rent_rate  deal_year_rent_multiple  6m_before_area_deal_mean  \
0            46.720150                30.709366                       NaN   
1            46.948811                30.634010                       NaN   
2            46.919945                30.402788                       NaN   
3            46.927986                30.383753                       NaN   
4            46.710403                30.479387                       NaN   

   6m_before_area_full_rent_mean  6m_before_area_year_rent_mean  \
0                            NaN                            NaN   
1                            NaN                            NaN   
2                            NaN                            NaN   
3                            NaN                            NaN   
4                            NaN                            NaN   

   6m_before_deal_full_rent_rate  6m_before_deal_year_rent_multiple  \
0                            NaN                                NaN   
1                            NaN                                NaN   
2                            NaN                                NaN   
3                            NaN                                NaN   
4                            NaN                                NaN   

   12m_before_area_deal_mean  12m_before_area_full_rent_mean  \
0                        NaN                             NaN   
1                        NaN                             NaN   
2                        NaN                             NaN   
3                        NaN                             NaN   
4                        NaN                             NaN   

   12m_before_area_year_rent_mean  12m_before_deal_full_rent_rate  \
0                             NaN                             NaN   
1                             NaN                             NaN   
2                             NaN                             NaN   
3                             NaN                             NaN   
4                             NaN                             NaN   

   12m_before_deal_year_rent_multiple  
0                                 NaN  
1                                 NaN  
2                                 NaN  
3                                 NaN  
4                                 NaN

In [ ]:
df_area_micro = df_area_micro.dropna()
df_area_micro.head()

year  month  day   area_deal  area_full_rent  area_year_rent  \
385  2012      3    1  548.170105      309.035980       20.537769   
386  2012      3    2  547.971802      308.738037       20.522972   
387  2012      3    3  547.847473      309.738129       20.533909   
388  2012      3    4  548.025452      309.982178       20.534513   
389  2012      3    5  547.768799      309.442413       20.514805   

     deal_full_rent_rate  deal_year_rent_multiple  6m_before_area_deal_mean  \
385            56.375927                26.690830                 -4.654602   
386            56.341957                26.700411                 -4.689094   
387            56.537292                26.680136                 -4.710719   
388            56.563461                26.688017                 -4.679762   
389            56.491428                26.701145                 -4.724403   

     6m_before_area_full_rent_mean  6m_before_area_year_rent_mean  \
385                       1.893891                       1.922042   
386                       1.795654                       1.848608   
387                       2.125400                       1.902884   
388                       2.205867                       1.905884   
389                       2.027898                       1.808077   

     6m_before_deal_full_rent_rate  6m_before_deal_year_rent_multiple  \
385                       6.868177                          -6.452623   
386                       6.803782                          -6.419044   
387                       7.174067                          -6.490106   
388                       7.223673                          -6.462483   
389                       7.087125                          -6.416471   

     12m_before_area_deal_mean  12m_before_area_full_rent_mean  \
385                 -13.919560                        3.367899   
386                 -13.950701                        3.268241   
387                 -13.970224                        3.602757   
388                 -13.942276                        3.684388   
389                 -13.982579                        3.503844   

     12m_before_area_year_rent_mean  12m_before_deal_full_rent_rate  \
385                       -1.691854                       20.082911   
386                       -1.762684                       20.010553   
387                       -1.710333                       20.426624   
388                       -1.707439                       20.482367   
389                       -1.801778                       20.328934   

     12m_before_deal_year_rent_multiple  
385                          -12.438140  
386                          -12.406710  
387                          -12.473225  
388                          -12.447370  
389                          -12.404301

In [ ]:
df_area_micro.tail()

year  month  day    area_deal  area_full_rent  area_year_rent  \
4642  2023     10   27  1029.540405      596.237915       30.427759   
4643  2023     10   28  1029.958740      596.546021       30.465477   
4644  2023     10   29  1029.966797      596.627197       30.464407   
4645  2023     10   30  1030.069458      596.618347       30.486279   
4646  2023     10   31  1029.982300      596.441956       30.495527   

      deal_full_rent_rate  deal_year_rent_multiple  6m_before_area_deal_mean  \
4642            57.913017                33.835564                 -0.137066   
4643            57.919407                33.807407                 -0.096488   
4644            57.926838                33.808857                 -0.095707   
4645            57.920204                33.787971                 -0.085749   
4646            57.907982                33.774864                 -0.094203   

      6m_before_area_full_rent_mean  6m_before_area_year_rent_mean  \
4642                       2.255442                       3.088138   
4643                       2.308283                       3.215925   
4644                       2.322204                       3.212300   
4645                       2.320687                       3.286400   
4646                       2.290435                       3.317734   

      6m_before_deal_full_rent_rate  6m_before_deal_year_rent_multiple  \
4642                       2.395790                          -3.128595   
4643                       2.407087                          -3.209206   
4644                       2.420226                          -3.205056   
4645                       2.408497                          -3.264851   
4646                       2.386887                          -3.302377   

      12m_before_area_deal_mean  12m_before_area_full_rent_mean  \
4642                  -4.653163                       -3.794986   
4643                  -4.614421                       -3.745272   
4644                  -4.613675                       -3.732174   
4645                  -4.604167                       -3.733602   
4646                  -4.612239                       -3.762064   

      12m_before_area_year_rent_mean  12m_before_deal_full_rent_rate  \
4642                        0.891465                        0.900052   
4643                        1.016528                        0.911185   
4644                        1.012981                        0.924131   
4645                        1.085502                        0.912574   
4646                        1.116168                        0.891279   

      12m_before_deal_year_rent_multiple  
4642                           -5.495639  
4643                           -5.574280  
4644                           -5.570232  
4645                           -5.628566  
4646                           -5.665175

In [ ]:
df_area_micro.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 4262 entries, 385 to 4646
Data columns (total 18 columns):
 #   Column                              Non-Null Count  Dtype  
---  ------                              --------------  -----  
 0   year                                4262 non-null   int64  
 1   month                               4262 non-null   int64  
 2   day                                 4262 non-null   int64  
 3   area_deal                           4262 non-null   float32
 4   area_full_rent                      4262 non-null   float32
 5   area_year_rent                      4262 non-null   float32
 6   deal_full_rent_rate                 4262 non-null   float32
 7   deal_year_rent_multiple             4262 non-null   float32
 8   6m_before_area_deal_mean            4262 non-null   float32
 9   6m_before_area_full_rent_mean       4262 non-null   float32
 10  6m_before_area_year_rent_mean       4262 non-null   float32
 11  6m_before_deal_full_rent_rate       4262 

In [ ]:
df_area_micro.to_pickle('/content/drive/MyDrive/house_price/after_data/df_area_micro.pkl')

## final_economic 과의 병합

In [ ]:
import pandas as pd
df_area_micro = pd.read_pickle('/content/drive/MyDrive/house_price/after_data/df_area_micro.pkl')
df_area_micro

year  month  day    area_deal  area_full_rent  area_year_rent  \
394   2012      3    1   548.170105      309.035980       20.537769   
395   2012      3    2   547.971802      308.738037       20.522972   
396   2012      3    3   547.847473      309.738129       20.533909   
397   2012      3    4   548.025452      309.982178       20.534513   
398   2012      3    5   547.768799      309.442413       20.514805   
...    ...    ...  ...          ...             ...             ...   
4467  2023      4   26  1024.179443      580.640137       29.545254   
4468  2023      4   27  1024.288940      580.863586       29.561056   
4469  2023      4   28  1024.102783      581.085632       29.577700   
4470  2023      4   29  1023.981995      581.219116       29.587328   
4471  2023      4   30  1023.966125      581.314514       29.594040   

      deal_full_rent_rate  deal_year_rent_multiple  6m_before_area_deal_mean  \
394             56.375927                26.690830                 -4.654602   
395             56.341957                26.700411                 -4.689094   
396             56.537292                26.680136                 -4.710719   
397             56.563461                26.688017                 -4.679762   
398             56.491428                26.701145                 -4.724403   
...                   ...                      ...                       ...   
4467            56.693203                34.664772                 -5.149648   
4468            56.708954                34.649944                 -5.139507   
4469            56.740944                34.624153                 -5.156748   
4470            56.760674                34.608803                 -5.167934   
4471            56.770874                34.600418                 -5.169404   

      6m_before_area_full_rent_mean  6m_before_area_year_rent_mean  \
394                        1.893891                       1.922042   
395                        1.795654                       1.848608   
396                        2.125400                       1.902884   
397                        2.205867                       1.905884   
398                        2.027898                       1.808077   
...                             ...                            ...   
4467                      -6.311741                      -2.039094   
4468                      -6.275686                      -1.986700   
4469                      -6.239858                      -1.931516   
4470                      -6.218320                      -1.899592   
4471                      -6.202927                      -1.877338   

      6m_before_deal_full_rent_rate  6m_before_deal_year_rent_multiple  \
394                        6.868177                          -6.452623   
395                        6.803782                          -6.419044   
396                        7.174067                          -6.490106   
397                        7.223673                          -6.462483   
398                        7.087125                          -6.416471   
...                             ...                                ...   
4467                      -1.225192                          -3.175297   
4468                      -1.197750                          -3.216714   
4469                      -1.142015                          -3.288753   
4470                      -1.107641                          -3.331629   
4471                      -1.089869                          -3.355049   

      12m_before_area_deal_mean  12m_before_area_full_rent_mean  \
394                  -14.525463                        2.814531   
395                  -14.556384                        2.715407   
396                  -14.575770                        3.048131   
397                  -14.548018                        3.129325   
398                  -14.588037                        2.949749   
...                         ...                             

In [ ]:
import pandas as pd
df_economic = pd.read_pickle('/content/drive/MyDrive/house_price/after_data/final_economic.pkl')
df_economic

date  year  month  day  kospi_index  korea_rp  korea_3_year  \
0     2012-02-01  2012      2    1      1959.24      3.25         3.380   
1     2012-02-02  2012      2    2      1984.30      3.25         3.380   
2     2012-02-03  2012      2    3      1972.34      3.25         3.380   
3     2012-02-04  2012      2    4      1972.34      3.25         3.380   
4     2012-02-05  2012      2    5      1972.34      3.25         3.380   
...          ...   ...    ...  ...          ...       ...           ...   
4285  2023-10-26  2023     10   26      2299.08      3.50         3.692   
4286  2023-10-27  2023     10   27      2302.81      3.50         3.692   
4287  2023-10-28  2023     10   28      2302.81      3.50         3.692   
4288  2023-10-29  2023     10   29      2302.81      3.50         3.692   
4289  2023-10-30  2023     10   30      2310.55      3.50         3.692   

      korea_10_year  us_3_month  us_2_year  ...  \
0             3.750       0.061      0.226  ...   
1             3.760       0.084      0.226  ...   
2             3.760       0.079      0.238  ...   
3             3.760       0.079      0.238  ...   
4             3.760       0.079      0.238  ...   
...             ...         ...        ...  ...   
4285          3.977       5.479      5.046  ...   
4286          3.977       5.477      5.015  ...   
4287          3.977       5.477      5.015  ...   
4288          3.977       5.477      5.015  ...   
4289          3.977       5.481      5.050  ...   

      last_month_etc_supply_12m_before  last_month_total_supply_12m_before  \
0                                  0.0                               265.0   
1                                  0.0                               265.0   
2                                  0.0                               265.0   
3                                  0.0                               265.0   
4                                  0.0                               265.0   
...                                ...                                 ...   
4285                            -150.0                               535.0   
4286                            -150.0                               535.0   
4287                            -150.0                               535.0   
4288                            -150.0                               535.0   
4289                            -150.0                               535.0   

      last_month_total_unsold_count_12m_before  \
0                                     -17137.0   
1                                     -17137.0   
2                                     -17137.0   
3                                     -17137.0   
4                                     -17137.0   
...                                        ...   
4285                                   18202.0   
4286                                   18202.0   
4287                                   18202.0   
4288                                   18202.0   
4289                                   18202.0   

      last_month_total_deal_count_12m_before  \
0                                    -4393.0   
1                                    -4393.0   
2                                    -4393.0   
3                                    -4393.0   
4                                    -4393.0   
...                                      ...   
4285                                  2799.0   
4286                                  2799.0   
4287                                  2799.0   
4288                                  2799.0   
4289                                  2799.0   

      last_month_total_full_rent_count_12m_before  \
0                                         -1891.0   
1                                         -1891.0   
2                                         -1891.0   
3                                         -1891.0   
4                                         -1891.0   
...                                           ...   
4285        

In [ ]:
df_original_dataset = pd.merge(df_area_micro,df_economic, on = ['year','month','day'])
df_original_dataset

year  month  day    area_deal  area_full_rent  area_year_rent  \
0     2012      3    1   548.170105      309.035980       20.537769   
1     2012      3    2   547.971802      308.738037       20.522972   
2     2012      3    3   547.847473      309.738129       20.533909   
3     2012      3    4   548.025452      309.982178       20.534513   
4     2012      3    5   547.768799      309.442413       20.514805   
...    ...    ...  ...          ...             ...             ...   
4256  2023     10   26  1029.659058      596.442871       30.401781   
4257  2023     10   27  1029.540405      596.237915       30.427759   
4258  2023     10   28  1029.958740      596.546021       30.465477   
4259  2023     10   29  1029.966797      596.627197       30.464407   
4260  2023     10   30  1030.069458      596.618347       30.486279   

      deal_full_rent_rate  deal_year_rent_multiple  6m_before_area_deal_mean  \
0               56.375927                26.690830                 -4.654602   
1               56.341957                26.700411                 -4.689094   
2               56.537292                26.680136                 -4.710719   
3               56.563461                26.688017                 -4.679762   
4               56.491428                26.701145                 -4.724403   
...                   ...                      ...                       ...   
4256            57.926250                33.868378                 -0.125557   
4257            57.913017                33.835564                 -0.137066   
4258            57.919407                33.807407                 -0.096488   
4259            57.926838                33.808857                 -0.095707   
4260            57.920204                33.787971                 -0.085749   

      6m_before_area_full_rent_mean  ...  last_month_etc_supply_12m_before  \
0                          1.893891  ...                              -2.0   
1                          1.795654  ...                              -2.0   
2                          2.125400  ...                              -2.0   
3                          2.205867  ...                              -2.0   
4                          2.027898  ...                              -2.0   
...                             ...  ...                               ...   
4256                       2.290592  ...                            -150.0   
4257                       2.255442  ...                            -150.0   
4258                       2.308283  ...                            -150.0   
4259                       2.322204  ...                            -150.0   
4260                       2.320687  ...                            -150.0   

      last_month_total_supply_12m_before  \
0                                  -35.0   
1                                  -35.0   
2                                  -35.0   
3                                  -35.0   
4                                  -35.0   
...                                  ...   
4256                               535.0   
4257                               535.0   
4258                               535.0   
4259                               535.0   
4260                               535.0   

      last_month_total_unsold_count_12m_before  \
0                                     -15738.0   
1                                     -15738.0   
2                                     -15738.0   
3                                     -15738.0   
4                                     -15738.0   
...                                        ...   
4256                                   18202.0   
4257                                   18202.0   
4258                                   18202.0   
4259                                   18202.0   
4260                                   18202.0   

      last_month_total_deal_count_12m_before  \
0                                    -2078.0   
1                            

In [ ]:
df_original_dataset.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 4261 entries, 0 to 4260
Data columns (total 76 columns):
 #   Column                                        Non-Null Count  Dtype  
---  ------                                        --------------  -----  
 0   year                                          4261 non-null   int64  
 1   month                                         4261 non-null   int64  
 2   day                                           4261 non-null   int64  
 3   area_deal                                     4261 non-null   float32
 4   area_full_rent                                4261 non-null   float32
 5   area_year_rent                                4261 non-null   float32
 6   deal_full_rent_rate                           4261 non-null   float32
 7   deal_year_rent_multiple                       4261 non-null   float32
 8   6m_before_area_deal_mean                      4261 non-null   float32
 9   6m_before_area_full_rent_mean                 4261 non-null   f

> 해당 데이터셋에는 null 값이 없음을 확인

In [ ]:
# date 컬럼의 타입을 변경
df_original_dataset['date'] = pd.to_datetime(df_original_dataset['date'])
df_original_dataset.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 4261 entries, 0 to 4260
Data columns (total 76 columns):
 #   Column                                        Non-Null Count  Dtype         
---  ------                                        --------------  -----         
 0   year                                          4261 non-null   int64         
 1   month                                         4261 non-null   int64         
 2   day                                           4261 non-null   int64         
 3   area_deal                                     4261 non-null   float32       
 4   area_full_rent                                4261 non-null   float32       
 5   area_year_rent                                4261 non-null   float32       
 6   deal_full_rent_rate                           4261 non-null   float32       
 7   deal_year_rent_multiple                       4261 non-null   float32       
 8   6m_before_area_deal_mean                      4261 non-null   float3

In [ ]:
df_original_dataset.to_pickle('/content/drive/MyDrive/house_price/after_data/df_original_dataset_without_future.pkl')

## 1년후 아파트 지수 병합

In [ ]:
import pandas as pd
df_seoul_index = pd.read_pickle('/content/drive/MyDrive/house_price/after_data/df_seoul_index.pkl')
df_seoul_index

date  seoul_index
0   2008-04-07       59.733
1   2008-04-14       59.882
2   2008-04-21       60.042
3   2008-04-28       60.163
4   2008-05-05       60.278
..         ...          ...
778 2023-09-18       90.635
779 2023-09-25       90.681
780 2023-10-09       90.733
781 2023-10-16       90.787
782 2023-10-23       90.820

[783 rows x 2 columns]

In [ ]:
import datetime

# 크롤링한 날짜 기간에 있는 모든 날짜들을 계산
start = datetime.datetime.strptime("07-04-2008", "%d-%m-%Y") # 시작날짜 설정
end = datetime.datetime.strptime("31-10-2023", "%d-%m-%Y") # 끝날짜 설정정
date_generated = [start + datetime.timedelta(days=x) for x in range(0, (end-start).days)] # 시작날짜와 끝날짜 사이에 있는 날짜들 생성
date_list=list()
for date in date_generated:
    date_list.append(date.strftime("%Y-%m-%d")) # date_list 에서 생성한 날짜들의 형식을 맞춰서 대입
# df_date는 조회할 모든 날짜들의 정보가 들어있는 series
df_date = pd.DataFrame({
    "future_date": date_list
}, columns=["future_date"])
df_date['future_date'] = pd.to_datetime(df_date['future_date'], format='%Y-%m-%d %H:%M:%S', errors='raise') # date 타입으로 변경

df_date

future_date
0     2008-04-07
1     2008-04-08
2     2008-04-09
3     2008-04-10
4     2008-04-11
...          ...
5680  2023-10-26
5681  2023-10-27
5682  2023-10-28
5683  2023-10-29
5684  2023-10-30

[5685 rows x 1 columns]

In [ ]:
# 두개의 데이터프레임 결합을 통해서 날짜별 기준금리 현황을 생성
df_future =pd.merge(df_date, df_seoul_index, left_on='future_date', right_on='date', how='left')
print(df_future.info())
df_future

<class 'pandas.core.frame.DataFrame'>
Int64Index: 5685 entries, 0 to 5684
Data columns (total 3 columns):
 #   Column       Non-Null Count  Dtype         
---  ------       --------------  -----         
 0   future_date  5685 non-null   datetime64[ns]
 1   date         783 non-null    datetime64[ns]
 2   seoul_index  783 non-null    float64       
dtypes: datetime64[ns](2), float64(1)
memory usage: 177.7 KB
None


future_date       date  seoul_index
0     2008-04-07 2008-04-07       59.733
1     2008-04-08        NaT          NaN
2     2008-04-09        NaT          NaN
3     2008-04-10        NaT          NaN
4     2008-04-11        NaT          NaN
...          ...        ...          ...
5680  2023-10-26        NaT          NaN
5681  2023-10-27        NaT          NaN
5682  2023-10-28        NaT          NaN
5683  2023-10-29        NaT          NaN
5684  2023-10-30        NaT          NaN

[5685 rows x 3 columns]

In [ ]:
df_future.drop('date',axis=1,inplace=True)

df_future['seoul_index'] = df_future['seoul_index'].interpolate(method='values')
df_future['seoul_index'] = round(df_future['seoul_index'],2)
print(df_future.info())
df_future

<class 'pandas.core.frame.DataFrame'>
Int64Index: 5685 entries, 0 to 5684
Data columns (total 2 columns):
 #   Column       Non-Null Count  Dtype         
---  ------       --------------  -----         
 0   future_date  5685 non-null   datetime64[ns]
 1   seoul_index  5685 non-null   float64       
dtypes: datetime64[ns](1), float64(1)
memory usage: 133.2 KB
None


future_date  seoul_index
0     2008-04-07        59.73
1     2008-04-08        59.75
2     2008-04-09        59.78
3     2008-04-10        59.80
4     2008-04-11        59.82
...          ...          ...
5680  2023-10-26        90.82
5681  2023-10-27        90.82
5682  2023-10-28        90.82
5683  2023-10-29        90.82
5684  2023-10-30        90.82

[5685 rows x 2 columns]

In [ ]:
# 365일 전의 날짜를 구함
df_future['date'] = df_future['future_date'] - pd.Timedelta(days=365)

df_future = df_future.rename(columns={'seoul_index':'future_index'})

print(df_future.info())
df_future.head()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 5685 entries, 0 to 5684
Data columns (total 3 columns):
 #   Column        Non-Null Count  Dtype         
---  ------        --------------  -----         
 0   future_date   5685 non-null   datetime64[ns]
 1   future_index  5685 non-null   float64       
 2   date          5685 non-null   datetime64[ns]
dtypes: datetime64[ns](2), float64(1)
memory usage: 177.7 KB
None


future_date  future_index       date
0  2008-04-07         59.73 2007-04-08
1  2008-04-08         59.75 2007-04-09
2  2008-04-09         59.78 2007-04-10
3  2008-04-10         59.80 2007-04-11
4  2008-04-11         59.82 2007-04-12

In [ ]:
df_future.tail()

future_date  future_index       date
5680  2023-10-26         90.82 2022-10-26
5681  2023-10-27         90.82 2022-10-27
5682  2023-10-28         90.82 2022-10-28
5683  2023-10-29         90.82 2022-10-29
5684  2023-10-30         90.82 2022-10-30

In [ ]:
df_future['year'] = df_future['date'].dt.year
df_future['month'] = df_future['date'].dt.month
df_future['day'] = df_future['date'].dt.day
df_future.drop('date',axis=1,inplace=True)

df_future.head()

future_date  future_index  year  month  day
0  2008-04-07         59.73  2007      4    8
1  2008-04-08         59.75  2007      4    9
2  2008-04-09         59.78  2007      4   10
3  2008-04-10         59.80  2007      4   11
4  2008-04-11         59.82  2007      4   12

In [ ]:
# 데이터 프레임 병합
df_original_dataset = pd.merge(df_original_dataset,df_future, on = ['year','month','day'], how='left')
df_original_dataset

year  month  day    area_deal  area_full_rent  area_year_rent  \
0     2012      3    1   548.170105      309.035980       20.537769   
1     2012      3    2   547.971802      308.738037       20.522972   
2     2012      3    3   547.847473      309.738129       20.533909   
3     2012      3    4   548.025452      309.982178       20.534513   
4     2012      3    5   547.768799      309.442413       20.514805   
...    ...    ...  ...          ...             ...             ...   
4256  2023     10   26  1029.659058      596.442871       30.401781   
4257  2023     10   27  1029.540405      596.237915       30.427759   
4258  2023     10   28  1029.958740      596.546021       30.465477   
4259  2023     10   29  1029.966797      596.627197       30.464407   
4260  2023     10   30  1030.069458      596.618347       30.486279   

      deal_full_rent_rate  deal_year_rent_multiple  6m_before_area_deal_mean  \
0               56.375927                26.690830                 -4.654602   
1               56.341957                26.700411                 -4.689094   
2               56.537292                26.680136                 -4.710719   
3               56.563461                26.688017                 -4.679762   
4               56.491428                26.701145                 -4.724403   
...                   ...                      ...                       ...   
4256            57.926250                33.868378                 -0.125557   
4257            57.913017                33.835564                 -0.137066   
4258            57.919407                33.807407                 -0.096488   
4259            57.926838                33.808857                 -0.095707   
4260            57.920204                33.787971                 -0.085749   

      6m_before_area_full_rent_mean  ...  \
0                          1.893891  ...   
1                          1.795654  ...   
2                          2.125400  ...   
3                          2.205867  ...   
4                          2.027898  ...   
...                             ...  ...   
4256                       2.290592  ...   
4257                       2.255442  ...   
4258                       2.308283  ...   
4259                       2.322204  ...   
4260                       2.320687  ...   

      last_month_total_unsold_count_12m_before  \
0                                     -15738.0   
1                                     -15738.0   
2                                     -15738.0   
3                                     -15738.0   
4                                     -15738.0   
...                                        ...   
4256                                   18202.0   
4257                                   18202.0   
4258                                   18202.0   
4259                                   18202.0   
4260                                   18202.0   

      last_month_total_deal_count_12m_before  \
0                                    -2078.0   
1                                    -2078.0   
2                                    -2078.0   
3                                    -2078.0   
4                                    -2078.0   
...                                      ...   
4256                                  2799.0   
4257                                  2799.0   
4258                                  2799.0   
4259                                  2799.0   
4260                                  2799.0   

      last_month_total_full_rent_count_12m_before  \
0                                           794.0   
1                                           794.0   
2                                           794.0   
3                                           794.0   
4                                           794.0   
...                                           ...   
4256                                        915.0   
4257                                        915.0   
4258    

In [ ]:
df_original_dataset.isnull().sum()

year                                          0
month                                         0
day                                           0
area_deal                                     0
area_full_rent                                0
                                           ... 
us_10-2_year_12m_before                       0
us_10-3_year_month_12m_before                 0
last_month_total_unsold_ratio_12m_before      0
future_date                                 365
future_index                                365
Length: 78, dtype: int64

> 365일 뒤를 미뤘으니, 365개의 null 값이 생기는 것음 맞음

In [ ]:
df_original_dataset.loc[(df_original_dataset['year']>=2022)&(df_original_dataset['future_date'].isnull()),:]

year  month  day    area_deal  area_full_rent  area_year_rent  \
3896  2022     10   31  1072.249390      616.301147       30.388184   
3897  2022     11    1  1071.884399      615.858154       30.359941   
3898  2022     11    2  1071.720825      615.359009       30.345861   
3899  2022     11    3  1071.687134      615.154297       30.362978   
3900  2022     11    4  1071.556396      615.286621       30.390690   
...    ...    ...  ...          ...             ...             ...   
4256  2023     10   26  1029.659058      596.442871       30.401781   
4257  2023     10   27  1029.540405      596.237915       30.427759   
4258  2023     10   28  1029.958740      596.546021       30.465477   
4259  2023     10   29  1029.966797      596.627197       30.464407   
4260  2023     10   30  1030.069458      596.618347       30.486279   

      deal_full_rent_rate  deal_year_rent_multiple  6m_before_area_deal_mean  \
3896            57.477409                35.285076                 -0.975604   
3897            57.455654                35.305878                 -1.399316   
3898            57.417847                35.316868                 -1.414363   
3899            57.400547                35.295849                 -1.417462   
3900            57.419903                35.259365                 -1.429489   
...                   ...                      ...                       ...   
4256            57.926250                33.868378                 -0.125557   
4257            57.913017                33.835564                 -0.137066   
4258            57.919407                33.807407                 -0.096488   
4259            57.926838                33.808857                 -0.095707   
4260            57.920204                33.787971                 -0.085749   

      6m_before_area_full_rent_mean  ...  \
3896                       1.268276  ...   
3897                       0.338758  ...   
3898                       0.257434  ...   
3899                       0.224082  ...   
3900                       0.245641  ...   
...                             ...  ...   
4256                       2.290592  ...   
4257                       2.255442  ...   
4258                       2.308283  ...   
4259                       2.322204  ...   
4260                       2.320687  ...   

      last_month_total_unsold_count_12m_before  \
3896                                   27762.0   
3897                                   33142.0   
3898                                   33142.0   
3899                                   33142.0   
3900                                   33142.0   
...                                        ...   
4256                                   18202.0   
4257                                   18202.0   
4258                                   18202.0   
4259                                   18202.0   
4260                                   18202.0   

      last_month_total_deal_count_12m_before  \
3896                                 -2155.0   
3897                                 -1721.0   
3898                                 -1721.0   
3899                                 -1721.0   
3900                                 -1721.0   
...                                      ...   
4256                                  2799.0   
4257                                  2799.0   
4258                                  2799.0   
4259                                  2799.0   
4260                                  2799.0   

      last_month_total_full_rent_count_12m_before  \
3896                                        951.0   
3897                                      -1437.0   
3898                                      -1437.0   
3899                                      -1437.0   
3900                                      -1437.0   
...                                           ...   
4256                                        915.0   
4257                                        915.0   
4258    

## 파일 저장

In [ ]:
df_original_dataset.to_pickle('/content/drive/MyDrive/house_price/after_data/df_original_dataset.pkl')

# 기계학습

- 여러 회귀 모델들을 사용해서 서울 전체 집값의 추이를 예상하는 모델을 생성

## df_train_test 생성

- df_train_test는 df_original_dataset 에서 future_area_deal과 상관관계가 높은 feature들만을 선택한 데이터프레임

In [ ]:
import pandas as pd

df_original_dataset = pd.read_pickle('/content/drive/MyDrive/house_price/after_data/df_original_dataset.pkl')
print(df_original_dataset.info())
df_original_dataset

<class 'pandas.core.frame.DataFrame'>
Int64Index: 4261 entries, 0 to 4260
Data columns (total 78 columns):
 #   Column                                        Non-Null Count  Dtype         
---  ------                                        --------------  -----         
 0   year                                          4261 non-null   int64         
 1   month                                         4261 non-null   int64         
 2   day                                           4261 non-null   int64         
 3   area_deal                                     4261 non-null   float32       
 4   area_full_rent                                4261 non-null   float32       
 5   area_year_rent                                4261 non-null   float32       
 6   deal_full_rent_rate                           4261 non-null   float32       
 7   deal_year_rent_multiple                       4261 non-null   float32       
 8   6m_before_area_deal_mean                      4261 non-null   float3

year  month  day    area_deal  area_full_rent  area_year_rent  \
0     2012      3    1   548.170105      309.035980       20.537769   
1     2012      3    2   547.971802      308.738037       20.522972   
2     2012      3    3   547.847473      309.738129       20.533909   
3     2012      3    4   548.025452      309.982178       20.534513   
4     2012      3    5   547.768799      309.442413       20.514805   
...    ...    ...  ...          ...             ...             ...   
4256  2023     10   26  1029.659058      596.442871       30.401781   
4257  2023     10   27  1029.540405      596.237915       30.427759   
4258  2023     10   28  1029.958740      596.546021       30.465477   
4259  2023     10   29  1029.966797      596.627197       30.464407   
4260  2023     10   30  1030.069458      596.618347       30.486279   

      deal_full_rent_rate  deal_year_rent_multiple  6m_before_area_deal_mean  \
0               56.375927                26.690830                 -4.654602   
1               56.341957                26.700411                 -4.689094   
2               56.537292                26.680136                 -4.710719   
3               56.563461                26.688017                 -4.679762   
4               56.491428                26.701145                 -4.724403   
...                   ...                      ...                       ...   
4256            57.926250                33.868378                 -0.125557   
4257            57.913017                33.835564                 -0.137066   
4258            57.919407                33.807407                 -0.096488   
4259            57.926838                33.808857                 -0.095707   
4260            57.920204                33.787971                 -0.085749   

      6m_before_area_full_rent_mean  ...  \
0                          1.893891  ...   
1                          1.795654  ...   
2                          2.125400  ...   
3                          2.205867  ...   
4                          2.027898  ...   
...                             ...  ...   
4256                       2.290592  ...   
4257                       2.255442  ...   
4258                       2.308283  ...   
4259                       2.322204  ...   
4260                       2.320687  ...   

      last_month_total_unsold_count_12m_before  \
0                                     -15738.0   
1                                     -15738.0   
2                                     -15738.0   
3                                     -15738.0   
4                                     -15738.0   
...                                        ...   
4256                                   18202.0   
4257                                   18202.0   
4258                                   18202.0   
4259                                   18202.0   
4260                                   18202.0   

      last_month_total_deal_count_12m_before  \
0                                    -2078.0   
1                                    -2078.0   
2                                    -2078.0   
3                                    -2078.0   
4                                    -2078.0   
...                                      ...   
4256                                  2799.0   
4257                                  2799.0   
4258                                  2799.0   
4259                                  2799.0   
4260                                  2799.0   

      last_month_total_full_rent_count_12m_before  \
0                                           794.0   
1                                           794.0   
2                                           794.0   
3                                           794.0   
4                                           794.0   
...                                           ...   
4256                                        915.0   
4257                                        915.0   
4258    

In [ ]:
pd.set_option('display.max_rows', 80)

df_original_dataset.corr()['future_index'].sort_values(ascending=False).to_frame()

<ipython-input-36-b2cfebcb3a0a>:3: FutureWarning:

The default value of numeric_only in DataFrame.corr is deprecated. In a future version, it will default to False. Select only valid columns or specify the value of numeric_only to silence this warning.



future_index
future_index                                      1.000000
deal_year_rent_multiple                           0.967644
area_deal                                         0.959716
area_full_rent                                    0.950341
year                                              0.945281
area_year_rent                                    0.896595
12m_before_area_deal_mean                         0.785215
kospi_index                                       0.774767
last_month_total_month_rent_count                 0.732730
6m_before_area_deal_mean                          0.681655
12m_before_area_year_rent_mean                    0.628017
6m_before_area_year_rent_mean                     0.599924
12m_before_deal_year_rent_multiple                0.590898
korea_10_year_12m_before                          0.454511
6m_before_deal_year_rent_multiple                 0.447874
last_month_total_full_rent_count                  0.439092
korea_3_year_6m_before                            0.432152
korea_3_year_12m_before                           0.421403
last_month_total_month_rent_count_12m_before      0.400111
korea_10_year_6m_before                           0.399390
korea_rp_6m_before                                0.318836
us_10-3_year_month_12m_before                     0.305103
12m_before_area_full_rent_mean                    0.269498
us_3_month                                        0.265410
kospi_index_12m_before                            0.251996
korea_rp_12m_before                               0.247452
us_2_year                                         0.223502
6m_before_area_full_rent_mean                     0.206393
us_10-2_year_12m_before                           0.188767
last_month_total_month_rent_count_6m_before       0.187722
last_month_combination_supply                     0.147233
last_month_total_full_rent_count_12m_before       0.134723
us_10-3_year_month_6m_before                      0.134659
kospi_index_6m_before                             0.123874
us_10_year_6m_before                              0.100195
last_month_total_supply                           0.097050
korea_10-3_year                                   0.076707
korea_10-3_year_12m_before                        0.073525
last_month_general_supply_6m_before               0.066595
us_10_year_12m_before                             0.066483
last_month_combination_supply_12m_before          0.065236
last_month_general_supply                         0.064577
us_2_year_6m_before                               0.060883
last_month_total_supply_6m_before                 0.052386
last_month_general_supply_12m_before              0.045639
last_month_combination_supply_6m_before           0.045427
us_10-2_year_6m_before                            0.044618
last_month_total_supply_12m_before                0.043624
last_month_total_full_rent_count_6m_before        0.032867
month                                             0.020036
last_month_total_unsold_ratio_12m_before          0.015927
last_month_etc_supply                             0.012962
day                                               0.004487
us_3_month_6m_before                             -0.016722
last_month_total_unsold_ratio_6m_before          -0.028502
last_month_etc_supply_6m_before                  -0.031994
last_month_total_unsold_ratio                    -0.034966
korea_10-3_year_6m_before                        -0.045183
last_month_etc_supply_12m_before                 -0.052998
us_2_year_12m_before                             -0.061270
last_month_total_unsold_count_6m_before          -0.142401
last_month_total_deal_count_6m_before            -0.166491
us_3_month_12m_before                            -0.176467
last_month_total_unsold_count_12m_before         -0.233024
last_month_total_deal_count                      -0.256400
last_month_total_deal_count_12m_before           -0.276152
us_10_year                                       -0.352591
korea_10_year                     

In [ ]:
# 상관관계들만을 컬럼으로 한 데이터 프레임 생성
df_corr = df_original_dataset.corr(numeric_only=False)['future_index']
df_corr.head()

year              0.945281
month             0.020036
day               0.004487
area_deal         0.959716
area_full_rent    0.950341
Name: future_index, dtype: float64

In [ ]:
df_corr.info()

<class 'pandas.core.series.Series'>
Index: 78 entries, year to future_index
Series name: future_index
Non-Null Count  Dtype  
--------------  -----  
78 non-null     float64
dtypes: float64(1)
memory usage: 3.3+ KB


In [ ]:
# 컬럼명(series의)을 수정
df_corr.name = 'correlation'
df_corr.info()

<class 'pandas.core.series.Series'>
Index: 78 entries, year to future_index
Series name: correlation
Non-Null Count  Dtype  
--------------  -----  
78 non-null     float64
dtypes: float64(1)
memory usage: 3.3+ KB


In [ ]:
# 상관계쑤가 0.7 이상이거나, -0.7 이하인것 (양의 상관관계나 음의 상관관계가 있는 컬럼들만을 고름)
learning_feature_list = list(df_corr[(df_corr >= 0.7) | (df_corr <= -0.7)].index)
learning_feature_list

['year',
 'area_deal',
 'area_full_rent',
 'area_year_rent',
 'deal_year_rent_multiple',
 '12m_before_area_deal_mean',
 '12m_before_deal_full_rent_rate',
 'date',
 'kospi_index',
 'korea_rp',
 'last_month_total_month_rent_count',
 'future_date',
 'future_index']

> 거시경제 지표와, 아파트 가치평가 지표들이 미래 가격과 상관관계가 있음 -> 수치로 표현되는 지표들이 어느정도 미래 가격을 예측하는데 상관관계가 있음을 확인

> year, date, future_date, future_index 컬럼들은 future_index와 상관관계가 높지만, 부동산 지수가 그동안 우상향이어서 선택된 컬럼들로, 큰 의미는 없다. 하지만 추후 시각화로 그래프를 출력하는데 해당 컬럼들이 필요함으로 굳이 제거하지 않고 진행

In [ ]:
# 사용할 컬러명들만 선택해서 학습&테스트 데이터셋을 확보
df_train_test = df_original_dataset[learning_feature_list]
df_train_test

year    area_deal  area_full_rent  area_year_rent  \
0     2012   548.170105      309.035980       20.537769   
1     2012   547.971802      308.738037       20.522972   
2     2012   547.847473      309.738129       20.533909   
3     2012   548.025452      309.982178       20.534513   
4     2012   547.768799      309.442413       20.514805   
...    ...          ...             ...             ...   
4256  2023  1029.659058      596.442871       30.401781   
4257  2023  1029.540405      596.237915       30.427759   
4258  2023  1029.958740      596.546021       30.465477   
4259  2023  1029.966797      596.627197       30.464407   
4260  2023  1030.069458      596.618347       30.486279   

      deal_year_rent_multiple  12m_before_area_deal_mean  \
0                   26.690830                 -13.919560   
1                   26.700411                 -13.950701   
2                   26.680136                 -13.970224   
3                   26.688017                 -13.942276   
4                   26.701145                 -13.982579   
...                       ...                        ...   
4256                33.868378                  -4.642175   
4257                33.835564                  -4.653163   
4258                33.807407                  -4.614421   
4259                33.808857                  -4.613675   
4260                33.787971                  -4.604167   

      12m_before_deal_full_rent_rate       date  kospi_index  korea_rp  \
0                          20.082911 2012-03-01      2030.25      3.25   
1                          20.010553 2012-03-02      2034.63      3.25   
2                          20.426624 2012-03-03      2034.63      3.25   
3                          20.482367 2012-03-04      2034.63      3.25   
4                          20.328934 2012-03-05      2016.06      3.25   
...                              ...        ...          ...       ...   
4256                        0.923108 2023-10-26      2299.08      3.50   
4257                        0.900052 2023-10-27      2302.81      3.50   
4258                        0.911185 2023-10-28      2302.81      3.50   
4259                        0.924131 2023-10-29      2302.81      3.50   
4260                        0.912574 2023-10-30      2310.55      3.50   

      last_month_total_month_rent_count future_date  future_index  
0                                2638.0  2013-03-01         56.00  
1                                2638.0  2013-03-02         56.00  
2                                2638.0  2013-03-03         55.99  
3                                2638.0  2013-03-04         55.99  
4                                2638.0  2013-03-05         55.98  
...                                 ...         ...           ...  
4256                             7342.0         NaT           NaN  
4257                             7342.0         NaT           NaN  
4258                             7342.0         NaT           NaN  
4259                             7342.0         NaT           NaN  
4260                             7342.0         NaT           NaN  

[4261 rows x 13 columns]

In [ ]:
df_train_test.to_pickle('/content/drive/MyDrive/house_price/after_data/df_train_test.pkl')

## df_train, df_test 생성

- '2023년 서울 아파트 매매지수'를 테스트 데이터로 선언 (과거를 학습한 데이터가 얼마나 최근 데이터에도 성능을 내는지 확인하기 위해서)

In [3]:
import pandas as pd

df_train_test = pd.read_pickle('/content/drive/MyDrive/house_price/after_data/df_train_test.pkl')
df_train_test.head()

year   area_deal  area_full_rent  area_year_rent  deal_year_rent_multiple  \
0  2012  548.170105      309.035980       20.537769                26.690830   
1  2012  547.971802      308.738037       20.522972                26.700411   
2  2012  547.847473      309.738129       20.533909                26.680136   
3  2012  548.025452      309.982178       20.534513                26.688017   
4  2012  547.768799      309.442413       20.514805                26.701145   

   12m_before_area_deal_mean  12m_before_deal_full_rent_rate       date  \
0                 -13.919560                       20.082911 2012-03-01   
1                 -13.950701                       20.010553 2012-03-02   
2                 -13.970224                       20.426624 2012-03-03   
3                 -13.942276                       20.482367 2012-03-04   
4                 -13.982579                       20.328934 2012-03-05   

   kospi_index  korea_rp  last_month_total_month_rent_count future_date  \
0      2030.25      3.25                             2638.0  2013-03-01   
1      2034.63      3.25                             2638.0  2013-03-02   
2      2034.63      3.25                             2638.0  2013-03-03   
3      2034.63      3.25                             2638.0  2013-03-04   
4      2016.06      3.25                             2638.0  2013-03-05   

   future_index  
0         56.00  
1         56.00  
2         55.99  
3         55.99  
4         55.98

In [4]:
df_train_test.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 4261 entries, 0 to 4260
Data columns (total 13 columns):
 #   Column                             Non-Null Count  Dtype         
---  ------                             --------------  -----         
 0   year                               4261 non-null   int64         
 1   area_deal                          4261 non-null   float32       
 2   area_full_rent                     4261 non-null   float32       
 3   area_year_rent                     4261 non-null   float32       
 4   deal_year_rent_multiple            4261 non-null   float32       
 5   12m_before_area_deal_mean          4261 non-null   float32       
 6   12m_before_deal_full_rent_rate     4261 non-null   float32       
 7   date                               4261 non-null   datetime64[ns]
 8   kospi_index                        4261 non-null   float64       
 9   korea_rp                           4261 non-null   float64       
 10  last_month_total_month_rent_count  4

In [5]:
# 학습할 때 입력을 할 feature들을 설정
train_columns = list(df_train_test.columns)

to_remove = ['future_index','date','year','future_date']
for x in to_remove:
    train_columns.remove(x)
train_columns


['area_deal',
 'area_full_rent',
 'area_year_rent',
 'deal_year_rent_multiple',
 '12m_before_area_deal_mean',
 '12m_before_deal_full_rent_rate',
 'kospi_index',
 'korea_rp',
 'last_month_total_month_rent_count']

In [6]:
# df_train_test에는 future_index가 null 값인 데이터들도 있음으로 필터링해서 학습용데이터셋은 df_train, 테스트용 데이터셋은 df_test 에 저장
df_train = df_train_test.loc[df_train_test['year']<2022, :].copy()
df_test = df_train_test.loc[(df_train_test['year']>=2022)&(df_train_test['future_index'].notnull()), :].copy()

In [7]:
df_train

year    area_deal  area_full_rent  area_year_rent  \
0     2012   548.170105      309.035980       20.537769   
1     2012   547.971802      308.738037       20.522972   
2     2012   547.847473      309.738129       20.533909   
3     2012   548.025452      309.982178       20.534513   
4     2012   547.768799      309.442413       20.514805   
...    ...          ...             ...             ...   
3588  2021  1083.472168      607.116211       28.811615   
3589  2021  1083.753906      606.659790       28.847986   
3590  2021  1083.566772      606.564270       28.837791   
3591  2021  1083.580566      606.848999       28.828548   
3592  2021  1083.398315      607.298218       28.820314   

      deal_year_rent_multiple  12m_before_area_deal_mean  \
0                   26.690830                 -13.919560   
1                   26.700411                 -13.950701   
2                   26.680136                 -13.970224   
3                   26.688017                 -13.942276   
4                   26.701145                 -13.982579   
...                       ...                        ...   
3588                37.605396                  15.883393   
3589                37.567749                  15.913527   
3590                37.574539                  15.893512   
3591                37.587067                  15.894987   
3592                37.591480                  15.875494   

      12m_before_deal_full_rent_rate       date  kospi_index  korea_rp  \
0                          20.082911 2012-03-01      2030.25      3.25   
1                          20.010553 2012-03-02      2034.63      3.25   
2                          20.426624 2012-03-03      2034.63      3.25   
3                          20.482367 2012-03-04      2034.63      3.25   
4                          20.328934 2012-03-05      2016.06      3.25   
...                              ...        ...          ...       ...   
3588                       -5.929564 2021-12-27      2999.55      1.00   
3589                       -6.024723 2021-12-28      3020.24      1.00   
3590                       -6.023295 2021-12-29      2993.29      1.00   
3591                       -5.980375 2021-12-30      2977.65      1.00   
3592                       -5.894950 2021-12-31      2977.65      1.00   

      last_month_total_month_rent_count future_date  future_index  
0                                2638.0  2013-03-01         56.00  
1                                2638.0  2013-03-02         56.00  
2                                2638.0  2013-03-03         55.99  
3                                2638.0  2013-03-04         55.99  
4                                2638.0  2013-03-05         55.98  
...                                 ...         ...           ...  
3588                             6661.0  2022-12-27         95.94  
3589                             6661.0  2022-12-28         95.89  
3590                             6661.0  2022-12-29         95.85  
3591                             6661.0  2022-12-30         95.80  
3592                             6661.0  2022-12-31         95.76  

[3593 rows x 13 columns]

In [8]:
df_test

year    area_deal  area_full_rent  area_year_rent  \
3593  2022  1083.536621      606.893738       28.841393   
3594  2022  1083.647461      606.853333       28.839933   
3595  2022  1083.479614      607.364014       28.851576   
3596  2022  1083.489624      606.642090       28.877390   
3597  2022  1083.651611      607.107971       28.828796   
...    ...          ...             ...             ...   
3891  2022  1073.413330      616.464355       30.461447   
3892  2022  1073.308960      616.624390       30.406357   
3893  2022  1073.112549      616.791504       30.423437   
3894  2022  1072.432983      617.013306       30.416872   
3895  2022  1072.386108      617.006836       30.423203   

      deal_year_rent_multiple  12m_before_area_deal_mean  \
3593                37.568806                  13.972645   
3594                37.574547                  13.984303   
3595                37.553570                  13.966648   
3596                37.520344                  13.967700   
3597                37.589207                  13.984739   
...                       ...                        ...   
3891                35.238422                   0.732220   
3892                35.298836                   0.722425   
3893                35.272560                   0.703994   
3894                35.257832                   0.640221   
3895                35.248955                   0.635822   

      12m_before_deal_full_rent_rate       date  kospi_index  korea_rp  \
3593                       -5.584571 2022-01-01      2977.65       1.0   
3594                       -5.600518 2022-01-02      2977.65       1.0   
3595                       -5.506430 2022-01-03      2988.77       1.0   
3596                       -5.619623 2022-01-04      2989.24       1.0   
3597                       -5.561261 2022-01-05      2953.97       1.0   
...                              ...        ...          ...       ...   
3891                        1.600907 2022-10-26      2249.56       3.0   
3892                        1.637168 2022-10-27      2288.78       3.0   
3893                        1.683322 2022-10-28      2268.40       3.0   
3894                        1.784342 2022-10-29      2268.40       3.0   
3895                        1.787730 2022-10-30      2268.40       3.0   

      last_month_total_month_rent_count future_date  future_index  
3593                            10052.0  2023-01-01         95.71  
3594                            10052.0  2023-01-02         95.67  
3595                            10052.0  2023-01-03         95.62  
3596                            10052.0  2023-01-04         95.56  
3597                            10052.0  2023-01-05         95.51  
...                                 ...         ...           ...  
3891                             7793.0  2023-10-26         90.82  
3892                             7793.0  2023-10-27         90.82  
3893                             7793.0  2023-10-28         90.82  
3894                             7793.0  2023-10-29         90.82  
3895                             7793.0  2023-10-30         90.82  

[303 rows x 13 columns]

## 모델 적용

In [18]:
display(df_test['future_index'].describe())

count    303.000000
mean      91.590693
std        1.501675
min       90.310000
25%       90.520000
50%       90.800000
75%       92.390000
max       95.710000
Name: future_index, dtype: float64

> 테스트로 예측할 future_index의 값은 90.31~95.71 사이에 값들이 존재함

> 모델의 성능은 mse 로 측정했을 때, 1 이하인 모델을 생성하는 것을 목표로 함(mse가 1이하 일때 실제로 mse가 더 작음에도는 rmse는 더 크게 되는 문제 발생 -> 성능 측정에 혼선이 없게 mse로 성능을 확인 )

### 선형회귀 모델

In [ ]:
# Importing required libraries
import pandas as pd
from sklearn.linear_model import LinearRegression
from sklearn.model_selection import train_test_split
from sklearn.metrics import mean_squared_error
import numpy as np
import plotly.graph_objs as go
from sklearn.metrics import r2_score

# Creating a Linear Regression model
model = LinearRegression()

X_train = df_train[train_columns]
y_train = df_train['future_index']

X_test = df_test[train_columns]
y_test = df_test['future_index']

# Training the model on the training set
model.fit(X_train, y_train)


# Making predictions on the testing set
y_pred = model.predict(X_test)


# Evaluating the model using Mean Squared Error (MSE)
mse = mean_squared_error(y_test , y_pred)
print('LinearRegression Mean Squared Error:', mse)
print('LinearRegression Root Mean Squared Error:', np.sqrt(mse))
print()

# Creating the traces
trace1 = go.Scatter(
    x = df_test['future_date'],
    y = y_test.values,
    mode = 'lines',
    name = 'actual_value'
)


trace2 = go.Scatter(
    x = df_test['future_date'],
    y = list(y_pred),
    mode = 'lines',
    name = 'predict_value'
)

# Combining the traces and creating the layout
data = [trace1, trace2]
layout = go.Layout(title='Linear Regression Predict future price for test dataset', xaxis=dict(title='index'), yaxis=dict(title='서울아파트지수'))

# Creating the figure and plotting it
fig = go.Figure(data=data, layout=layout)
fig.show()


LinearRegression Mean Squared Error: 21.649886770747557
LinearRegression Root Mean Squared Error: 4.65294388218336



> 오차 값이 존재하나, 추세가 비슷하게 움직임

> 하지만 2023년 8월 이후로 예측한 부분이 크게 실제값과 벗어남을 확인

### 다항회귀 모델

#### 2차항

In [8]:
# Importing required libraries
import pandas as pd
from sklearn.preprocessing import PolynomialFeatures
from sklearn.linear_model import LinearRegression
from sklearn.model_selection import train_test_split
from sklearn.metrics import mean_squared_error
import numpy as np
import plotly.graph_objs as go


X_train = df_train[train_columns]
y_train = df_train['future_index']

X_test = df_test[train_columns]
y_test = df_test['future_index']

# Creating polynomial features
poly = PolynomialFeatures(degree=2)
X_train_poly = poly.fit_transform(X_train)
X_test_poly = poly.transform(X_test)

# Creating a Polynomial Regression model
model = LinearRegression()

# Training the model on the training set
model.fit(X_train_poly, y_train)

# Making predictions on the testing set
y_pred = model.predict(X_test_poly)

# Evaluating the model using Mean Squared Error (MSE)
mse = mean_squared_error(y_test, y_pred)
print('2 PolynomialFeatures Mean Squared Error:', mse)
print('2 PolynomialFeatures Root Mean Squared Error:', np.sqrt(mse))
print()

# Creating the traces
trace1 = go.Scatter(
    x = df_test['future_date'],
    y = y_test.values,
    mode = 'lines',
    name = 'actual_value'
)


trace2 = go.Scatter(
    x = df_test['future_date'],
    y = list(y_pred),
    mode = 'lines',
    name = 'predict_value'
)

# Combining the traces and creating the layout
data = [trace1, trace2]
layout = go.Layout(title='Linear Regression Poly2 Predict future price for test dataset', xaxis=dict(title='index'), yaxis=dict(title='서울아파트지수'))

# Creating the figure and plotting it
fig = go.Figure(data=data, layout=layout)
fig.show()



2 PolynomialFeatures Mean Squared Error: 477.93997993894186
2 PolynomialFeatures Root Mean Squared Error: 21.861838439137316



> 2차항 다항회귀 모델을 적용해보았으니, 선형회귀보다 더 성능이 안좋게 나옴

#### 3차항

In [10]:
# Importing required libraries
import pandas as pd
from sklearn.preprocessing import PolynomialFeatures
from sklearn.linear_model import LinearRegression
from sklearn.model_selection import train_test_split
from sklearn.metrics import mean_squared_error
import numpy as np
import plotly.graph_objs as go


X_train = df_train[train_columns]
y_train = df_train['future_index']

X_test = df_test[train_columns]
y_test = df_test['future_index']

# Creating polynomial features
poly = PolynomialFeatures(degree=3)
X_train_poly = poly.fit_transform(X_train)
X_test_poly = poly.transform(X_test)

# Creating a Polynomial Regression model
model = LinearRegression()

# Training the model on the training set
model.fit(X_train_poly, y_train)

# Making predictions on the testing set
y_pred = model.predict(X_test_poly)

# Evaluating the model using Mean Squared Error (MSE)
mse = mean_squared_error(y_test, y_pred)
print('3 PolynomialFeatures Mean Squared Error:', mse)
print('3 PolynomialFeatures Root Mean Squared Error:', np.sqrt(mse))
print()

# Creating the traces
trace1 = go.Scatter(
    x = df_test['future_date'],
    y = y_test.values,
    mode = 'lines',
    name = 'actual_value'
)


trace2 = go.Scatter(
    x = df_test['future_date'],
    y = list(y_pred),
    mode = 'lines',
    name = 'predict_value'
)

# Combining the traces and creating the layout
data = [trace1, trace2]
layout = go.Layout(title='Linear Regression Poly3 Predict future price for test dataset', xaxis=dict(title='index'), yaxis=dict(title='서울아파트지수'))

# Creating the figure and plotting it
fig = go.Figure(data=data, layout=layout)
fig.show()



3 PolynomialFeatures Mean Squared Error: 37099.686023837174
3 PolynomialFeatures Root Mean Squared Error: 192.61278779934932



> 3차항 다항회귀를 사용했으나, 너무 성능이 않좋게 나옴

### Gradient Boosting 모델

In [ ]:
# Importing required libraries
import pandas as pd
from sklearn.ensemble import GradientBoostingRegressor
from sklearn.model_selection import train_test_split
from sklearn.metrics import mean_squared_error
import numpy as np
import plotly.graph_objs as go
from tqdm import tqdm

X_train = df_train[train_columns]
y_train = df_train['future_index']

X_test = df_test[train_columns]
y_test = df_test['future_index']

best_mse_score = np.inf
best_estimator = 0
best_learning = 0
best_depth = 0

estimator_list = np.arange(80, 301, 10)
learning_list = [0.001,0.005,0.01,0.05,0.1]

# Assuming estimator_list and learning_list are defined somewhere in your code
for estimator in tqdm(estimator_list):
  for learning in learning_list:
    for depth in range(1, 6):

      # Creating a Gradient Boosting model
      model = GradientBoostingRegressor(n_estimators= estimator, learning_rate= learning, max_depth = depth, random_state=0)

      # Training the model on the training set
      model.fit(X_train, y_train)

      # Making predictions on the testing set
      y_pred = model.predict(X_test)

      # Evaluating the model using Mean Squared Error (MSE)
      mse = mean_squared_error(y_test , y_pred)

      if mse < best_mse_score:

        best_mse_score = mse
        best_estimator = estimator
        best_learning = learning
        best_depth =  depth


print()
print('GradientBoostingRegressor Mean Squared Error:', best_mse_score)
print('GradientBoostingRegressor Root Mean Squared Error:', np.sqrt(best_mse_score))
print()
print('n_estimators :', best_estimator,'learning_rate :',best_learning,'max_depth',  best_depth)
model = GradientBoostingRegressor(n_estimators= best_estimator, learning_rate=  best_learning, max_depth = best_depth, random_state=0)

model.fit(X_train, y_train)

y_pred = model.predict(X_test)


# Creating the traces
trace1 = go.Scatter(
    x = df_test['future_date'],
    y = y_test.values,
    mode = 'lines',
    name = 'actual_value'
)


trace2 = go.Scatter(
    x = df_test['future_date'],
    y = list(y_pred),
    mode = 'lines',
    name = 'predict_value'
)

# Combining the traces and creating the layout
data = [trace1, trace2]
layout = go.Layout(title='Gradient Boosting Predict future price for test dataset', xaxis=dict(title='index'), yaxis=dict(title='서울아파트지수'))

# Creating the figure and plotting it
fig = go.Figure(data=data, layout=layout)
fig.show()


100%|██████████| 23/23 [20:43<00:00, 54.07s/it]



GradientBoostingRegressor Mean Squared Error: 1.1167184205462022
GradientBoostingRegressor Root Mean Squared Error: 1.0567489865366335

n_estimators : 230 learning_rate : 0.01 max_depth 5


> for 문을 이용해 파라미터들을 변경시켜가면서 최고의 성능을 보이는 파라미터들을 찾음

> n_estimators : 230 learning_rate : 0.01 max_depth 5 일때, Mean Squared Error: 1.11 로 목표로 하는 성능과 상당히 유사한 성능을 보임

### XGBoost 모델

In [ ]:
# Importing required libraries
import pandas as pd
import xgboost as xgb
from sklearn.model_selection import train_test_split
from sklearn.metrics import mean_squared_error
import numpy as np
import plotly.graph_objs as go

X_train = df_train[train_columns]
y_train = df_train['future_index']

X_test = df_test[train_columns]
y_test = df_test['future_index']


best_mse_score = np.inf
best_estimator = 0
best_learning = 0
best_depth = 0

estimator_list = np.arange(80, 201, 10)
learning_list = [0.001,0.005,0.01,0.05,0.1]

# Assuming estimator_list and learning_list are defined somewhere in your code
for estimator in tqdm(estimator_list):
  for learning in learning_list:
    for depth in range(1, 6):


      # Creating an XGBoost model
      model = xgb.XGBRegressor(objective ='reg:squarederror', n_estimators=estimator, learning_rate= learning, max_depth=depth, random_state=0)

      # Training the model on the training set
      model.fit(X_train, y_train)


      # Making predictions on the testing set
      y_pred = model.predict(X_test)


      # Evaluating the model using Mean Squared Error (MSE)
      mse = mean_squared_error(y_test , y_pred)

      if mse < best_mse_score:

        best_mse_score = mse
        best_estimator = estimator
        best_learning = learning
        best_depth =  depth
print()
print('XGBRegressor Mean Squared Error:', best_mse_score)
print('XGBRegressor Root Mean Squared Error:', np.sqrt(best_mse_score))

print()
print('n_estimators :', best_estimator,'learning_rate :',best_learning,'max_depth',  best_depth)
model = xgb.XGBRegressor(objective ='reg:squarederror', n_estimators= best_estimator, learning_rate=  best_learning, max_depth = best_depth, random_state=0)

model.fit(X_train, y_train)

y_pred = model.predict(X_test)


# Creating the traces
trace1 = go.Scatter(
    x = df_test['future_date'],
    y = y_test.values,
    mode = 'lines',
    name = 'actual_value'
)


trace2 = go.Scatter(
    x = df_test['future_date'],
    y = list(y_pred),
    mode = 'lines',
    name = 'predict_value'
)

# Combining the traces and creating the layout
data = [trace1, trace2]
layout = go.Layout(title='XGBoost Predict future price for test dataset', xaxis=dict(title='index'), yaxis=dict(title='서울아파트지수'))

# Creating the figure and plotting it
fig = go.Figure(data=data, layout=layout)
fig.show()


100%|██████████| 13/13 [01:07<00:00,  5.16s/it]


XGBRegressor Mean Squared Error: 1.2220096120066088
XGBRegressor Root Mean Squared Error: 1.1054454360150974

n_estimators : 120 learning_rate : 0.1 max_depth 4


> for 문을 이용해 파라미터들을 변경시켜가면서 최고의 성능을 보이는 파라미터들을 찾음

> n_estimators : 120 learning_rate : 0.1 max_depth 4 일 때, Mean Squared Error: 1.22 로 최고의 성능을 보임

> Gradient Bossting 모델에 비해서 성능은 다소 떨어지만 크게 차이가 나지 않고(mse 기준 0.11 차이) 학습 속도가 훨씬 빠름

### RandomForest Regressor 모델



In [ ]:
# Importing required libraries
import pandas as pd
from sklearn.ensemble import RandomForestRegressor
from sklearn.model_selection import train_test_split
from sklearn.metrics import mean_squared_error
import numpy as np
import plotly.graph_objs as go

X_train = df_train[train_columns]
y_train = df_train['future_index']

X_test = df_test[train_columns]
y_test = df_test['future_index']

best_mse_score = np.inf
best_estimator = 0
estimator_list = np.arange(80, 201, 10)

for estimator in tqdm(estimator_list):
  # Creating a Random Forest Regressor model
  model = RandomForestRegressor(n_estimators= estimator, random_state=0)

  # Training the model on the training set
  model.fit(X_train, y_train)

  # Making predictions on the testing set
  y_pred = model.predict(X_test)

  # Evaluating the model using Mean Squared Error (MSE)
  mse = mean_squared_error(y_test , y_pred)

  if mse < best_mse_score:
      best_mse_score = mse
      best_estimator = estimator

print()
print('RandomForestRegressor Mean Squared Error:', best_mse_score)
print('RandomForestRegressor Root Mean Squared Error:', np.sqrt(best_mse_score))
print()

print('n_estimators :', best_estimator)

model = RandomForestRegressor(n_estimators= estimator, random_state=0)

model.fit(X_train, y_train)

y_pred = model.predict(X_test)



# Creating the traces
trace1 = go.Scatter(
    x = df_test['future_date'],
    y = y_test.values,
    mode = 'lines',
    name = 'actual_value'
)


trace2 = go.Scatter(
    x = df_test['future_date'],
    y = list(y_pred),
    mode = 'lines',
    name = 'predict_value'
)


# Combining the traces and creating the layout
data = [trace1, trace2]
layout = go.Layout(title='RandomForest Regressor Predict future price for test dataset', xaxis=dict(title='Date'), yaxis=dict(title='서울아파트지수'))

# Creating the figure and plotting it
fig = go.Figure(data=data, layout=layout)
fig.show()


100%|██████████| 13/13 [00:53<00:00,  4.08s/it]



RandomForestRegressor Mean Squared Error: 30.085491006472935
RandomForestRegressor Root Mean Squared Error: 5.48502424848541

n_estimators : 190


> for 문을 이용해 파라미터들을 변경시켜가면서 최고의 성능을 보이는 파라미터들을 찾음

> n_estimators : 190 일 때, Mean Squared Error: 30.08 로 최적의 성능을 보임

> Gradient Boosting, XGBoost, LinearRegressor 보다도 성능이 안좋게 나옴

## 데이터 범위 수정

In [ ]:
df_train_test.describe()

year    area_deal  area_full_rent  area_year_rent  \
count  4261.000000  4261.000000     4261.000000     4261.000000   
mean   2017.496362   732.685425      459.802490       24.162024   
std       3.375665   210.211655       99.731697        3.097236   
min    2012.000000   508.184509      304.899719       20.161331   
25%    2015.000000   536.843872      368.355988       21.448662   
50%    2017.000000   657.146118      460.357452       23.608965   
75%    2020.000000   942.029785      560.719177       26.345444   
max    2023.000000  1090.708984      622.134399       30.486279   

       deal_year_rent_multiple  12m_before_area_deal_mean  \
count              4261.000000                4261.000000   
mean                 29.780930                   5.907815   
std                   4.954143                   8.543085   
min                  24.165903                 -14.941670   
25%                  24.884462                  -0.036408   
50%                  27.786295                   6.869967   
75%                  34.550373                  12.578342   
max                  38.265236                  21.542885   

       12m_before_deal_full_rent_rate  kospi_index     korea_rp  \
count                     4261.000000  4261.000000  4261.000000   
mean                         1.053344  2247.941908     1.810490   
std                          6.849267   354.375349     0.864054   
min                        -11.132855  1457.640000     0.500000   
25%                         -4.619988  1986.620000     1.250000   
50%                          0.016122  2100.200000     1.500000   
75%                          6.237414  2439.900000     2.500000   
max                         21.222189  3305.210000     3.500000   

       last_month_total_month_rent_count  future_index  
count                        4261.000000   3896.000000  
mean                         4948.403661     72.756907  
std                          2094.932302     15.602975  
min                          2038.000000     55.360000  
25%                          3585.000000     58.787500  
50%                          4277.000000     68.335000  
75%                          5842.000000     89.090000  
max                         12374.000000    100.640000

In [ ]:
from sklearn.preprocessing import MinMaxScaler

# MinMaxScaler 객체 생성
scaler = MinMaxScaler(feature_range=(50, 100))

# 스케일링을 적용할 열 선택
columns_to_scale = ['area_deal', 'area_full_rent', 'area_year_rent', 'deal_year_rent_multiple', '12m_before_area_deal_mean', '12m_before_deal_full_rent_rate', 'kospi_index', 'korea_rp', 'last_month_total_month_rent_count']

# 선택한 열들에 대해 Min-Max Scaling 적용
df_train_test[columns_to_scale] = scaler.fit_transform(df_train_test[columns_to_scale].values)

# 결과 확인
display(df_train_test[columns_to_scale].describe())
display(df_train_test)

<ipython-input-26-e7d8295a530f>:10: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



area_deal  area_full_rent  area_year_rent  deal_year_rent_multiple  \
count  4261.000000     4261.000000     4261.000000              4261.000000   
mean     69.269651       74.414539       69.373917                69.912373   
std      18.043161       15.718914       14.998797                17.568713   
min      50.000000       50.000000       50.000000                50.000000   
25%      52.459928       60.001471       56.234078                52.548203   
50%      62.785867       74.502008       66.695648                62.838876   
75%      87.238373       90.320223       79.947429                86.826104   
max     100.000000      100.000000      100.000000               100.000000   

       12m_before_area_deal_mean  12m_before_deal_full_rent_rate  kospi_index  \
count                4261.000000                     4261.000000  4261.000000   
mean                   78.573029                       68.831993    71.387604   
std                    11.707810                       10.584544     9.590309   
min                    50.000000                       50.000000    50.000000   
25%                    70.426812                       60.064686    64.315560   
50%                    79.891604                       67.229118    67.389328   
75%                    87.714606                       76.843217    76.582484   
max                   100.000000                      100.000000   100.000000   

          korea_rp  last_month_total_month_rent_count  
count  4261.000000                        4261.000000  
mean     71.841508                          64.078965  
std      14.400901                          10.134154  
min      50.000000                          50.000000  
25%      62.500000                          57.483553  
50%      66.666667                          60.831076  
75%      83.333333                          68.401703  
max     100.000000                         100.000000

year  area_deal  area_full_rent  area_year_rent  \
0     2012  53.432096       50.651924       51.822954   
1     2012  53.415075       50.604965       51.751297   
2     2012  53.404403       50.762592       51.804259   
3     2012  53.419680       50.801057       51.807187   
4     2012  53.397650       50.715983       51.711746   
...    ...        ...             ...             ...   
4256  2023  94.759883       95.950706       99.590809   
4257  2023  94.749699       95.918403       99.716612   
4258  2023  94.785606       95.966964       99.899266   
4259  2023  94.786297       95.979758       99.894084   
4260  2023  94.795109       95.978363      100.000000   

      deal_year_rent_multiple  12m_before_area_deal_mean  \
0                   58.954066                  51.400743   
1                   58.988041                  51.358067   
2                   58.916140                  51.331311   
3                   58.944089                  51.369613   
4                   58.990646                  51.314380   
...                       ...                        ...   
4256                84.407566                  64.114870   
4257                84.291199                  64.099811   
4258                84.191349                  64.152906   
4259                84.196490                  64.153929   
4260                84.122425                  64.166958   

      12m_before_deal_full_rent_rate       date  kospi_index    korea_rp  \
0                          98.239411 2012-03-01    65.496301   95.833333   
1                          98.127594 2012-03-02    65.614835   95.833333   
2                          98.770571 2012-03-03    65.614835   95.833333   
3                          98.856712 2012-03-04    65.614835   95.833333   
4                          98.619604 2012-03-05    65.112283   95.833333   
...                              ...        ...          ...         ...   
4256                       68.630732 2023-10-26    72.771532  100.000000   
4257                       68.595103 2023-10-27    72.872476  100.000000   
4258                       68.612307 2023-10-28    72.872476  100.000000   
4259                       68.632314 2023-10-29    72.872476  100.000000   
4260                       68.614453 2023-10-30    73.081940  100.000000   

      last_month_total_month_rent_count future_date  future_index  
0                             52.902477  2013-03-01         56.00  
1                             52.902477  2013-03-02         56.00  
2                             52.902477  2013-03-03         55.99  
3                             52.902477  2013-03-04         55.99  
4                             52.902477  2013-03-05         55.98  
...                                 ...         ...           ...  
4256                          75.657895         NaT           NaN  
4257                          75.657895         NaT           NaN  
4258                          75.657895         NaT           NaN  
4259                          75.657895         NaT           NaN  
4260                          75.657895         NaT           NaN  

[4261 rows x 13 columns]

In [ ]:
# 학습할 때 입력을 할 feature들을 설정
train_columns = list(df_train_test.columns)

to_remove = ['future_index','date','year','future_date']
for x in to_remove:
    train_columns.remove(x)
train_columns


['area_deal',
 'area_full_rent',
 'area_year_rent',
 'deal_year_rent_multiple',
 '12m_before_area_deal_mean',
 '12m_before_deal_full_rent_rate',
 'kospi_index',
 'korea_rp',
 'last_month_total_month_rent_count']

In [ ]:
df_train = df_train_test.loc[df_train_test['year']<2022, :].copy()
df_test = df_train_test.loc[(df_train_test['year']>=2022)&(df_train_test['future_index'].notnull()), :].copy()

> 데이터크기를 조절한 데이터셋을 각 모델들에 적요을 시켜봤지만, 성능의 개선이 없었음

> 데이터 크기를 수정한다고 무조건 성능이 좋아지지는 않음

## 모델 혼합(앙상블)

- 시각적으로 확인을 했을 때, Gradient Boosting , XGBoost, Linear Regressor 순으로 모델의 성능이 좋은
- 더 좋은 모델을 만들기 위해서 Gradient Boosting 모델과 Linear Regressor 모델을 조합해서 앙상블 모델을 생성

#### 앙상블 임의 생성

- 앙상블 모델이 실제로 성능의 향상이 있는지 임의로 한개의 앙상블 모델을 생성해서 확인

In [ ]:
# Importing required libraries
import pandas as pd
from sklearn.linear_model import LinearRegression
from sklearn.ensemble import GradientBoostingRegressor
import xgboost as xgb
from sklearn.ensemble import VotingRegressor
from sklearn.model_selection import train_test_split
from sklearn.metrics import mean_squared_error
import numpy as np
import plotly.graph_objs as go

X_train = df_train[train_columns]
y_train = df_train['future_index']

X_test = df_test[train_columns]
y_test = df_test['future_index']

# Creating a Linear Regression model
lr_model = LinearRegression()

# Creating a Gradient Boosting model
gb_model = GradientBoostingRegressor(n_estimators=230, learning_rate=0.01, max_depth=5, random_state=0)

# Creating a XGBoosting model
xgb_model = xgb.XGBRegressor(objective ='reg:squarederror', n_estimators= 120, learning_rate=  0.1, max_depth = 4, random_state=0)

# VotingRegressor를 통해 앙상블 모델 생성
ensemble_model_1 = VotingRegressor([('lr', lr_model), ('gb', gb_model)], weights=[0.2, 0.8])




# Training the model on the training set
lr_model.fit(X_train, y_train)
lr_predict = lr_model.predict(X_test)
lr_mse = mean_squared_error(y_test ,lr_predict)

# Training the model on the training set
gb_model.fit(X_train, y_train)
gb_predict = gb_model.predict(X_test)
gb_mse = mean_squared_error(y_test ,gb_predict)

# Training the model on the training set
xgb_model.fit(X_train, y_train)
xgb_predict = xgb_model.predict(X_test)
xgb_mse = mean_squared_error(y_test ,xgb_predict)

# Training the model on the training set
ensemble_model_1.fit(X_train, y_train)
ensemble_1_predict = ensemble_model_1.predict(X_test)
ensemble_1_mse = mean_squared_error(y_test ,ensemble_1_predict)


# Creating the traces
trace1 = go.Scatter(
    x = df_test['future_date'],
    y = y_test.values,
    mode = 'lines',
    name = 'actual_value'
)


trace2 = go.Scatter(
    x = df_test['future_date'],
    y = list(lr_predict),
    mode = 'lines',
    name = 'lr_model predict_value'
)

trace3 = go.Scatter(
    x = df_test['future_date'],
    y = list(gb_predict),
    mode = 'lines',
    name = 'gb_model predict_value'
)

trace4 = go.Scatter(
    x = df_test['future_date'],
    y = list(xgb_predict),
    mode = 'lines',
    name = 'xgb_model predict_value'
)

trace5 = go.Scatter(
    x = df_test['future_date'],
    y = list(ensemble_1_predict),
    mode = 'lines',
    name = 'ensemble_model_1 predict_value'
)





# Combining the traces and creating the layout
data = [trace1, trace2, trace3, trace4,trace5]
layout = go.Layout(title='Variable Models Predict future price for total dataset', xaxis=dict(title='Date'), yaxis=dict(title='아파트지수'))

# Creating the figure and plotting it
fig = go.Figure(data=data, layout=layout)
fig.show()

print('LinearRegression Mean Squared Error:', lr_mse)
print('GradientBoostingRegressor Mean Squared Error:', gb_mse)
print('XGBRegressor Mean Squared Error:', xgb_mse)
print('Ensemble 1 Mean Squared Error:', ensemble_1_mse)

LinearRegression Mean Squared Error: 21.649886770747557
GradientBoostingRegressor Mean Squared Error: 1.1167184205462022
XGBRegressor Mean Squared Error: 1.2220096120066088
Ensemble 1 Mean Squared Error: 0.5584074793365612


> ensemble_1 모델은 2:8로 Linear Regressor 모델과 Gradient Boosting 모델을 조합

> 기존에는 Gradient Boosting 모델이 mse가 1.11로 가장 성능이 좋았지만, 앙상블 모델을 임의로 생성했는데 0.55로 성능이 더 좋아짐을 확인

> for문을 이용해 여러 경우의 앙상블 모델을 생성 해야 함

#### 최적 앙상블 모델 생성

- 3개의 모델의 조합을 구해야 함, 각 3개의 모델의 비중을 어떻게 조합할지 정하는 부분 구현

In [10]:
from sklearn.ensemble import VotingRegressor
from itertools import product



# List to store results
weights_list = []

# Define weight increments (10% increments)
weights = [i / 10.0 for i in range(11)]

# Generate all possible combinations of weights
weight_combinations = product(weights, repeat=3)

# Iterate through all combinations
for w_combination in weight_combinations:
    # Check if the weights sum to 1
    if sum(w_combination) == 1.0:


        # Perform your desired operations or evaluations here
        # For example, train the model and evaluate it on your data

        # Store the result (you can modify this based on your needs)
        weights_list.append(w_combination)

# Display the results
for weights in weights_list:
    print(weights)
    # Display more information from the result if needed
    print()


(0.0, 0.0, 1.0)

(0.0, 0.1, 0.9)

(0.0, 0.2, 0.8)

(0.0, 0.3, 0.7)

(0.0, 0.4, 0.6)

(0.0, 0.5, 0.5)

(0.0, 0.6, 0.4)

(0.0, 0.7, 0.3)

(0.0, 0.8, 0.2)

(0.0, 0.9, 0.1)

(0.0, 1.0, 0.0)

(0.1, 0.0, 0.9)

(0.1, 0.1, 0.8)

(0.1, 0.2, 0.7)

(0.1, 0.3, 0.6)

(0.1, 0.4, 0.5)

(0.1, 0.5, 0.4)

(0.1, 0.6, 0.3)

(0.1, 0.7, 0.2)

(0.1, 0.8, 0.1)

(0.1, 0.9, 0.0)

(0.2, 0.0, 0.8)

(0.2, 0.1, 0.7)

(0.2, 0.2, 0.6)

(0.2, 0.3, 0.5)

(0.2, 0.4, 0.4)

(0.2, 0.5, 0.3)

(0.2, 0.6, 0.2)

(0.2, 0.8, 0.0)

(0.3, 0.0, 0.7)

(0.3, 0.1, 0.6)

(0.3, 0.2, 0.5)

(0.3, 0.3, 0.4)

(0.3, 0.4, 0.3)

(0.3, 0.5, 0.2)

(0.3, 0.7, 0.0)

(0.4, 0.0, 0.6)

(0.4, 0.1, 0.5)

(0.4, 0.2, 0.4)

(0.4, 0.3, 0.3)

(0.4, 0.4, 0.2)

(0.4, 0.5, 0.1)

(0.4, 0.6, 0.0)

(0.5, 0.0, 0.5)

(0.5, 0.1, 0.4)

(0.5, 0.2, 0.3)

(0.5, 0.3, 0.2)

(0.5, 0.4, 0.1)

(0.5, 0.5, 0.0)

(0.6, 0.0, 0.4)

(0.6, 0.1, 0.3)

(0.6, 0.2, 0.2)

(0.6, 0.4, 0.0)

(0.7, 0.0, 0.3)

(0.7, 0.1, 0.2)

(0.7, 0.3, 0.0)

(0.8, 0.0, 0.2)

(0.8, 0.1, 0.1)

(0.8, 0.2, 0.0

In [11]:
# Importing required libraries
import pandas as pd
from sklearn.linear_model import LinearRegression
from sklearn.ensemble import GradientBoostingRegressor
import xgboost as xgb
from sklearn.ensemble import VotingRegressor
from sklearn.model_selection import train_test_split
from sklearn.metrics import mean_squared_error
import numpy as np
import plotly.graph_objs as go
from tqdm import tqdm
from sklearn.metrics import mean_absolute_error, r2_score

X_train = df_train[train_columns]
y_train = df_train['future_index']

X_test = df_test[train_columns]
y_test = df_test['future_index']

# Creating a Linear Regression model
lr_model = LinearRegression()

# Creating a Gradient Boosting model
gb_model = GradientBoostingRegressor(n_estimators=230, learning_rate=0.01, max_depth=5, random_state=0)

# Creating a XGBoosting model
xgb_model = xgb.XGBRegressor(objective ='reg:squarederror', n_estimators= 120, learning_rate=  0.1, max_depth = 4, random_state=0)


best_mse_score = np.inf
best_weights = 0

for weights in tqdm(weights_list):
  # VotingRegressor를 통해 앙상블 모델 생성
  ensemble_model = VotingRegressor(estimators=[('lr', lr_model),('gb', gb_model),('xgb', xgb_model)], weights= weights)
  # Training the model on the training set
  ensemble_model.fit(X_train, y_train)
  ensemble_predict = ensemble_model.predict(X_test)
  ensemble_mse = mean_squared_error(y_test ,ensemble_predict)

  if ensemble_mse < best_mse_score:
    best_mse_score = ensemble_mse
    best_weights = weights


# Training the model on the training set
gb_model.fit(X_train, y_train)
gb_predict = gb_model.predict(X_test)
gb_mse = mean_squared_error(y_test ,gb_predict)
print('GradientBoostingRegressor Mean Squared Error:', gb_mse)

print()

best_ensemble_model = VotingRegressor(estimators=[('lr', lr_model),('gb', gb_model),('xgb', xgb_model)], weights=  best_weights)
best_ensemble_model.fit(X_train, y_train)
best_ensemble_predict = best_ensemble_model.predict(X_test)

best_ensemble_mse = mean_squared_error(y_test ,best_ensemble_predict)
best_ensemble_mae = mean_absolute_error(y_test, best_ensemble_predict)
best_ensemble_r2 = r2_score(y_test, best_ensemble_predict)
best_ensemble_corr = np.corrcoef(y_test, best_ensemble_predict)[0, 1]

print('best Weights :', best_weights)
print('Best Ensemble Mean Squared Error:', best_ensemble_mse)
print('Best Ensemble Mean Absolute Error:', best_ensemble_mae)
print('Best Ensemble R-squared:', best_ensemble_r2)
print('Best Ensemble Pearson Correlation Coefficient:', best_ensemble_corr)
print()





# Creating the traces
trace1 = go.Scatter(
    x = df_test['future_date'],
    y = y_test.values,
    mode = 'lines',
    name = 'actual_value'
)

trace2 = go.Scatter(
    x = df_test['future_date'],
    y = list(gb_predict),
    mode = 'lines',
    name = 'gb_model predict_value'
)


trace3 = go.Scatter(
    x = df_test['future_date'],
    y = list(best_ensemble_predict),
    mode = 'lines',
    name = 'best_ensemble_model predict_value'
)







# Combining the traces and creating the layout
data = [trace1, trace2, trace3]
layout = go.Layout(title='Final Models Predict future price for total dataset', xaxis=dict(title='Date'), yaxis=dict(title='아파트지수'))

# Creating the figure and plotting it
fig = go.Figure(data=data, layout=layout)
fig.show()


100%|██████████| 62/62 [04:30<00:00,  4.36s/it]


GradientBoostingRegressor Mean Squared Error: 1.1167184205462022

best Weights : (0.1, 0.5, 0.4)
Best Ensemble Mean Squared Error: 0.44679675735094954
Best Ensemble Mean Absolute Error: 0.5561022859696734
Best Ensemble R-squared: 0.8012102664346892
Best Ensemble Pearson Correlation Coefficient: 0.9169610372958904



> Linear Regressor, Gradient Boosting, XGBoost 모델 중에서 가장 높은 성능을 보이는 모델들을 추출한 뒤, 1:5:4의 비중으로 조합

> 생성한 모델의 성능이 Mean Squared Error: 0.44 로 이전 Gradient Boosting 의 성능 Mean Squared Error: 1.11 보다 훨씬 좋아짐을 확인

> 예측한 값들이 최솟값이 90.31 이고, 최댓값이 95.71 인데 mse가 0.44임으로 모델의 성능이 좋다라고 판단(목표치는 mse 1 이하를 만족)

> mae는 0.55, R-squared 는 0.8, Pearson Correlation Coefficient 는 0.9 로 성능이 좋게 나옴을 확인

> https://medium.com/analytics-vidhya/mae-mse-rmse-coefficient-of-determination-adjusted-r-squared-which-metric-is-better-cd0326a5697e 참조

## 미래 아파트 가격지수 예측

- 결과값은 2023년 10월 30일 까지의 예측값 까지만을 가지고 있음으로, 2023년 10월 30일 이후의 예측값들을 생성한 모델을 적용하여서 도출

In [ ]:
df_test = df_train_test.loc[(df_train_test['year']>=2022), :].copy()
df_test['future_date'] = df_test['date'] + pd.Timedelta(days=365)
df_test

year    area_deal  area_full_rent  area_year_rent  \
3593  2022  1083.536621      606.893738       28.841393   
3594  2022  1083.647461      606.853333       28.839933   
3595  2022  1083.479614      607.364014       28.851576   
3596  2022  1083.489624      606.642090       28.877390   
3597  2022  1083.651611      607.107971       28.828796   
...    ...          ...             ...             ...   
4256  2023  1029.659058      596.442871       30.401781   
4257  2023  1029.540405      596.237915       30.427759   
4258  2023  1029.958740      596.546021       30.465477   
4259  2023  1029.966797      596.627197       30.464407   
4260  2023  1030.069458      596.618347       30.486279   

      deal_year_rent_multiple  12m_before_area_deal_mean  \
3593                37.568806                  13.972645   
3594                37.574547                  13.984303   
3595                37.553570                  13.966648   
3596                37.520344                  13.967700   
3597                37.589207                  13.984739   
...                       ...                        ...   
4256                33.868378                  -4.642175   
4257                33.835564                  -4.653163   
4258                33.807407                  -4.614421   
4259                33.808857                  -4.613675   
4260                33.787971                  -4.604167   

      12m_before_deal_full_rent_rate       date  kospi_index  korea_rp  \
3593                       -5.584571 2022-01-01      2977.65       1.0   
3594                       -5.600518 2022-01-02      2977.65       1.0   
3595                       -5.506430 2022-01-03      2988.77       1.0   
3596                       -5.619623 2022-01-04      2989.24       1.0   
3597                       -5.561261 2022-01-05      2953.97       1.0   
...                              ...        ...          ...       ...   
4256                        0.923108 2023-10-26      2299.08       3.5   
4257                        0.900052 2023-10-27      2302.81       3.5   
4258                        0.911185 2023-10-28      2302.81       3.5   
4259                        0.924131 2023-10-29      2302.81       3.5   
4260                        0.912574 2023-10-30      2310.55       3.5   

      last_month_total_month_rent_count future_date  future_index  
3593                            10052.0  2023-01-01         95.71  
3594                            10052.0  2023-01-02         95.67  
3595                            10052.0  2023-01-03         95.62  
3596                            10052.0  2023-01-04         95.56  
3597                            10052.0  2023-01-05         95.51  
...                                 ...         ...           ...  
4256                             7342.0  2024-10-25           NaN  
4257                             7342.0  2024-10-26           NaN  
4258                             7342.0  2024-10-27           NaN  
4259                             7342.0  2024-10-28           NaN  
4260                             7342.0  2024-10-29           NaN  

[668 rows x 13 columns]

In [ ]:
# Importing required libraries
import pandas as pd
from sklearn.linear_model import LinearRegression
from sklearn.ensemble import GradientBoostingRegressor
import xgboost as xgb
from sklearn.ensemble import VotingRegressor
from sklearn.model_selection import train_test_split
from sklearn.metrics import mean_squared_error
import numpy as np
import plotly.graph_objs as go
from tqdm import tqdm

X_train = df_train[train_columns]
y_train = df_train['future_index']

X_test = df_test[train_columns]

# Creating a Linear Regression model
lr_model = LinearRegression()

# Creating a Gradient Boosting model
gb_model = GradientBoostingRegressor(n_estimators=230, learning_rate=0.01, max_depth=5, random_state=0)

# Creating a XGBoosting model
xgb_model = xgb.XGBRegressor(objective ='reg:squarederror', n_estimators= 120, learning_rate=  0.1, max_depth = 4, random_state=0)




best_ensemble_model = VotingRegressor(estimators=[('lr', lr_model),('gb', gb_model),('xgb', xgb_model)], weights=  (0.1, 0.5, 0.4))
best_ensemble_model.fit(X_train, y_train)
best_ensemble_predict = best_ensemble_model.predict(X_test)




# Creating the traces
trace1 = go.Scatter(
    x = df_test['future_date'],
    y = y_test.values,
    mode = 'lines',
    name = 'actual_value'
)


trace2 = go.Scatter(
    x = df_test['future_date'],
    y = list(best_ensemble_predict),
    mode = 'lines',
    name = 'best_ensemble_model predict_value'
)





# Combining the traces and creating the layout
data = [trace1, trace2]
layout = go.Layout(title='Final Models Predict future price for total dataset', xaxis=dict(title='Date'), yaxis=dict(title='아파트지수'))

# Creating the figure and plotting it
fig = go.Figure(data=data, layout=layout)
fig.show()


> 최종적으로 만든 앙상블 모델로 '서울 아파트 매매가격지수'를 예측

> 파란선은 현재까지 나온 '서울 아파트 매매가격지수', 빨간선은 모델로 예측한 현재까지와 향후의 '서울 아파트 매매가격지수'

> 2022년 10월 30일까지는 1년 뒤 값인 2023년 10월 30일의 값 까지는 있지만,  2022년 10월 30일 이후의 값으로 예측한 2023년 10월 30일 이후의 '서울 아파트 매매가격지수'를 확인

> 2024년 10월까지는 지속적인 '서울 아파트 부동산'의 불황이 예상됨

# 결론

- 최종적으로 완성한 앙상블 모델이 가장 실제값과 상관관계가 높지만, 시각화를 한 결과 너무 직선으로 움직이는 부분이 있어 과연 신빙성이 있을까라는 의문
- 너무 테스트 성능을 높이기 위해서 과적합이 되었을 수 있기 때문에, 지속적인 모니터링을 통해 모델의 성능을 검증할 필요가 있음
- 과거에는 있었지만 현재는 없는 아파트들을 거르는 단계를 진행하지 않음. 그래서 데이터에 오류가 있었을 수도 있음

- 모델들 마다 정확한 수치들은 차이가 있지만, 실제 데이터와 비슷하게 움직이는 모델들을 적용시켰을 때, 2023년 말 까지는 서울 아파트 전체의 값들이 유지되거나 내려가는 추세임으로 현재 아파트를 매수하는 것은 추천하지 않는다

# 주의할 점&보완할 점

## 1. 주의할 점

- 데이터에 따라서 null 값 대신 ''로 값을 채워놓은 경우들이 있다, 데이터를 다루기 전에 빈 칸으로 처리되 부분이 있는지 확인이 필요하다
- 판다스에서 object 타입과 string 타입은 차이가 있기에 .str.replace() 등의 함수를 사용할때 str 타입으로 변경후에 사용을 해야 한다.
- 컬럼별로 계산을 할 때, 속성값에 0이나 null 값이 있는지 잘 확인을 하고 연산을 진행해야 한다
- 메모리 용량을 줄이기 위해서 데이터 타입을 변환할 수도 있다.
- 값들을 병합하거나 수정한 후, null 이나 inf 값들이 존재함을 확인해야 한다.
- stack() 함수를 사용할 때, null 값은 패스를 하기에, 계산 시 원하는 의도의 변경을 예방하기 위해서 null 값들을 치환할 수도 있다.
- pandas는 row 개수가 많은것이, column의 개수가 많은 것보다 더 메모리 부담이 크다
- info()를 사용해서 얻은 메모리 사용량과 memory_usage(deep=True)를 통해서 얻는 메모리 사용량은 다를 수 있다.(https://pythonspeed.com/articles/pandas-dataframe-series-memory-usage/ 참조)


## 2. 보완할 점

### 2-1. 프로젝트 시작 전

- 변수명이나 프로젝트 진행시에 쓰는 용어, 약속한 개념들을 확실히 정한 다음 진행을 해야지 프로젝트를 혼선 없이 진행할 수 있다.
- 데이터 분석을 진행 할 때, 최종 생성할 테이블과, 중간에 생성을 할 테이블들에 대한 구조들(스키마 테이블)을 미리 설계를 해놔야 추후 데이터들을 전처리하거나 생성할 때 더 효율적으로 일을 처리할 수 있음을 배움 -> 설계방법에 대한 학습 필요
- 데이터 시각화를 어떤 상황에 어느 시각 지표를 적용하면 좋을지 판단하는 능력의 향상이 필요
- 어느 지표들에 어떤 시각화를 사용할 지 미리 계획이 되어 있어야 한다.
- csv파일, pkl파일, mysql 데이터베이스 사용시의 차이점들 비교하여 학습할 필요
- 기계학습 모델을 사용하려면, 어떤 문제(분류, 회귀 등)에 어떤 모델을 적용할지 미리 설정하고 프로젝트를 진행해야 한다.

### 2-2. 프로젝트 진행 중

- 생각했던 가설이 참이 아닌 경우, 왜 참이 아니었는지 판단하고 검증하고 수정하는 능력이 필요함
- 주제목, 부제목, 설명들을 적으면서 진행을 해야 추후 정리를 할 때 수월하다




#### 2-2-1. 전처리 과정

- 판다스를 통해서 데이터를 전처리를 할 때, 함수를 활용하는 식 등의 메모리를 효율적으로 사용하는 식으로 코딩할 능력의 필요성을 느낌(메모리 부족으로 여러번에 나누어서 실행하면 번거롭고 원하는 결과와 다른 결과가 나올 수도 있음)
- 파이썬의 문법들을 활용해서 더 효율적인 함수를 만들 수 있는 능력이 필요
- 상황에 맞는 이상치를 제거하는 방법들에 대한 학습 필요
- 상황에 맞는 결측치를 채우는 방법들에 대한 학습 필요


#### 2-2-2. 분석 과정

- 기계학습 모델의 성능을 효과적으로 파악하기 위해서는, 그래프를 사용하는 것이  시각적으로 효용성이 있음
- 모델이 테스트 데이터셋를 통해서는 성능이 좋을 수는 있어도, 실제 미래의 값들은 다를 수 있음
- 각 모델의 동작과정을 알아야지, 어느 상황에서 어느 모델을 사용할 수 있는지 확인이 가능하고 파라미터 수정등이 용이할 듯
- 기계학습 등의 모델에서 하이퍼파라미터를 수정하는 것이 단순히 수정을 하면 되는 것인지 아니면 기준을 가지고 수정을 해야하는지 학습 필요

- 회귀 모델에서 오차의 허용 범위와 성능평가 방법을 어떻게 설정하는지가 모델의 성능의 큰 영향을 미치는듯 하다
- 회귀 모델의 경우 성능평가 방법들이 각각 어느정도 수치와 기준이 좋은 성능을 내는 것인지 파악을 할 줄 알아야 함
- 회귀모델을 통해서 정확한 값을 얻으려 노력하기 보다 추세를 보려고 노력하는 것이 더 맞는 방향이지 않을까? 하는 생각
- 선그래프를 통해 봤을 때는 추세적으로 비슷하게 움직이는 것 같았지만 실제 corr()을 통해서 확인했을 때는 그 수치가 크게 나오지 않을 수도 있다. -> 추세가 비슷하게 움직이는 다른 평가지표에 대한 조사 및 학습 필요





- 데이터 분석을 하기위해서 사용하는 방식으로 기계학습 모델 사용 뿐이 아닌, 데이터를 시각화를 통한 인사이트를 얻는 방법과 통계적 방법들을 통해 인사이트를 얻는 방법들에 대한 학습 필요

### 2-3. 프로젝트 종료 후

- 프로젝트를 보기 좋게 정리하는 법 및 설득력을 가질 수 있게 정리하는 법에 대한 학습 필요